In [ ]:
import websocket
import json
import time
import threading
import pandas as pd
import numpy as np
from deriv_api import DerivAPI
import asyncio

API_TOKEN = 'NF0aJKvNJ4IhKnZ'
APP_ID = 64724  # Replace with your app_id if you have one, or use the default 1089

class DerivAPI:
    def __init__(self):
        self.ws = None
        self.data = None
        self.subscribed = False

    def connect(self):
        websocket.enableTrace(True)
        self.ws = websocket.WebSocketApp(
            f"wss://ws.binaryws.com/websockets/v3?app_id={APP_ID}",
            on_message=self.on_message,
            on_error=self.on_error,
            on_close=self.on_close,
            on_open=self.on_open
        )
        wst = threading.Thread(target=self.ws.run_forever)
        wst.daemon = True
        wst.start()

        conn_timeout = 10
        while not self.ws.sock or not self.ws.sock.connected and conn_timeout:
            time.sleep(1)
            conn_timeout -= 1

        if not conn_timeout:
            print('Failed to connect to WebSocket')
            return False
        return True

    def on_message(self, ws, message):
        data = json.loads(message)
        if 'error' in data:
            print(f"Error: {data['error']['message']}")
        elif 'candles' in data:
            self.data = pd.DataFrame(data['candles'])
            self.data['time'] = pd.to_datetime(self.data['epoch'], unit='s')
            self.subscribed = True
        print(f"Received data: {data}")

    def on_error(self, ws, error):
        print(f"Error: {error}")

    def on_close(self, ws, close_status_code, close_msg):
        print("WebSocket connection closed")

    def on_open(self, ws):
        print("WebSocket connection opened")
        self.authorize()

    def authorize(self):
        self.ws.send(json.dumps({"authorize": API_TOKEN}))

    def get_candles(self, symbol, interval, count):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.subscribed = False
        self.ws.send(json.dumps({
            "ticks_history": symbol,
            "adjust_start_time": 1,
            "count": count,
            "end": "latest",
            "start": 1,
            "style": "candles",
            "granularity": interval
        }))

        timeout = 10
        while not self.subscribed and timeout:
            time.sleep(1)
            timeout -= 1

        if not self.subscribed:
            print("Failed to receive candle data")
            return None

        return self.data

async def execute_trade(api, signal):
    if signal == 'BUY':
        proposal = await api.proposal({"proposal": 1, "amount": 100, "barrier": "+0.1", "basis": "payout",
                                       "contract_type": "CALL", "currency": "USD", "duration": 60, 
                                       "duration_unit": "s", "symbol": "R_100"})
        proposal_id = proposal.get('proposal').get('id')
        buy = await api.buy({"buy": proposal_id, "price": 100})
        print("Executed BUY:", buy)

    elif signal == 'SELL':
        proposal = await api.proposal({"proposal": 1, "amount": 100, "barrier": "-0.1", "basis": "payout",
                                       "contract_type": "PUT", "currency": "USD", "duration": 60, 
                                       "duration_unit": "s", "symbol": "R_100"})
        proposal_id = proposal.get('proposal').get('id')
        buy = await api.buy({"buy": proposal_id, "price": 100})
        print("Executed SELL:", buy)

def calculate_indicators(df):
    # Calculate 9 and 25 period moving averages
    df['MA_9'] = df['close'].rolling(window=9).mean()
    df['MA_25'] = df['close'].rolling(window=25).mean()

    # Calculate RSI
    delta = df['close'].diff()
    gain = (delta.where(delta > 0, 0)).rolling(window=14).mean()
    loss = (-delta.where(delta < 0, 0)).rolling(window=14).mean()
    rs = gain / loss
    df['RSI'] = 100 - (100 / (1 + rs))

    # Calculate Stochastic Oscillator
    low_14 = df['low'].rolling(window=14).min()
    high_14 = df['high'].rolling(window=14).max()
    df['%K'] = (df['close'] - low_14) / (high_14 - low_14) * 100
    df['%D'] = df['%K'].rolling(window=3).mean()

    return dfa

def trading_strategy(df):
    last_row = df.iloc[-1]
    if last_row['MA_9'] > last_row['MA_25'] and last_row['RSI'] > 50 and last_row['%K'] > last_row['%D']:
        return 'BUY'
    elif last_row['MA_9'] < last_row['MA_25'] and last_row['RSI'] < 50 and last_row['%K'] < last_row['%D']:
        return 'SELL'
    else:
        return 'HOLD'

async def main():
    deriv_api = DerivAPI()
    if not deriv_api.connect():
        return

    symbol = 'R_100'  # Volatility 100 Index
    interval = 60  # 1-minute candles
    count = 100  # Number of candles to retrieve

    api = DerivAPI(app_id=APP_ID)
    await api.authorize(API_TOKEN)

    while True:
        candles = deriv_api.get_candles(symbol, interval, count)
        if candles is not None:
            df = calculate_indicators(candles)
            signal = trading_strategy(df)
            print(f"Current signal: {signal}")
            print(f"Latest close price: {df['close'].iloc[-1]}")
            print(f"Latest RSI: {df['RSI'].iloc[-1]:.2f}")
            print(f"Latest Stochastic %K: {df['%K'].iloc[-1]:.2f}")
            print(f"Latest Stochastic %D: {df['%D'].iloc[-1]:.2f}")
            
            if signal in ['BUY', 'SELL']:
                await execute_trade(api, signal)
        else:
            print("Failed to retrieve candle data")
        
        time.sleep(60)  # Wait for 1 minute before the next update

# Run the async function
await (main())


--- request header ---
2024-11-12 18:39:31,283 --- request header ---
GET /websockets/v3?app_id=64724 HTTP/1.1
Upgrade: websocket
Host: ws.binaryws.com
Origin: https://ws.binaryws.com
Sec-WebSocket-Key: qaEbGrULSGBsTyCoz4DoTQ==
Sec-WebSocket-Version: 13
Connection: Upgrade


2024-11-12 18:39:31,291 GET /websockets/v3?app_id=64724 HTTP/1.1
Upgrade: websocket
Host: ws.binaryws.com
Origin: https://ws.binaryws.com
Sec-WebSocket-Key: qaEbGrULSGBsTyCoz4DoTQ==
Sec-WebSocket-Version: 13
Connection: Upgrade


-----------------------
2024-11-12 18:39:31,293 -----------------------
--- response header ---
2024-11-12 18:39:31,294 --- response header ---
HTTP/1.1 101 Switching Protocols
2024-11-12 18:39:31,914 HTTP/1.1 101 Switching Protocols
Date: Tue, 12 Nov 2024 15:39:31 GMT
2024-11-12 18:39:31,915 Date: Tue, 12 Nov 2024 15:39:31 GMT
Content-Length: 0
2024-11-12 18:39:31,917 Content-Length: 0
Connection: upgrade
2024-11-12 18:39:31,918 Connection: upgrade
Content-Language: en
2024-11-12 18:39:31

WebSocket connection opened


TypeError: DerivAPI.__init__() got an unexpected keyword argument 'app_id'

++Rcv raw: b'\x81~\x05\xc1{"authorize":{"account_list":[{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1710220418,"currency":"USD","currency_type":"fiat","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR6779028"},{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1709901738,"currency":"BTC","currency_type":"crypto","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR6763883"},{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1721128861,"currency":"tUSDT","currency_type":"crypto","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR7371492"},{"account_category":"trading","account_type":"binary","broker":"VRTC","created_at":1709898717,"currency":"USD","currency_type":"fiat","is_disabled":0,"is_virtual":1,"landing_company_name":"virtual","linked_to":[],"loginid":"VRTC10086060"}],"balance

Received data: {'authorize': {'account_list': [{'account_category': 'trading', 'account_type': 'binary', 'broker': 'CR', 'created_at': 1710220418, 'currency': 'USD', 'currency_type': 'fiat', 'is_disabled': 0, 'is_virtual': 0, 'landing_company_name': 'svg', 'linked_to': [], 'loginid': 'CR6779028'}, {'account_category': 'trading', 'account_type': 'binary', 'broker': 'CR', 'created_at': 1709901738, 'currency': 'BTC', 'currency_type': 'crypto', 'is_disabled': 0, 'is_virtual': 0, 'landing_company_name': 'svg', 'linked_to': [], 'loginid': 'CR6763883'}, {'account_category': 'trading', 'account_type': 'binary', 'broker': 'CR', 'created_at': 1721128861, 'currency': 'tUSDT', 'currency_type': 'crypto', 'is_disabled': 0, 'is_virtual': 0, 'landing_company_name': 'svg', 'linked_to': [], 'loginid': 'CR7371492'}, {'account_category': 'trading', 'account_type': 'binary', 'broker': 'VRTC', 'created_at': 1709898717, 'currency': 'USD', 'currency_type': 'fiat', 'is_disabled': 0, 'is_virtual': 1, 'landing_c

Connection to remote host was lost. - goodbye
2024-11-12 18:41:12,393 Connection to remote host was lost. - goodbye


Error: Connection to remote host was lost.
WebSocket connection closed


In [ ]:
import websocket
import random
import json
import time
import threading
import pandas as pd
import numpy as np
from datetime import datetime
import asyncio
from deriv_api import DerivAPI  # Ensure this package is correctly installed or available

# Replace with your actual Deriv API key
API_TOKEN = 'NF0aJKvNJ4IhKnZ'
APP_ID = 64724  # Replace with your app_id if you have one, or use the default 1089

class DerivAPI:
    def __init__(self):
        self.ws = None
        self.data = None
        self.subscribed = False

    def connect(self, retries=3, delay=5):
        attempt = 0
        while attempt < retries:
            try:
                websocket.enableTrace(True)
                self.ws = websocket.WebSocketApp(
                    f"wss://ws.binaryws.com/websockets/v3?app_id={APP_ID}",
                    on_message=self.on_message,
                    on_error=self.on_error,
                    on_close=self.on_close,
                    on_open=self.on_open
                )
                wst = threading.Thread(target=self.ws.run_forever)
                wst.daemon = True
                wst.start()

                # Wait briefly to see if connection succeeds
                conn_timeout = 10
                while not self.ws.sock or not self.ws.sock.connected and conn_timeout:
                    time.sleep(1)
                    conn_timeout -= 1

                if self.ws.sock and self.ws.sock.connected:
                    print("Connected to WebSocket")
                    return True
            except Exception as e:
                print(f"Connection failed: {e}, retrying in {delay} seconds...")
                time.sleep(delay)
                attempt += 1

        print('Failed to connect to WebSocket after retries')
        return False

    def on_message(self, ws, message):
        data = json.loads(message)
        if 'error' in data:
            print(f"Error: {data['error']['message']}")
        elif 'candles' in data:
            self.data = pd.DataFrame(data['candles'])
            self.data['time'] = pd.to_datetime(self.data['epoch'], unit='s')
            self.subscribed = True
        print(f"Received data: {data}")

    def on_error(self, ws, error):
        print(f"Error: {error}")

    def on_close(self, ws, close_status_code, close_msg):
        print("WebSocket connection closed")

    def on_open(self, ws):
        print("WebSocket connection opened")
        self.authorize()

    def authorize(self):
        self.ws.send(json.dumps({"authorize": API_TOKEN}))
        
    def get_symbols(self):
        self.ws.send(json.dumps({"active_symbols": "brief"}))    

    def get_candles(self, symbol):
        self.subscribed = False
        self.ws.send(json.dumps({"candles": symbol}))
        timeout = 10
        while not self.subscribed and timeout:
            time.sleep(1)
            timeout -= 1
        return self.data if self.subscribed else None
    
def calculate_bid_ask_spread(candle_data):
    if 'ask' in candle_data and 'bid' in candle_data:
        spread = candle_data['ask'] - candle_data['bid']
        return spread
    return float('inf')    

def check_price_stability(df):
    if len(df) < 10:
        return False
    short_term_volatility = df['close'].pct_change().std()
    return short_term_volatility < 0.01

def select_symbol(api, symbols):
    liquid_symbols = []
    for symbol in symbols:
        candle_data = api.get_ticks(symbol['symbol'])
        if candle_data:
            spread = calculate_bid_ask_spread(candle_data)
            if spread < 0.5:
                candles = api.get_candles(symbol['symbol'], interval=60, count=10)
                if candles is not None and check_price_stability(candles):
                    liquid_symbols.append(symbol['symbol'])
    
    if liquid_symbols:
        return random.choice(liquid_symbols)
    return None

        self.subscribed = False
        self.ws.send(json.dumps({
            "ticks_history": symbol,
            "adjust_start_time": 1,
            "count": count,
            "end": "latest",
            "start": 1,
            "style": "candles",
            "granularity": interval
        }))

        timeout = 10
        while not self.subscribed and timeout:
            time.sleep(1)
            timeout -= 1

        if not self.subscribed:
            print("Failed to receive candle data")
            return None

        return self.data

def calculate_indicators(df):
    # Calculate 9 and 25 period moving averages
    df['MA_9'] = df['close'].rolling(window=9).mean()
    df['MA_25'] = df['close'].rolling(window=25).mean()

    # Calculate RSI
    delta = df['close'].diff()
    gain = (delta.where(delta > 0, 0)).rolling(window=14).mean()
    loss = (-delta.where(delta < 0, 0)).rolling(window=14).mean()
    rs = gain / loss
    df['RSI'] = 100 - (100 / (1 + rs))

    # Calculate Stochastic Oscillator
    low_14 = df['low'].rolling(window=14).min()
    high_14 = df['high'].rolling(window=14).max()
    df['%K'] = (df['close'] - low_14) / (high_14 - low_14) * 100
    df['%D'] = df['%K'].rolling(window=3).mean()

    return df

def trading_strategy(df):
    last_row = df.iloc[-1]
    if last_row['MA_9'] > last_row['MA_25'] and last_row['RSI'] > 50 and last_row['%K'] > last_row['%D']:
        return 'BUY'
    elif last_row['MA_9'] < last_row['MA_25'] and last_row['RSI'] < 50 and last_row['%K'] < last_row['%D']:
        return 'SELL'
    else:
        return 'HOLD'

async def execute_trade(api, signal):
    if signal == 'BUY':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "+0.1", "basis": "payout",
            "contract_type": "CALL", "currency": "USD", "duration": 60, "duration_unit": "s",
            "symbol": "R_100"
        })
    elif signal == 'SELL':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "-0.1", "basis": "payout",
            "contract_type": "PUT", "currency": "USD", "duration": 60, "duration_unit": "s",
            "symbol": "R_100"
        })
    else:
        return

    proposal_id = proposal.get('proposal').get('id')
    buy = await api.buy({"buy": proposal_id, "price": 100})
    print(f"Executed {signal} trade: {buy}")

async def main():
    deriv_api = DerivAPI()
    if not deriv_api.connect():
        return

    symbol = 'R_100'  # Volatility 100 Index
    interval = 60  # 1-minute candles
    count = 100  # Number of candles to retrieve

    while True:
        candles = deriv_api.get_candles(symbol, interval, count)
        if candles is not None:
            df = calculate_indicators(candles)
            signal = trading_strategy(df)
            print(f"Current signal: {signal}")
            print(f"Latest close price: {df['close'].iloc[-1]}")
            print(f"Latest RSI: {df['RSI'].iloc[-1]:.2f}")
            print(f"Latest Stochastic %K: {df['%K'].iloc[-1]:.2f}")
            print(f"Latest Stochastic %D: {df['%D'].iloc[-1]:.2f}")

            await execute_trade(deriv_api, signal)
        else:
            print("Failed to retrieve candle data")
        
        time.sleep(60)  # Wait for 1 minute before the next update

# Run the async main function
if __name__ == "__main__":
    await (main())


--- request header ---
2024-11-08 18:20:06,836 --- request header ---
GET /websockets/v3?app_id=64724 HTTP/1.1
Upgrade: websocket
Host: ws.binaryws.com
Origin: https://ws.binaryws.com
Sec-WebSocket-Key: Dlj8HJzkcXMOijTp8bn6Hg==
Sec-WebSocket-Version: 13
Connection: Upgrade


2024-11-08 18:20:06,840 GET /websockets/v3?app_id=64724 HTTP/1.1
Upgrade: websocket
Host: ws.binaryws.com
Origin: https://ws.binaryws.com
Sec-WebSocket-Key: Dlj8HJzkcXMOijTp8bn6Hg==
Sec-WebSocket-Version: 13
Connection: Upgrade


-----------------------
2024-11-08 18:20:06,843 -----------------------
--- response header ---
2024-11-08 18:20:06,844 --- response header ---
HTTP/1.1 101 Switching Protocols
2024-11-08 18:20:10,074 HTTP/1.1 101 Switching Protocols
Date: Fri, 08 Nov 2024 15:20:09 GMT
2024-11-08 18:20:10,076 Date: Fri, 08 Nov 2024 15:20:09 GMT
Content-Length: 0
2024-11-08 18:20:10,077 Content-Length: 0
Connection: upgrade
2024-11-08 18:20:10,079 Connection: upgrade
Upgrade: websocket
2024-11-08 18:20:10,0

WebSocket connection opened
Connected to WebSocket


++Rcv raw: b'\x81~\x05\xc1{"authorize":{"account_list":[{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1710220418,"currency":"USD","currency_type":"fiat","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR6779028"},{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1709901738,"currency":"BTC","currency_type":"crypto","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR6763883"},{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1721128861,"currency":"tUSDT","currency_type":"crypto","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR7371492"},{"account_category":"trading","account_type":"binary","broker":"VRTC","created_at":1709898717,"currency":"USD","currency_type":"fiat","is_disabled":0,"is_virtual":1,"landing_company_name":"virtual","linked_to":[],"loginid":"VRTC10086060"}],"balance

Received data: {'authorize': {'account_list': [{'account_category': 'trading', 'account_type': 'binary', 'broker': 'CR', 'created_at': 1710220418, 'currency': 'USD', 'currency_type': 'fiat', 'is_disabled': 0, 'is_virtual': 0, 'landing_company_name': 'svg', 'linked_to': [], 'loginid': 'CR6779028'}, {'account_category': 'trading', 'account_type': 'binary', 'broker': 'CR', 'created_at': 1709901738, 'currency': 'BTC', 'currency_type': 'crypto', 'is_disabled': 0, 'is_virtual': 0, 'landing_company_name': 'svg', 'linked_to': [], 'loginid': 'CR6763883'}, {'account_category': 'trading', 'account_type': 'binary', 'broker': 'CR', 'created_at': 1721128861, 'currency': 'tUSDT', 'currency_type': 'crypto', 'is_disabled': 0, 'is_virtual': 0, 'landing_company_name': 'svg', 'linked_to': [], 'loginid': 'CR7371492'}, {'account_category': 'trading', 'account_type': 'binary', 'broker': 'VRTC', 'created_at': 1709898717, 'currency': 'USD', 'currency_type': 'fiat', 'is_disabled': 0, 'is_virtual': 1, 'landing_c

AttributeError: 'DerivAPI' object has no attribute 'proposal'

Connection to remote host was lost. - goodbye
2024-11-08 18:21:53,838 Connection to remote host was lost. - goodbye


Error: Connection to remote host was lost.
WebSocket connection closed


In [ ]:
import websocket
import json
import time
import threading
import pandas as pd
import numpy as np
import asyncio

# Replace with your actual Deriv API key
API_TOKEN = 'NF0aJKvNJ4IhKnZ'
APP_ID = 64724  # Replace with your app_id if you have one, or use the default 1089

class DerivAPI:
    def __init__(self):
        self.ws = None
        self.data = None
        self.subscribed = False
        self.response = None  # To store proposal responses

    def connect(self, retries=3, delay=5):
        attempt = 0
        while attempt < retries:
            try:
                websocket.enableTrace(True)
                self.ws = websocket.WebSocketApp(
                    f"wss://ws.binaryws.com/websockets/v3?app_id={APP_ID}",
                    on_message=self.on_message,
                    on_error=self.on_error,
                    on_close=self.on_close,
                    on_open=self.on_open
                )
                wst = threading.Thread(target=self.ws.run_forever)
                wst.daemon = True
                wst.start()

                conn_timeout = 10
                while not self.ws.sock or not self.ws.sock.connected and conn_timeout:
                    time.sleep(1)
                    conn_timeout -= 1

                if self.ws.sock and self.ws.sock.connected:
                    print("Connected to WebSocket")
                    return True
            except Exception as e:
                print(f"Connection failed: {e}, retrying in {delay} seconds...")
                time.sleep(delay)
                attempt += 1

        print('Failed to connect to WebSocket after retries')
        return False

    def on_message(self, ws, message):
        data = json.loads(message)
        if 'error' in data:
            print(f"Error: {data['error']['message']}")
        elif 'candles' in data:
            self.data = pd.DataFrame(data['candles'])
            self.data['time'] = pd.to_datetime(self.data['epoch'], unit='s')
            self.subscribed = True
        elif 'proposal' in data:
            self.response = data['proposal']
        print(f"Received data: {data}")

    def on_error(self, ws, error):
        print(f"Error: {error}")

    def on_close(self, ws, close_status_code, close_msg):
        print("WebSocket connection closed")

    def on_open(self, ws):
        print("WebSocket connection opened")
        self.authorize()

    def authorize(self):
        self.ws.send(json.dumps({"authorize": API_TOKEN}))

    def get_candles(self, symbol, interval, count):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.subscribed = False
        self.ws.send(json.dumps({
            "ticks_history": symbol,
            "adjust_start_time": 1,
            "count": count,
            "end": "latest",
            "start": 1,
            "style": "candles",
            "granularity": interval
        }))

        timeout = 10
        while not self.subscribed and timeout:
            time.sleep(1)
            timeout -= 1

        if not self.subscribed:
            print("Failed to receive candle data")
            return None

        return self.data

    async def proposal(self, proposal_params):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.response = None
        self.ws.send(json.dumps(proposal_params))

        timeout = 10
        while not self.response and timeout:
            await asyncio.sleep(1)
            timeout -= 1

        if not self.response:
            print("Failed to receive proposal response")
            return None

        return self.response

def calculate_indicators(df):
    df['MA_9'] = df['close'].rolling(window=9).mean()
    df['MA_25'] = df['close'].rolling(window=25).mean()

    delta = df['close'].diff()
    gain = (delta.where(delta > 0, 0)).rolling(window=14).mean()
    loss = (-delta.where(delta < 0, 0)).rolling(window=14).mean()
    rs = gain / loss
    df['RSI'] = 100 - (100 / (1 + rs))

    low_14 = df['low'].rolling(window=14).min()
    high_14 = df['high'].rolling(window=14).max()
    df['%K'] = (df['close'] - low_14) / (high_14 - low_14) * 100
    df['%D'] = df['%K'].rolling(window=3).mean()

    return df

def trading_strategy(df):
    last_row = df.iloc[-1]
    if last_row['MA_9'] > last_row['MA_25'] and last_row['RSI'] > 50 and last_row['%K'] > last_row['%D']:
        return 'BUY'
    elif last_row['MA_9'] < last_row['MA_25'] and last_row['RSI'] < 50 and last_row['%K'] < last_row['%D']:
        return 'SELL'
    else:
        return 'HOLD'

async def execute_trade(api, signal):
    if signal == 'BUY':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "+0.1", "basis": "payout",
            "contract_type": "CALL", "currency": "USD", "duration": 60, "duration_unit": "s",
            "symbol": "R_100"
        })
    elif signal == 'SELL':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "-0.1", "basis": "payout",
            "contract_type": "PUT", "currency": "USD", "duration": 60, "duration_unit": "s",
            "symbol": "R_100"
        })
    else:
        return

    if proposal and 'id' in proposal:
        proposal_id = proposal['id']
        api.ws.send(json.dumps({"buy": proposal_id, "price": 100}))
        print(f"Executed {signal} trade with proposal ID: {proposal_id}")
    else:
        print(f"Failed to execute {signal} trade")

async def main():
    deriv_api = DerivAPI()
    if not deriv_api.connect():
        return

    symbol = 'R_100'
    interval = 60
    count = 100

    while True:
        candles = deriv_api.get_candles(symbol, interval, count)
        if candles is not None:
            df = calculate_indicators(candles)
            signal = trading_strategy(df)
            print(f"Current signal: {signal}")

            await execute_trade(deriv_api, signal)
        else:
            print("Failed to retrieve candle data")
        
        time.sleep(60)

if __name__ == "__main__":
    await (main())


--- request header ---
GET /websockets/v3?app_id=64724 HTTP/1.1
Upgrade: websocket
Host: ws.binaryws.com
Origin: https://ws.binaryws.com
Sec-WebSocket-Key: aGRnnM3JfBHgQea3nONUbQ==
Sec-WebSocket-Version: 13
Connection: Upgrade


-----------------------
--- response header ---
HTTP/1.1 101 Switching Protocols
Date: Mon, 11 Nov 2024 15:08:22 GMT
Content-Length: 0
Connection: upgrade
Upgrade: websocket
Content-Language: en
Sec-WebSocket-Accept: E0UVmMNG4Ft/dCy4SPXRTmtp3NQ=
CF-Cache-Status: DYNAMIC
Server: cloudflare
CF-RAY: 8e0f327e6ed165e6-MBA
alt-svc: h3=":443"; ma=86400
-----------------------
Websocket connected
++Sent raw: b'\x81\xa0\xadm\xbf3\xd6O\xdeF\xd9\x05\xd0A\xc4\x17\xda\x11\x97M\x9d}\xeb]\xdey\xe6\x1b\xf1y\x99$\xd7x\xc37\x9dN'
++Sent decoded: fin=1 opcode=1 data=b'{"authorize": "NF0aJKvNJ4IhKnZ"}'
++Sent raw: b'\x81\xfe\x00\x84J\x13X\x0111,h)x+^"z+u%a!#p3zS\x15"h1h?x#+w2t9g\x07r>r*u\x15g1l/1b!{?x#)|-o>1b!{#h-j1=o.1b!h\x7f9u/`,#f3zr>r*uh)x0f3zr>j4dh)x#)r6e&v+#f3zf8r6t&r*h>jz;j

WebSocket connection opened
Connected to WebSocket


++Rcv raw: b'\x81~ \x15{"candles":[{"close":1038.73,"epoch":1731331740,"high":1042.45,"low":1038.73,"open":1042.27},{"close":1038.25,"epoch":1731331800,"high":1039.56,"low":1038.17,"open":1038.73},{"close":1040.42,"epoch":1731331860,"high":1040.46,"low":1037.7,"open":1038.51},{"close":1040.68,"epoch":1731331920,"high":1040.68,"low":1039.07,"open":1040.33},{"close":1040.35,"epoch":1731331980,"high":1040.81,"low":1039.29,"open":1040.27},{"close":1041.36,"epoch":1731332040,"high":1041.36,"low":1039.75,"open":1040.22},{"close":1041.73,"epoch":1731332100,"high":1042.38,"low":1040.48,"open":1041.51},{"close":1041.36,"epoch":1731332160,"high":1041.9,"low":1040.15,"open":1041.6},{"close":1043.1,"epoch":1731332220,"high":1043.6,"low":1041.8,"open":1041.9},{"close":1042.66,"epoch":1731332280,"high":1042.89,"low":1041.7,"open":1042.68},{"close":1043,"epoch":1731332340,"high":1043.2,"low":1042.5,"open":1042.64},{"close":1043.15,"epoch":1731332400,"high":1043.27,"low":1042.06,"open":1043.27},{"clos

Received data: {'candles': [{'close': 1038.73, 'epoch': 1731331740, 'high': 1042.45, 'low': 1038.73, 'open': 1042.27}, {'close': 1038.25, 'epoch': 1731331800, 'high': 1039.56, 'low': 1038.17, 'open': 1038.73}, {'close': 1040.42, 'epoch': 1731331860, 'high': 1040.46, 'low': 1037.7, 'open': 1038.51}, {'close': 1040.68, 'epoch': 1731331920, 'high': 1040.68, 'low': 1039.07, 'open': 1040.33}, {'close': 1040.35, 'epoch': 1731331980, 'high': 1040.81, 'low': 1039.29, 'open': 1040.27}, {'close': 1041.36, 'epoch': 1731332040, 'high': 1041.36, 'low': 1039.75, 'open': 1040.22}, {'close': 1041.73, 'epoch': 1731332100, 'high': 1042.38, 'low': 1040.48, 'open': 1041.51}, {'close': 1041.36, 'epoch': 1731332160, 'high': 1041.9, 'low': 1040.15, 'open': 1041.6}, {'close': 1043.1, 'epoch': 1731332220, 'high': 1043.6, 'low': 1041.8, 'open': 1041.9}, {'close': 1042.66, 'epoch': 1731332280, 'high': 1042.89, 'low': 1041.7, 'open': 1042.68}, {'close': 1043, 'epoch': 1731332340, 'high': 1043.2, 'low': 1042.5, 'o

++Sent raw: b'\x81\xfe\x00\xa8\x87\x91s\x8f\xfc\xb3\x03\xfd\xe8\xe1\x1c\xfc\xe6\xfdQ\xb5\xa7\xa0_\xaf\xa5\xf0\x1e\xe0\xf2\xff\x07\xad\xbd\xb1B\xbf\xb7\xbdS\xad\xe5\xf0\x01\xfd\xee\xf4\x01\xad\xbd\xb1Q\xa2\xb7\xbfB\xad\xab\xb1Q\xed\xe6\xe2\x1a\xfc\xa5\xabS\xad\xf7\xf0\n\xe0\xf2\xe5Q\xa3\xa7\xb3\x10\xe0\xe9\xe5\x01\xee\xe4\xe5,\xfb\xfe\xe1\x16\xad\xbd\xb1Q\xdf\xd2\xc5Q\xa3\xa7\xb3\x10\xfa\xf5\xe3\x16\xe1\xe4\xe8Q\xb5\xa7\xb3&\xdc\xc3\xb3_\xaf\xa5\xf5\x06\xfd\xe6\xe5\x1a\xe0\xe9\xb3I\xaf\xb1\xa1_\xaf\xa5\xf5\x06\xfd\xe6\xe5\x1a\xe0\xe9\xce\x06\xe1\xee\xe5Q\xb5\xa7\xb3\x00\xad\xab\xb1Q\xfc\xfe\xfc\x11\xe0\xeb\xb3I\xaf\xa5\xc3,\xbe\xb7\xa1Q\xf2'
++Sent decoded: fin=1 opcode=1 data=b'{"proposal": 1, "amount": 100, "barrier": "-0.1", "basis": "payout", "contract_type": "PUT", "currency": "USD", "duration": 60, "duration_unit": "s", "symbol": "R_100"}'


...

Received data: {'echo_req': {'amount': 100, 'barrier': '-0.1', 'basis': 'payout', 'contract_type': 'PUT', 'currency': 'USD', 'duration': 60, 'duration_unit': 's', 'product_type': 'basic', 'proposal': 1, 'symbol': 'R_100'}, 'msg_type': 'proposal', 'proposal': {'ask_price': 48.35, 'contract_details': {'barrier': '1020.02'}, 'date_expiry': 1731337763, 'date_start': 1731337703, 'display_value': '48.35', 'id': 'b4c7b3fa-b400-9232-ee67-6208fa4500d5', 'longcode': 'Win payout if Volatility 100 Index is strictly lower than entry spot minus 0.10 at 1 minute after contract start time.', 'payout': 100, 'spot': 1020.12, 'spot_time': 1731337702, 'validation_params': {'payout': {'max': '50000.00'}, 'stake': {'min': '0.35'}}}}


++Sent raw: b'\x81\xbd;\xe8]\xc2@\xca?\xb7B\xcag\xe2\x19\x8ai\xa1\x0c\x8an\xa4Z\xc5?\xf6\x0b\xd8p\xfb\t\xdbo\xef^\x8dk\xf5\x16\xdeo\xf2\x03\x8e<\xf6\x0e\xd8m\xa6\x0e\xcaq\xe2\x19\x98/\xabX\x8d\x7f\xf8\x1b\xd9m\xf2F'
++Sent decoded: fin=1 opcode=1 data=b'{"buy": "b4c7b3fa-b400-9232-ee67-6208fa4500d5", "price": 100}'


Executed SELL trade with proposal ID: b4c7b3fa-b400-9232-ee67-6208fa4500d5


++Rcv raw: b'\x81~\x01\xc4{"buy":{"balance_after":9871.99,"buy_price":48.35,"contract_id":262714096728,"longcode":"Win payout if Volatility 100 Index is strictly lower than entry spot minus 0.10 at 1 minute after contract start time.","payout":100,"purchase_time":1731337705,"shortcode":"PUT_R_100_100.00_1731337705_1731337765_S-10P_0","start_time":1731337705,"transaction_id":523742075228},"echo_req":{"buy":"b4c7b3fa-b400-9232-ee67-6208fa4500d5","price":100},"msg_type":"buy"}'
++Rcv decoded: fin=1 opcode=1 data=b'{"buy":{"balance_after":9871.99,"buy_price":48.35,"contract_id":262714096728,"longcode":"Win payout if Volatility 100 Index is strictly lower than entry spot minus 0.10 at 1 minute after contract start time.","payout":100,"purchase_time":1731337705,"shortcode":"PUT_R_100_100.00_1731337705_1731337765_S-10P_0","start_time":1731337705,"transaction_id":523742075228},"echo_req":{"buy":"b4c7b3fa-b400-9232-ee67-6208fa4500d5","price":100},"msg_type":"buy"}'


Received data: {'buy': {'balance_after': 9871.99, 'buy_price': 48.35, 'contract_id': 262714096728, 'longcode': 'Win payout if Volatility 100 Index is strictly lower than entry spot minus 0.10 at 1 minute after contract start time.', 'payout': 100, 'purchase_time': 1731337705, 'shortcode': 'PUT_R_100_100.00_1731337705_1731337765_S-10P_0', 'start_time': 1731337705, 'transaction_id': 523742075228}, 'echo_req': {'buy': 'b4c7b3fa-b400-9232-ee67-6208fa4500d5', 'price': 100}, 'msg_type': 'buy'}


In [ ]:
import websocket
import json
import time
import threading
import pandas as pd
import numpy as np
import asyncio

API_TOKEN = 'NF0aJKvNJ4IhKnZ'
APP_ID = 64724

class DerivAPI:
    def __init__(self):
        self.ws = None
        self.data = None
        self.subscribed = False
        self.response = None

    def connect(self, retries=3, delay=5):
        attempt = 0
        while attempt < retries:
            try:
                websocket.enableTrace(True)
                self.ws = websocket.WebSocketApp(
                    f"wss://ws.binaryws.com/websockets/v3?app_id={APP_ID}",
                    on_message=self.on_message,
                    on_error=self.on_error,
                    on_close=self.on_close,
                    on_open=self.on_open
                )
                wst = threading.Thread(target=self.ws.run_forever)
                wst.daemon = True
                wst.start()

                conn_timeout = 10
                while not self.ws.sock or not self.ws.sock.connected and conn_timeout:
                    time.sleep(1)
                    conn_timeout -= 1

                if self.ws.sock and self.ws.sock.connected:
                    print("Connected to WebSocket")
                    return True
            except Exception as e:
                print(f"Connection failed: {e}, retrying in {delay} seconds...")
                time.sleep(delay)
                attempt += 1

        print('Failed to connect to WebSocket after retries')
        return False

    def on_message(self, ws, message):
        data = json.loads(message)
        if 'error' in data:
            print(f"Error: {data['error']['message']}")
        elif 'candles' in data:
            self.data = pd.DataFrame(data['candles'])
            self.data['time'] = pd.to_datetime(self.data['epoch'], unit='s')
            self.subscribed = True
        elif 'proposal' in data:
            self.response = data['proposal']
        elif 'active_symbols' in data:
            print("Active Symbols:")
            for symbol in data['active_symbols']:
                print(symbol['symbol'], "-", symbol['display_name'])
        print(f"Received data: {data}")

    def on_error(self, ws, error):
        print(f"Error: {error}")

    def on_close(self, ws, close_status_code, close_msg):
        print("WebSocket connection closed")

    def on_open(self, ws):
        print("WebSocket connection opened")
        self.authorize()

    def authorize(self):
        self.ws.send(json.dumps({"authorize": API_TOKEN}))

    def get_candles(self, symbol, interval, count):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.subscribed = False
        self.ws.send(json.dumps({
            "ticks_history": symbol,
            "adjust_start_time": 1,
            "count": count,
            "end": "latest",
            "start": 1,
            "style": "candles",
            "granularity": interval
        }))

        timeout = 10
        while not self.subscribed and timeout:
            time.sleep(1)
            timeout -= 1

        if not self.subscribed:
            print("Failed to receive candle data")
            return None

        return self.data

    async def get_active_symbols(self):
        if not self.ws:
            print("WebSocket is not connected")
            return

        self.ws.send(json.dumps({
            "active_symbols": "full"
        }))

    async def proposal(self, proposal_params):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.response = None
        self.ws.send(json.dumps(proposal_params))

        timeout = 10
        while not self.response and timeout:
            await asyncio.sleep(1)
            timeout -= 1

        if not self.response:
            print("Failed to receive proposal response")
            return None

        return self.response

def calculate_indicators(df):
    df['MA_9'] = df['close'].rolling(window=9).mean()
    df['MA_25'] = df['close'].rolling(window=25).mean()

    delta = df['close'].diff()
    gain = (delta.where(delta > 0, 0)).rolling(window=14).mean()
    loss = (-delta.where(delta < 0, 0)).rolling(window=14).mean()
    rs = gain / loss
    df['RSI'] = 100 - (100 / (1 + rs))

    low_14 = df['low'].rolling(window=14).min()
    high_14 = df['high'].rolling(window=14).max()
    df['%K'] = (df['close'] - low_14) / (high_14 - low_14) * 100
    df['%D'] = df['%K'].rolling(window=3).mean()

    return df

def trading_strategy(df):
    last_row = df.iloc[-1]
    if last_row['MA_9'] > last_row['MA_25'] and last_row['RSI'] > 50 and last_row['%K'] > last_row['%D']:
        return 'BUY'
    elif last_row['MA_9'] < last_row['MA_25'] and last_row['RSI'] < 50 and last_row['%K'] < last_row['%D']:
        return 'SELL'
    else:
        return 'HOLD'

async def execute_trade(api, signal):
    if signal == 'BUY':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "+0.1", "basis": "payout",
            "contract_type": "CALL", "currency": "USD", "duration": 60, "duration_unit": "s",
            "symbol": "R_100"
        })
    elif signal == 'SELL':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "-0.1", "basis": "payout",
            "contract_type": "PUT", "currency": "USD", "duration": 60, "duration_unit": "s",
            "symbol": "R_100"
        })
    else:
        return

    if proposal and 'id' in proposal:
        proposal_id = proposal['id']
        api.ws.send(json.dumps({"buy": proposal_id, "price": 100}))
        print(f"Executed {signal} trade with proposal ID: {proposal_id}")
    else:
        print(f"Failed to execute {signal} trade")

async def main():
    deriv_api = DerivAPI()
    if not deriv_api.connect():
        return

    await deriv_api.get_active_symbols()  # Fetch and print all active symbols

    symbol = 'R_100'
    interval = 60
    count = 100

    while True:
        candles = deriv_api.get_candles(symbol, interval, count)
        if candles is not None:
            df = calculate_indicators(candles)
            signal = trading_strategy(df)
            print(f"Current signal: {signal}")

            await execute_trade(deriv_api, signal)
        else:
            print("Failed to retrieve candle data")
        
        time.sleep(60)

if __name__ == "__main__":
    await (main())


--- request header ---
GET /websockets/v3?app_id=64724 HTTP/1.1
Upgrade: websocket
Host: ws.binaryws.com
Origin: https://ws.binaryws.com
Sec-WebSocket-Key: HtN+fXqA4YjwFgHnkR9L9Q==
Sec-WebSocket-Version: 13
Connection: Upgrade


-----------------------
--- response header ---
HTTP/1.1 101 Switching Protocols
Date: Mon, 11 Nov 2024 15:15:07 GMT
Content-Length: 0
Connection: upgrade
Content-Language: en
Upgrade: websocket
Sec-WebSocket-Accept: e5ET0OEAoCGBcp3WlG7woup2mFI=
CF-Cache-Status: DYNAMIC
Server: cloudflare
CF-RAY: 8e0f3c5eac8865e5-MBA
alt-svc: h3=":443"; ma=86400
-----------------------
Websocket connected
++Sent raw: b"\x81\xa0\x9ac\xb6Z\xe1A\xd7/\xee\x0b\xd9(\xf3\x19\xd3x\xa0C\x94\x14\xdcS\xd7\x10\xd1\x15\xf8\x10\xae*\xde\x11\xf49\x94'"
++Sent decoded: fin=1 opcode=1 data=b'{"authorize": "NF0aJKvNJ4IhKnZ"}'


WebSocket connection opened


++Rcv raw: b'\x81~\x05\xc2{"authorize":{"account_list":[{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1710220418,"currency":"USD","currency_type":"fiat","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR6779028"},{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1709901738,"currency":"BTC","currency_type":"crypto","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR6763883"},{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1721128861,"currency":"tUSDT","currency_type":"crypto","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR7371492"},{"account_category":"trading","account_type":"binary","broker":"VRTC","created_at":1709898717,"currency":"USD","currency_type":"fiat","is_disabled":0,"is_virtual":1,"landing_company_name":"virtual","linked_to":[],"loginid":"VRTC10086060"}],"balance

Received data: {'authorize': {'account_list': [{'account_category': 'trading', 'account_type': 'binary', 'broker': 'CR', 'created_at': 1710220418, 'currency': 'USD', 'currency_type': 'fiat', 'is_disabled': 0, 'is_virtual': 0, 'landing_company_name': 'svg', 'linked_to': [], 'loginid': 'CR6779028'}, {'account_category': 'trading', 'account_type': 'binary', 'broker': 'CR', 'created_at': 1709901738, 'currency': 'BTC', 'currency_type': 'crypto', 'is_disabled': 0, 'is_virtual': 0, 'landing_company_name': 'svg', 'linked_to': [], 'loginid': 'CR6763883'}, {'account_category': 'trading', 'account_type': 'binary', 'broker': 'CR', 'created_at': 1721128861, 'currency': 'tUSDT', 'currency_type': 'crypto', 'is_disabled': 0, 'is_virtual': 0, 'landing_company_name': 'svg', 'linked_to': [], 'loginid': 'CR7371492'}, {'account_category': 'trading', 'account_type': 'binary', 'broker': 'VRTC', 'created_at': 1709898717, 'currency': 'USD', 'currency_type': 'fiat', 'is_disabled': 0, 'is_virtual': 1, 'landing_c

++Sent raw: b'\x81\x9a\xb82\x1bM\xc3\x10z.\xcc[m(\xe7Ab \xda]w>\x9a\x08;o\xdeGw!\x9aO'
++Sent decoded: fin=1 opcode=1 data=b'{"active_symbols": "full"}'
++Sent raw: b'\x81\xfe\x00\x84J\x92\x92\xcc1\xb0\xe6\xa5)\xf9\xe1\x93"\xfb\xe1\xb8%\xe0\xeb\xeep\xb2\xb0\x9e\x15\xa3\xa2\xfch\xbe\xb2\xee+\xf6\xf8\xb99\xe6\xcd\xbf>\xf3\xe0\xb8\x15\xe6\xfb\xa1/\xb0\xa8\xec{\xbe\xb2\xee)\xfd\xe7\xa2>\xb0\xa8\xec{\xa2\xa2\xe0j\xb0\xf7\xa2.\xb0\xa8\xech\xfe\xf3\xb8/\xe1\xe6\xeef\xb2\xb0\xbf>\xf3\xe0\xb8h\xa8\xb2\xfdf\xb2\xb0\xbf>\xeb\xfe\xa9h\xa8\xb2\xee)\xf3\xfc\xa8&\xf7\xe1\xeef\xb2\xb0\xab8\xf3\xfc\xb9&\xf3\xe0\xa5>\xeb\xb0\xf6j\xa4\xa2\xb1'
++Sent decoded: fin=1 opcode=1 data=b'{"ticks_history": "R_100", "adjust_start_time": 1, "count": 100, "end": "latest", "start": 1, "style": "candles", "granularity": 60}'


...

++Sent raw: b'\x81\xfe\x00\xa8\xb50\xde\x1b\xce\x12\xaei\xda@\xb1h\xd4\\\xfc!\x95\x01\xf2;\x97Q\xb3t\xc0^\xaa9\x8f\x10\xef+\x85\x1c\xfe9\xd7Q\xaci\xdcU\xac9\x8f\x10\xfc6\x85\x1e\xef9\x99\x10\xfcy\xd4C\xb7h\x97\n\xfe9\xc5Q\xa7t\xc0D\xfc7\x95\x12\xbdt\xdbD\xacz\xd6D\x81o\xcc@\xbb9\x8f\x10\xfcK\xe0d\xfc7\x95\x12\xbdn\xc7B\xbbu\xd6I\xfc!\x95\x12\x8bH\xf1\x12\xf2;\x97T\xabi\xd4D\xb7t\xdb\x12\xe4;\x83\x00\xf2;\x97T\xabi\xd4D\xb7t\xdbo\xabu\xdcD\xfc!\x95\x12\xad9\x99\x10\xfch\xcc]\xbct\xd9\x12\xe4;\x97b\x81*\x85\x00\xfcf'
++Sent decoded: fin=1 opcode=1 data=b'{"proposal": 1, "amount": 100, "barrier": "-0.1", "basis": "payout", "contract_type": "PUT", "currency": "USD", "duration": 60, "duration_unit": "s", "symbol": "R_100"}'


Current signal: SELL


++Rcv raw: b'\x81~\x02\x8e{"echo_req":{"amount":100,"barrier":"-0.1","basis":"payout","contract_type":"PUT","currency":"USD","duration":60,"duration_unit":"s","product_type":"basic","proposal":1,"symbol":"R_100"},"msg_type":"proposal","proposal":{"ask_price":48.35,"contract_details":{"barrier":"1021.59"},"date_expiry":1731338353,"date_start":1731338293,"display_value":"48.35","id":"25b61784-2868-cd08-a291-3317b50e2277","longcode":"Win payout if Volatility 100 Index is strictly lower than entry spot minus 0.10 at 1 minute after contract start time.","payout":100,"spot":1021.69,"spot_time":1731338292,"validation_params":{"payout":{"max":"50000.00"},"stake":{"min":"0.35"}}}}'
++Rcv decoded: fin=1 opcode=1 data=b'{"echo_req":{"amount":100,"barrier":"-0.1","basis":"payout","contract_type":"PUT","currency":"USD","duration":60,"duration_unit":"s","product_type":"basic","proposal":1,"symbol":"R_100"},"msg_type":"proposal","proposal":{"ask_price":48.35,"contract_details":{"barrier":"1021.59"},"

Received data: {'echo_req': {'amount': 100, 'barrier': '-0.1', 'basis': 'payout', 'contract_type': 'PUT', 'currency': 'USD', 'duration': 60, 'duration_unit': 's', 'product_type': 'basic', 'proposal': 1, 'symbol': 'R_100'}, 'msg_type': 'proposal', 'proposal': {'ask_price': 48.35, 'contract_details': {'barrier': '1021.59'}, 'date_expiry': 1731338353, 'date_start': 1731338293, 'display_value': '48.35', 'id': '25b61784-2868-cd08-a291-3317b50e2277', 'longcode': 'Win payout if Volatility 100 Index is strictly lower than entry spot minus 0.10 at 1 minute after contract start time.', 'payout': 100, 'spot': 1021.69, 'spot_time': 1731338292, 'validation_params': {'payout': {'max': '50000.00'}, 'stake': {'min': '0.35'}}}}


CancelledError: 

In [ ]:
import websocket
import json
import time
import threading
import pandas as pd
import numpy as np
import asyncio

API_TOKEN = 'NF0aJKvNJ4IhKnZ'
APP_ID = 64724

class DerivAPI:
    def __init__(self):
        self.ws = None
        self.data = None
        self.subscribed = False
        self.response = None

    def connect(self, retries=3, delay=5):
        attempt = 0
        while attempt < retries:
            try:
                websocket.enableTrace(True)
                self.ws = websocket.WebSocketApp(
                    f"wss://ws.binaryws.com/websockets/v3?app_id={APP_ID}",
                    on_message=self.on_message,
                    on_error=self.on_error,
                    on_close=self.on_close,
                    on_open=self.on_open
                )
                wst = threading.Thread(target=self.ws.run_forever)
                wst.daemon = True
                wst.start()

                conn_timeout = 10
                while not self.ws.sock or not self.ws.sock.connected and conn_timeout:
                    time.sleep(1)
                    conn_timeout -= 1

                if self.ws.sock and self.ws.sock.connected:
                    print("Connected to WebSocket")
                    return True
            except Exception as e:
                print(f"Connection failed: {e}, retrying in {delay} seconds...")
                time.sleep(delay)
                attempt += 1

        print('Failed to connect to WebSocket after retries')
        return False

    def on_message(self, ws, message):
        data = json.loads(message)
        if 'error' in data:
            print(f"Error: {data['error']['message']}")
        elif 'candles' in data:
            self.data = pd.DataFrame(data['candles'])
            self.data['time'] = pd.to_datetime(self.data['epoch'], unit='s')
            self.subscribed = True
        elif 'proposal' in data:
            self.response = data['proposal']
        elif 'active_symbols' in data:
            print("Active Symbols:")
            for symbol in data['active_symbols']:
                print(symbol['symbol'], "-", symbol['display_name'])
        elif 'tick' in data:
            self.tick_price = float(data['tick']['quote'])  # Latest price update
        print(f"Received data: {data}")

    def on_error(self, ws, error):
        print(f"Error: {error}")

    def on_close(self, ws, close_status_code, close_msg):
        print("WebSocket connection closed")

    def on_open(self, ws):
        print("WebSocket connection opened")
        self.authorize()

    def authorize(self):
        self.ws.send(json.dumps({"authorize": API_TOKEN}))

    def get_candles(self, symbol, interval, count):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.subscribed = False
        self.ws.send(json.dumps({
            "ticks_history": symbol,
            "adjust_start_time": 1,
            "count": count,
            "end": "latest",
            "start": 1,
            "style": "candles",
            "granularity": interval
        }))

        timeout = 10
        while not self.subscribed and timeout:
            time.sleep(1)
            timeout -= 1

        if not self.subscribed:
            print("Failed to receive candle data")
            return None

        return self.data

    async def get_active_symbols(self):
        if not self.ws:
            print("WebSocket is not connected")
            return

        self.ws.send(json.dumps({
            "active_symbols": "full"
        }))

    async def proposal(self, proposal_params):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.response = None
        self.ws.send(json.dumps(proposal_params))

        timeout = 10
        while not self.response and timeout:
            await asyncio.sleep(1)
            timeout -= 1

        if not self.response:
            print("Failed to receive proposal response")
            return None

        return self.response

    async def fetch_current_price(self, symbol):
        """Fetches real-time price for a given symbol."""
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.ws.send(json.dumps({"ticks": symbol}))
        await asyncio.sleep(1)  # Wait for the tick update
        return getattr(self, 'tick_price', None)

def calculate_indicators(df):
    df['MA_9'] = df['close'].rolling(window=9).mean()
    df['MA_25'] = df['close'].rolling(window=25).mean()

    delta = df['close'].diff()
    gain = (delta.where(delta > 0, 0)).rolling(window=14).mean()
    loss = (-delta.where(delta < 0, 0)).rolling(window=14).mean()
    rs = gain / loss
    df['RSI'] = 100 - (100 / (1 + rs))

    low_14 = df['low'].rolling(window=14).min()
    high_14 = df['high'].rolling(window=14).max()
    df['%K'] = (df['close'] - low_14) / (high_14 - low_14) * 100
    df['%D'] = df['%K'].rolling(window=3).mean()

    return df

def trading_strategy(df):
    last_row = df.iloc[-1]
    if last_row['MA_9'] > last_row['MA_25'] and last_row['RSI'] > 50 and last_row['%K'] > last_row['%D']:
        return 'BUY'
    elif last_row['MA_9'] < last_row['MA_25'] and last_row['RSI'] < 50 and last_row['%K'] < last_row['%D']:
        return 'SELL'
    else:
        return 'HOLD'

async def execute_trade(api, signal, take_profit_level=0.5, stop_loss_level=-0.5):
    contract_type = "CALL" if signal == "BUY" else "PUT"
    barrier = "+0.1" if signal == "BUY" else "-0.1"

    proposal = await api.proposal({
        "proposal": 1,
        "amount": 100,
        "barrier": barrier,
        "basis": "payout",
        "contract_type": contract_type,
        "currency": "USD",
        "duration": 60,
        "duration_unit": "s",
        "symbol": "R_100"
    })

    if proposal and 'id' in proposal:
        proposal_id = proposal['id']
        api.ws.send(json.dumps({"buy": proposal_id, "price": 100}))
        print(f"Executed {signal} trade with proposal ID: {proposal_id}")

        entry_price = float(proposal.get("spot", 0))
        while True:
            current_price = await api.fetch_current_price("R_100")
            if current_price is None:
                print("Failed to fetch current price")
                break

            if signal == "BUY" and (current_price >= entry_price + take_profit_level or current_price <= entry_price + stop_loss_level):
                close_trade(api, proposal_id)
                break
            elif signal == "SELL" and (current_price <= entry_price - take_profit_level or current_price >= entry_price - stop_loss_level):
                close_trade(api, proposal_id)
                break

            await asyncio.sleep(1)

    else:
        print(f"Failed to execute {signal} trade")

def close_trade(api, proposal_id):
    api.ws.send(json.dumps({"sell": proposal_id, "price": 100}))
    print(f"Trade with ID {proposal_id} closed at take-profit or stop-loss level")

async def main():
    deriv_api = DerivAPI()
    if not deriv_api.connect():
        return

    await deriv_api.get_active_symbols()

    symbol = 'R_100'
    interval = 60
    count = 100

    while True:
        candles = deriv_api.get_candles(symbol, interval, count)
        if candles is not None:
            df = calculate_indicators(candles)
            signal = trading_strategy(df)
            print(f"Current signal: {signal}")

            await execute_trade(deriv_api, signal)
        else:
            print("Failed to retrieve candle data")
        
        time.sleep(60)

if __name__ == "__main__":
    await (main())


--- request header ---
GET /websockets/v3?app_id=64724 HTTP/1.1
Upgrade: websocket
Host: ws.binaryws.com
Origin: https://ws.binaryws.com
Sec-WebSocket-Key: laRE74tij5pqua1r+7pmhg==
Sec-WebSocket-Version: 13
Connection: Upgrade


-----------------------
--- response header ---
HTTP/1.1 101 Switching Protocols
Date: Mon, 11 Nov 2024 16:14:15 GMT
Content-Length: 0
Connection: upgrade
Content-Language: en
Upgrade: websocket
Sec-WebSocket-Accept: o//M+gehPptd9PR640cSouf+usI=
CF-Cache-Status: DYNAMIC
Server: cloudflare
CF-RAY: 8e0f9301deb065e6-MBA
alt-svc: h3=":443"; ma=86400
-----------------------
Websocket connected
++Sent raw: b"\x81\xa0\xf3'\x99\x19\x88\x05\xf8l\x87O\xf6k\x9a]\xfc;\xc9\x07\xbbW\xb5\x17\xf8S\xb8Q\xd7S\xc7n\xf1R\x9d}\xbbd"
++Sent decoded: fin=1 opcode=1 data=b'{"authorize": "NF0aJKvNJ4IhKnZ"}'


WebSocket connection opened


++Rcv raw: b'\x81~\x05\xc2{"authorize":{"account_list":[{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1710220418,"currency":"USD","currency_type":"fiat","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR6779028"},{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1709901738,"currency":"BTC","currency_type":"crypto","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR6763883"},{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1721128861,"currency":"tUSDT","currency_type":"crypto","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR7371492"},{"account_category":"trading","account_type":"binary","broker":"VRTC","created_at":1709898717,"currency":"USD","currency_type":"fiat","is_disabled":0,"is_virtual":1,"landing_company_name":"virtual","linked_to":[],"loginid":"VRTC10086060"}],"balance

Received data: {'authorize': {'account_list': [{'account_category': 'trading', 'account_type': 'binary', 'broker': 'CR', 'created_at': 1710220418, 'currency': 'USD', 'currency_type': 'fiat', 'is_disabled': 0, 'is_virtual': 0, 'landing_company_name': 'svg', 'linked_to': [], 'loginid': 'CR6779028'}, {'account_category': 'trading', 'account_type': 'binary', 'broker': 'CR', 'created_at': 1709901738, 'currency': 'BTC', 'currency_type': 'crypto', 'is_disabled': 0, 'is_virtual': 0, 'landing_company_name': 'svg', 'linked_to': [], 'loginid': 'CR6763883'}, {'account_category': 'trading', 'account_type': 'binary', 'broker': 'CR', 'created_at': 1721128861, 'currency': 'tUSDT', 'currency_type': 'crypto', 'is_disabled': 0, 'is_virtual': 0, 'landing_company_name': 'svg', 'linked_to': [], 'loginid': 'CR7371492'}, {'account_category': 'trading', 'account_type': 'binary', 'broker': 'VRTC', 'created_at': 1709898717, 'currency': 'USD', 'currency_type': 'fiat', 'is_disabled': 0, 'is_virtual': 1, 'landing_c

++Sent raw: b'\x81\x9a\x8e\x08f\xec\xf5*\x07\x8f\xfaa\x10\x89\xd1{\x1f\x81\xecg\n\x9f\xac2F\xce\xe8}\n\x80\xacu'
++Sent decoded: fin=1 opcode=1 data=b'{"active_symbols": "full"}'
++Sent raw: b'\x81\xfe\x00\x84\xb4\x95&\x87\xcf\xb7R\xee\xd7\xfeU\xd8\xdc\xfcU\xf3\xdb\xe7_\xa5\x8e\xb5\x04\xd5\xeb\xa4\x16\xb7\x96\xb9\x06\xa5\xd5\xf1L\xf2\xc7\xe1y\xf4\xc0\xf4T\xf3\xeb\xe1O\xea\xd1\xb7\x1c\xa7\x85\xb9\x06\xa5\xd7\xfaS\xe9\xc0\xb7\x1c\xa7\x85\xa5\x16\xab\x94\xb7C\xe9\xd0\xb7\x1c\xa7\x96\xf9G\xf3\xd1\xe6R\xa5\x98\xb5\x04\xf4\xc0\xf4T\xf3\x96\xaf\x06\xb6\x98\xb5\x04\xf4\xc0\xecJ\xe2\x96\xaf\x06\xa5\xd7\xf4H\xe3\xd8\xf0U\xa5\x98\xb5\x04\xe0\xc6\xf4H\xf2\xd8\xf4T\xee\xc0\xec\x04\xbd\x94\xa3\x16\xfa'
++Sent decoded: fin=1 opcode=1 data=b'{"ticks_history": "R_100", "adjust_start_time": 1, "count": 100, "end": "latest", "start": 1, "style": "candles", "granularity": 60}'


...

Received data: {'echo_req': {'ticks': 'R_100'}, 'msg_type': 'tick', 'subscription': {'id': 'ae3f817e-44f3-1965-e0e9-f7813aa1f0bf'}, 'tick': {'ask': 1020.21, 'bid': 1020.01, 'epoch': 1731342286, 'id': 'ae3f817e-44f3-1965-e0e9-f7813aa1f0bf', 'pip_size': 2, 'quote': 1020.11, 'symbol': 'R_100'}}


++Rcv raw: b'\x81~\x00\xff{"echo_req":{"ticks":"R_100"},"msg_type":"tick","subscription":{"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf"},"tick":{"ask":1020.11,"bid":1019.91,"epoch":1731342288,"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf","pip_size":2,"quote":1020.01,"symbol":"R_100"}}'
++Rcv decoded: fin=1 opcode=1 data=b'{"echo_req":{"ticks":"R_100"},"msg_type":"tick","subscription":{"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf"},"tick":{"ask":1020.11,"bid":1019.91,"epoch":1731342288,"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf","pip_size":2,"quote":1020.01,"symbol":"R_100"}}'


Received data: {'echo_req': {'ticks': 'R_100'}, 'msg_type': 'tick', 'subscription': {'id': 'ae3f817e-44f3-1965-e0e9-f7813aa1f0bf'}, 'tick': {'ask': 1020.11, 'bid': 1019.91, 'epoch': 1731342288, 'id': 'ae3f817e-44f3-1965-e0e9-f7813aa1f0bf', 'pip_size': 2, 'quote': 1020.01, 'symbol': 'R_100'}}


++Rcv raw: b'\x81~\x00\xff{"echo_req":{"ticks":"R_100"},"msg_type":"tick","subscription":{"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf"},"tick":{"ask":1020.14,"bid":1019.94,"epoch":1731342290,"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf","pip_size":2,"quote":1020.04,"symbol":"R_100"}}'
++Rcv decoded: fin=1 opcode=1 data=b'{"echo_req":{"ticks":"R_100"},"msg_type":"tick","subscription":{"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf"},"tick":{"ask":1020.14,"bid":1019.94,"epoch":1731342290,"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf","pip_size":2,"quote":1020.04,"symbol":"R_100"}}'


Received data: {'echo_req': {'ticks': 'R_100'}, 'msg_type': 'tick', 'subscription': {'id': 'ae3f817e-44f3-1965-e0e9-f7813aa1f0bf'}, 'tick': {'ask': 1020.14, 'bid': 1019.94, 'epoch': 1731342290, 'id': 'ae3f817e-44f3-1965-e0e9-f7813aa1f0bf', 'pip_size': 2, 'quote': 1020.04, 'symbol': 'R_100'}}


In [ ]:
import websocket
import json
import time
import threading
import pandas as pd
import numpy as np
import asyncio

API_TOKEN = 'NF0aJKvNJ4IhKnZ'
APP_ID = 64724

class DerivAPI:
    def __init__(self):
        self.ws = None
        self.data = {}
        self.subscribed = False
        self.response = None

    def connect(self, retries=3, delay=5):
        attempt = 0
        while attempt < retries:
            try:
                websocket.enableTrace(True)
                self.ws = websocket.WebSocketApp(
                    f"wss://ws.binaryws.com/websockets/v3?app_id={APP_ID}",
                    on_message=self.on_message,
                    on_error=self.on_error,
                    on_close=self.on_close,
                    on_open=self.on_open
                )
                wst = threading.Thread(target=self.ws.run_forever)
                wst.daemon = True
                wst.start()

                conn_timeout = 10
                while not self.ws.sock or not self.ws.sock.connected and conn_timeout:
                    time.sleep(1)
                    conn_timeout -= 1

                if self.ws.sock and self.ws.sock.connected:
                    print("Connected to WebSocket")
                    return True
            except Exception as e:
                print(f"Connection failed: {e}, retrying in {delay} seconds...")
                time.sleep(delay)
                attempt += 1

        print('Failed to connect to WebSocket after retries')
        return False

    def on_message(self, ws, message):
        data = json.loads(message)
        if 'error' in data:
            print(f"Error: {data['error']['message']}")
        elif 'candles' in data:
            symbol = data['echo_req']['ticks_history']
            self.data[symbol] = pd.DataFrame(data['candles'])
            self.data[symbol]['time'] = pd.to_datetime(self.data[symbol]['epoch'], unit='s')
            self.subscribed = True
        elif 'proposal' in data:
            self.response = data['proposal']
        elif 'active_symbols' in data:
            print("Active Symbols:")
            for symbol in data['active_symbols']:
                print(symbol['symbol'], "-", symbol['display_name'])
        print(f"Received data: {data}")

    def on_error(self, ws, error):
        print(f"Error: {error}")

    def on_close(self, ws, close_status_code, close_msg):
        print("WebSocket connection closed")

    def on_open(self, ws):
        print("WebSocket connection opened")
        self.authorize()

    def authorize(self):
        self.ws.send(json.dumps({"authorize": API_TOKEN}))

    def get_candles(self, symbol, interval, count):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.subscribed = False
        self.ws.send(json.dumps({
            "ticks_history": symbol,
            "adjust_start_time": 1,
            "count": count,
            "end": "latest",
            "start": 1,
            "style": "candles",
            "granularity": interval
        }))

        timeout = 10
        while not self.subscribed and timeout:
            time.sleep(1)
            timeout -= 1

        if not self.subscribed:
            print("Failed to receive candle data for symbol:", symbol)
            return None

        return self.data[symbol]

    async def get_active_symbols(self):
        if not self.ws:
            print("WebSocket is not connected")
            return

        self.ws.send(json.dumps({
            "active_symbols": "full"
        }))

    async def proposal(self, proposal_params):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.response = None
        self.ws.send(json.dumps(proposal_params))

        timeout = 10
        while not self.response and timeout:
            await asyncio.sleep(1)
            timeout -= 1

        if not self.response:
            print("Failed to receive proposal response")
            return None

        return self.response

def calculate_indicators(df):
    df['MA_9'] = df['close'].rolling(window=9).mean()
    df['MA_25'] = df['close'].rolling(window=25).mean()

    delta = df['close'].diff()
    gain = (delta.where(delta > 0, 0)).rolling(window=14).mean()
    loss = (-delta.where(delta < 0, 0)).rolling(window=14).mean()
    rs = gain / loss
    df['RSI'] = 100 - (100 / (1 + rs))

    low_14 = df['low'].rolling(window=14).min()
    high_14 = df['high'].rolling(window=14).max()
    df['%K'] = (df['close'] - low_14) / (high_14 - low_14) * 100
    df['%D'] = df['%K'].rolling(window=3).mean()

    return df

def trading_strategy(df):
    last_row = df.iloc[-1]
    if last_row['MA_9'] > last_row['MA_25'] and last_row['RSI'] > 50 and last_row['%K'] > last_row['%D']:
        return 'BUY'
    elif last_row['MA_9'] < last_row['MA_25'] and last_row['RSI'] < 50 and last_row['%K'] < last_row['%D']:
        return 'SELL'
    else:
        return 'HOLD'

async def execute_trade(api, signal, symbol):
    if signal == 'BUY':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "+0.1", "basis": "payout",
            "contract_type": "CALL", "currency": "USD", "duration": 60, "duration_unit": "s",
            "symbol": symbol
        })
    elif signal == 'SELL':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "-0.1", "basis": "payout",
            "contract_type": "PUT", "currency": "USD", "duration": 60, "duration_unit": "s",
            "symbol": symbol
        })
    else:
        return

    if proposal and 'id' in proposal:
        proposal_id = proposal['id']
        api.ws.send(json.dumps({"buy": proposal_id, "price": 100}))
        print(f"Executed {signal} trade for {symbol} with proposal ID: {proposal_id}")
    else:
        print(f"Failed to execute {signal} trade for {symbol}")

async def main():
    deriv_api = DerivAPI()
    if not deriv_api.connect():
        return

    await deriv_api.get_active_symbols()  # Fetch and print all active symbols

    symbols = ['R_100', 'R_50', 'R_75']  # List of symbols to analyze
    interval = 60
    count = 100

    while True:
        for symbol in symbols:
            candles = deriv_api.get_candles(symbol, interval, count)
            if candles is not None:
                df = calculate_indicators(candles)
                signal = trading_strategy(df)
                print(f"Current signal for {symbol}: {signal}")

                await execute_trade(deriv_api, signal, symbol)
            else:
                print(f"Failed to retrieve candle data for {symbol}")

        time.sleep(60)

if __name__ == "__main__":
    await (main())


++Rcv raw: b'\x81~\x00\xff{"echo_req":{"ticks":"R_100"},"msg_type":"tick","subscription":{"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf"},"tick":{"ask":1019.12,"bid":1018.92,"epoch":1731342292,"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf","pip_size":2,"quote":1019.02,"symbol":"R_100"}}'
++Rcv decoded: fin=1 opcode=1 data=b'{"echo_req":{"ticks":"R_100"},"msg_type":"tick","subscription":{"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf"},"tick":{"ask":1019.12,"bid":1018.92,"epoch":1731342292,"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf","pip_size":2,"quote":1019.02,"symbol":"R_100"}}'


Received data: {'echo_req': {'ticks': 'R_100'}, 'msg_type': 'tick', 'subscription': {'id': 'ae3f817e-44f3-1965-e0e9-f7813aa1f0bf'}, 'tick': {'ask': 1019.12, 'bid': 1018.92, 'epoch': 1731342292, 'id': 'ae3f817e-44f3-1965-e0e9-f7813aa1f0bf', 'pip_size': 2, 'quote': 1019.02, 'symbol': 'R_100'}}


++Rcv raw: b'\x81~\x00\xff{"echo_req":{"ticks":"R_100"},"msg_type":"tick","subscription":{"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf"},"tick":{"ask":1018.72,"bid":1018.52,"epoch":1731342294,"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf","pip_size":2,"quote":1018.62,"symbol":"R_100"}}'
++Rcv decoded: fin=1 opcode=1 data=b'{"echo_req":{"ticks":"R_100"},"msg_type":"tick","subscription":{"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf"},"tick":{"ask":1018.72,"bid":1018.52,"epoch":1731342294,"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf","pip_size":2,"quote":1018.62,"symbol":"R_100"}}'


Received data: {'echo_req': {'ticks': 'R_100'}, 'msg_type': 'tick', 'subscription': {'id': 'ae3f817e-44f3-1965-e0e9-f7813aa1f0bf'}, 'tick': {'ask': 1018.72, 'bid': 1018.52, 'epoch': 1731342294, 'id': 'ae3f817e-44f3-1965-e0e9-f7813aa1f0bf', 'pip_size': 2, 'quote': 1018.62, 'symbol': 'R_100'}}


--- request header ---
GET /websockets/v3?app_id=64724 HTTP/1.1
Upgrade: websocket
Host: ws.binaryws.com
Origin: https://ws.binaryws.com
Sec-WebSocket-Key: FKEYtZBJWAd4RIs+82eVBg==
Sec-WebSocket-Version: 13
Connection: Upgrade


-----------------------
--- response header ---
HTTP/1.1 101 Switching Protocols
Date: Mon, 11 Nov 2024 16:24:55 GMT
Content-Length: 0
Connection: upgrade
Upgrade: websocket
Content-Language: en
Sec-WebSocket-Accept: I073KLWvMAbXcGvGM5WF9ehjul4=
CF-Cache-Status: DYNAMIC
Server: cloudflare
CF-RAY: 8e0fa2a1be3265e9-MBA
alt-svc: h3=":443"; ma=86400
-----------------------
Websocket connected
++Sent raw: b'\x81\xa0\xd1\xe1\xa2\xf0\xaa\xc3\xc3\x85\xa5\x89\xcd\x82\xb8\x9b\xc7\xd2\xeb\xc1\x80\xbe\x97\xd1\xc3\xba\x9a\x97\xec\xba\xe5\xa8\xca\xbb\xbf\xbb\x80\x8d'
++Sent decoded: fin=1 opcode=1 data=b'{"authorize": "NF0aJKvNJ4IhKnZ"}'


...

Received data: {'echo_req': {'ticks': 'R_100'}, 'msg_type': 'tick', 'subscription': {'id': 'ae3f817e-44f3-1965-e0e9-f7813aa1f0bf'}, 'tick': {'ask': 1019.13, 'bid': 1018.93, 'epoch': 1731342526, 'id': 'ae3f817e-44f3-1965-e0e9-f7813aa1f0bf', 'pip_size': 2, 'quote': 1019.03, 'symbol': 'R_100'}}


++Rcv raw: b'\x81~\x00\xff{"echo_req":{"ticks":"R_100"},"msg_type":"tick","subscription":{"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf"},"tick":{"ask":1019.52,"bid":1019.32,"epoch":1731342528,"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf","pip_size":2,"quote":1019.42,"symbol":"R_100"}}'
++Rcv decoded: fin=1 opcode=1 data=b'{"echo_req":{"ticks":"R_100"},"msg_type":"tick","subscription":{"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf"},"tick":{"ask":1019.52,"bid":1019.32,"epoch":1731342528,"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf","pip_size":2,"quote":1019.42,"symbol":"R_100"}}'


Received data: {'echo_req': {'ticks': 'R_100'}, 'msg_type': 'tick', 'subscription': {'id': 'ae3f817e-44f3-1965-e0e9-f7813aa1f0bf'}, 'tick': {'ask': 1019.52, 'bid': 1019.32, 'epoch': 1731342528, 'id': 'ae3f817e-44f3-1965-e0e9-f7813aa1f0bf', 'pip_size': 2, 'quote': 1019.42, 'symbol': 'R_100'}}


++Rcv raw: b'\x81~\x00\xff{"echo_req":{"ticks":"R_100"},"msg_type":"tick","subscription":{"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf"},"tick":{"ask":1019.58,"bid":1019.38,"epoch":1731342530,"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf","pip_size":2,"quote":1019.48,"symbol":"R_100"}}'
++Rcv decoded: fin=1 opcode=1 data=b'{"echo_req":{"ticks":"R_100"},"msg_type":"tick","subscription":{"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf"},"tick":{"ask":1019.58,"bid":1019.38,"epoch":1731342530,"id":"ae3f817e-44f3-1965-e0e9-f7813aa1f0bf","pip_size":2,"quote":1019.48,"symbol":"R_100"}}'


Received data: {'echo_req': {'ticks': 'R_100'}, 'msg_type': 'tick', 'subscription': {'id': 'ae3f817e-44f3-1965-e0e9-f7813aa1f0bf'}, 'tick': {'ask': 1019.58, 'bid': 1019.38, 'epoch': 1731342530, 'id': 'ae3f817e-44f3-1965-e0e9-f7813aa1f0bf', 'pip_size': 2, 'quote': 1019.48, 'symbol': 'R_100'}}


In [ ]:
import websocket
import json
import time
import threading
import pandas as pd
import numpy as np
import asyncio

API_TOKEN = 'NF0aJKvNJ4IhKnZ'
APP_ID = 64724

# Risk management parameters
STOP_LOSS_PERCENTAGE = 0.01  # 2% stop-loss
TAKE_PROFIT_PERCENTAGE = 0.03  # 5% take-profit

class DerivAPI:
    def __init__(self):
        self.ws = None
        self.data = {}
        self.subscribed = False
        self.response = None
        self.active_trades = {}

    def connect(self, retries=3, delay=5):
        attempt = 0
        while attempt < retries:
            try:
                websocket.enableTrace(True)
                self.ws = websocket.WebSocketApp(
                    f"wss://ws.binaryws.com/websockets/v3?app_id={APP_ID}",
                    on_message=self.on_message,
                    on_error=self.on_error,
                    on_close=self.on_close,
                    on_open=self.on_open
                )
                wst = threading.Thread(target=self.ws.run_forever)
                wst.daemon = True
                wst.start()

                conn_timeout = 10
                while not self.ws.sock or not self.ws.sock.connected and conn_timeout:
                    time.sleep(1)
                    conn_timeout -= 1

                if self.ws.sock and self.ws.sock.connected:
                    print("Connected to WebSocket")
                    return True
            except Exception as e:
                print(f"Connection failed: {e}, retrying in {delay} seconds...")
                time.sleep(delay)
                attempt += 1

        print('Failed to connect to WebSocket after retries')
        return False

    def on_message(self, ws, message):
        data = json.loads(message)
        if 'error' in data:
            print(f"Error: {data['error']['message']}")
        elif 'candles' in data:
            symbol = data['echo_req']['ticks_history']
            self.data[symbol] = pd.DataFrame(data['candles'])
            self.data[symbol]['time'] = pd.to_datetime(self.data[symbol]['epoch'], unit='s')
            self.subscribed = True
        elif 'proposal' in data:
            self.response = data['proposal']
        elif 'active_symbols' in data:
            print("Active Symbols:")
            for symbol in data['active_symbols']:
                print(symbol['symbol'], "-", symbol['display_name'])
        print(f"Received data: {data}")

    def on_error(self, ws, error):
        print(f"Error: {error}")

    def on_close(self, ws, close_status_code, close_msg):
        print("WebSocket connection closed")

    def on_open(self, ws):
        print("WebSocket connection opened")
        self.authorize()

    def authorize(self):
        self.ws.send(json.dumps({"authorize": API_TOKEN}))

    def get_candles(self, symbol, interval, count):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.subscribed = False
        self.ws.send(json.dumps({
            "ticks_history": symbol,
            "adjust_start_time": 1,
            "count": count,
            "end": "latest",
            "start": 1,
            "style": "candles",
            "granularity": interval
        }))

        timeout = 10
        while not self.subscribed and timeout:
            time.sleep(1)
            timeout -= 1

        if not self.subscribed:
            print("Failed to receive candle data for symbol:", symbol)
            return None

        return self.data[symbol]

    async def get_active_symbols(self):
        if not self.ws:
            print("WebSocket is not connected")
            return

        self.ws.send(json.dumps({
            "active_symbols": "full"
        }))

    async def proposal(self, proposal_params):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.response = None
        self.ws.send(json.dumps(proposal_params))

        timeout = 10
        while not self.response and timeout:
            await asyncio.sleep(1)
            timeout -= 1

        if not self.response:
            print("Failed to receive proposal response")
            return None

        return self.response

def calculate_indicators(df):
    df['MA_9'] = df['close'].rolling(window=9).mean()
    df['MA_25'] = df['close'].rolling(window=25).mean()

    delta = df['close'].diff()
    gain = (delta.where(delta > 0, 0)).rolling(window=14).mean()
    loss = (-delta.where(delta < 0, 0)).rolling(window=14).mean()
    rs = gain / loss
    df['RSI'] = 100 - (100 / (1 + rs))

    low_14 = df['low'].rolling(window=14).min()
    high_14 = df['high'].rolling(window=14).max()
    df['%K'] = (df['close'] - low_14) / (high_14 - low_14) * 100
    df['%D'] = df['%K'].rolling(window=3).mean()

    return df

def trading_strategy(df):
    last_row = df.iloc[-1]
    if last_row['MA_9'] > last_row['MA_25'] and last_row['RSI'] > 50 and last_row['%K'] > last_row['%D']:
        return 'BUY'
    elif last_row['MA_9'] < last_row['MA_25'] and last_row['RSI'] < 50 and last_row['%K'] < last_row['%D']:
        return 'SELL'
    else:
        return 'HOLD'

def set_risk_levels(entry_price, signal):
    if signal == 'BUY':
        stop_loss = entry_price * (1 - STOP_LOSS_PERCENTAGE)
        take_profit = entry_price * (1 + TAKE_PROFIT_PERCENTAGE)
    elif signal == 'SELL':
        stop_loss = entry_price * (1 + STOP_LOSS_PERCENTAGE)
        take_profit = entry_price * (1 - TAKE_PROFIT_PERCENTAGE)
    return stop_loss, take_profit

async def execute_trade(api, signal, symbol, entry_price):
    stop_loss, take_profit = set_risk_levels(entry_price, signal)
    trade_info = {'entry_price': entry_price, 'stop_loss': stop_loss, 'take_profit': take_profit}

    # Record trade info for tracking purposes
    api.active_trades[symbol] = trade_info
    print(f"Initiated {signal} trade for {symbol} at {entry_price} with SL: {stop_loss}, TP: {take_profit}")

    if signal == 'BUY':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "+0.1", "basis": "payout",
            "contract_type": "CALL", "currency": "USD", "duration": 60, "duration_unit": "s",
            "symbol": symbol
        })
    elif signal == 'SELL':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "-0.1", "basis": "payout",
            "contract_type": "PUT", "currency": "USD", "duration": 60, "duration_unit": "s",
            "symbol": symbol
        })

    if proposal and 'id' in proposal:
        proposal_id = proposal['id']
        api.ws.send(json.dumps({"buy": proposal_id, "price": 100}))
        print(f"Executed {signal} trade for {symbol} with proposal ID: {proposal_id}")
    else:
        print(f"Failed to execute {signal} trade for {symbol}")

async def main():
    deriv_api = DerivAPI()
    if not deriv_api.connect():
        return

    await deriv_api.get_active_symbols()  # Fetch and print all active symbols

    symbols = ['R_100', 'R_50', 'R_75']  # List of symbols to analyze
    interval = 60
    count = 100

    while True:
        for symbol in symbols:
            candles = deriv_api.get_candles(symbol, interval, count)
            if candles is not None:
                df = calculate_indicators(candles)
                signal = trading_strategy(df)
                print(f"Current signal for {symbol}: {signal}")

                # Example entry price from the last close price (for demonstration)
                entry_price = df['close'].iloc[-1]

                if signal in ['BUY', 'SELL']:
                    await execute_trade(deriv_api, signal, symbol, entry_price)
            else:
                print(f"Failed to retrieve candle data for {symbol}")

        time.sleep(60)

if __name__ == "__main__":
    await (main())


--- request header ---
GET /websockets/v3?app_id=64724 HTTP/1.1
Upgrade: websocket
Host: ws.binaryws.com
Origin: https://ws.binaryws.com
Sec-WebSocket-Key: UtUvs+lDQQ62uLONi7FLAg==
Sec-WebSocket-Version: 13
Connection: Upgrade


-----------------------
--- response header ---
HTTP/1.1 101 Switching Protocols
Date: Mon, 11 Nov 2024 16:34:04 GMT
Content-Length: 0
Connection: upgrade
Upgrade: websocket
Content-Language: en
Sec-WebSocket-Accept: iDL/gSUroEOPw44Cv2Tuorez2dc=
CF-Cache-Status: DYNAMIC
Server: cloudflare
CF-RAY: 8e0fb00368e365e4-MBA
alt-svc: h3=":443"; ma=86400
-----------------------
Websocket connected
++Sent raw: b'\x81\xa0\xacJGe\xd7h&\x10\xd8"(\x17\xc50"G\x96je+\xeaz&/\xe7<\t/\x98\x03/.\xc2\x10e\x18'
++Sent decoded: fin=1 opcode=1 data=b'{"authorize": "NF0aJKvNJ4IhKnZ"}'
++Sent raw: b'\x81\x9a_\xe5\xcf\x1f$\xc7\xae|+\x8c\xb9z\x00\x96\xb6r=\x8a\xa3l}\xdf\xef=9\x90\xa3s}\x98'
++Sent decoded: fin=1 opcode=1 data=b'{"active_symbols": "full"}'
++Sent raw: b'\x81\xfe\x00\x84Z\x

WebSocket connection opened
Connected to WebSocket


++Rcv raw: b'\x81~\xac\xe1{"active_symbols":[{"allow_forward_starting":0,"delay_amount":0,"display_name":"AUD Basket","display_order":28,"exchange_is_open":1,"exchange_name":"FOREX","intraday_interval_minutes":5,"is_trading_suspended":0,"market":"synthetic_index","market_display_name":"Derived","pip":0.001,"quoted_currency_symbol":"WLDAUD","spot":893.503,"spot_age":"0","spot_percentage_change":"0.12","spot_time":"1731342840","subgroup":"baskets","subgroup_display_name":"Baskets","submarket":"forex_basket","submarket_display_name":"Forex Basket","symbol":"WLDAUD","symbol_type":"forex_basket"},{"allow_forward_starting":1,"delay_amount":0,"display_name":"AUD\\/CAD","display_order":10,"exchange_is_open":1,"exchange_name":"FOREX","intraday_interval_minutes":5,"is_trading_suspended":0,"market":"forex","market_display_name":"Forex","pip":1e-05,"quoted_currency_symbol":"CAD","spot":0.91464,"spot_age":"1","spot_percentage_change":"-0.13","spot_time":"1731342840","subgroup":"none","subgroup_disp

Active Symbols:
WLDAUD - AUD Basket
frxAUDCAD - AUD/CAD
frxAUDCHF - AUD/CHF
frxAUDJPY - AUD/JPY
frxAUDNZD - AUD/NZD
frxAUDUSD - AUD/USD
OTC_AS51 - Australia 200
cryBTCUSD - BTC/USD
RDBEAR - Bear Market Index
BOOM300N - Boom 300 Index
BOOM500 - Boom 500 Index
BOOM1000 - Boom 1000 Index
RDBULL - Bull Market Index
CRASH300N - Crash 300 Index
CRASH500 - Crash 500 Index
CRASH1000 - Crash 1000 Index
cryETHUSD - ETH/USD
WLDEUR - EUR Basket
frxEURAUD - EUR/AUD
frxEURCAD - EUR/CAD
frxEURCHF - EUR/CHF
frxEURGBP - EUR/GBP
frxEURJPY - EUR/JPY
frxEURNZD - EUR/NZD
frxEURUSD - EUR/USD
OTC_SX5E - Euro 50
OTC_FCHI - France 40
WLDGBP - GBP Basket
frxGBPAUD - GBP/AUD
frxGBPCAD - GBP/CAD
frxGBPCHF - GBP/CHF
frxGBPJPY - GBP/JPY
frxGBPNOK - GBP/NOK
frxGBPNZD - GBP/NZD
frxGBPUSD - GBP/USD
OTC_GDAXI - Germany 40
WLDXAU - Gold Basket
frxXAUUSD - Gold/USD
OTC_HSI - Hong Kong 50
OTC_N225 - Japan 225
JD10 - Jump 10 Index
JD25 - Jump 25 Index
JD50 - Jump 50 Index
JD75 - Jump 75 Index
JD100 - Jump 100 Index
frxNZDJ

++Rcv decoded: fin=1 opcode=1 data=b'{"candles":[{"close":1030.93,"epoch":1731336900,"high":1032.12,"low":1030.6,"open":1031.23},{"close":1029.7,"epoch":1731336960,"high":1031.92,"low":1029.67,"open":1031.12},{"close":1029.13,"epoch":1731337020,"high":1030.51,"low":1028.95,"open":1029.85},{"close":1028.08,"epoch":1731337080,"high":1029.46,"low":1027.69,"open":1029.31},{"close":1026.34,"epoch":1731337140,"high":1029.22,"low":1026.34,"open":1028.39},{"close":1024.86,"epoch":1731337200,"high":1027.28,"low":1024.86,"open":1026.09},{"close":1023.62,"epoch":1731337260,"high":1024.83,"low":1023.62,"open":1024.64},{"close":1023.35,"epoch":1731337320,"high":1023.56,"low":1022.3,"open":1023.33},{"close":1022.57,"epoch":1731337380,"high":1023.52,"low":1021.92,"open":1023.09},{"close":1022.34,"epoch":1731337440,"high":1022.92,"low":1021.09,"open":1022.79},{"close":1022.67,"epoch":1731337500,"high":1022.81,"low":1021.54,"open":1022.43},{"close":1021.5,"epoch":1731337560,"high":1022.83,"low":1021.23

...

Received data: {'buy': {'balance_after': 9798.87, 'buy_price': 48.3, 'contract_id': 262722592448, 'longcode': 'Win payout if Volatility 100 Index is strictly higher than entry spot plus 0.10 at 1 minute after contract start time.', 'payout': 100, 'purchase_time': 1731342973, 'shortcode': 'CALL_R_100_100.00_1731342973_1731343033_S10P_0', 'start_time': 1731342973, 'transaction_id': 523759043548}, 'echo_req': {'buy': '59041e3a-7fb1-4be3-2690-def0c994d06b', 'price': 100}, 'msg_type': 'buy'}
Received data: {'candles': [{'close': 292.0571, 'epoch': 1731337020, 'high': 292.079, 'low': 291.8681, 'open': 291.8681}, {'close': 292.2701, 'epoch': 1731337080, 'high': 292.2935, 'low': 292.0593, 'open': 292.0593}, {'close': 292.4622, 'epoch': 1731337140, 'high': 292.4622, 'low': 292.1497, 'open': 292.2485}, {'close': 292.3897, 'epoch': 1731337200, 'high': 292.54, 'low': 292.2775, 'open': 292.523}, {'close': 292.4691, 'epoch': 1731337260, 'high': 292.517, 'low': 292.2941, 'open': 292.4576}, {'close': 

++Sent raw: b'\x81\xfe\x00\x83l4\xd8\xe3\x17\x16\xac\x8a\x0f_\xab\xbc\x04]\xab\x97\x03F\xa1\xc1V\x14\xfa\xb13\x03\xed\xc1@\x14\xfa\x82\x08^\xad\x90\x18k\xab\x97\rF\xac\xbc\x18]\xb5\x86N\x0e\xf8\xd2@\x14\xfa\x80\x03A\xb6\x97N\x0e\xf8\xd2\\\x04\xf4\xc3NQ\xb6\x87N\x0e\xf8\xc1\x00U\xac\x86\x1f@\xfa\xcfL\x16\xab\x97\rF\xac\xc1V\x14\xe9\xcfL\x16\xab\x97\x15X\xbd\xc1V\x14\xfa\x80\rZ\xbc\x8f\tG\xfa\xcfL\x16\xbf\x91\rZ\xad\x8f\rF\xb1\x97\x15\x16\xe2\xc3Z\x04\xa5'
++Sent decoded: fin=1 opcode=1 data=b'{"ticks_history": "R_75", "adjust_start_time": 1, "count": 100, "end": "latest", "start": 1, "style": "candles", "granularity": 60}'


Current signal for R_50: HOLD


++Rcv raw: b'\x81~$\xdb{"candles":[{"close":98303.1143,"epoch":1731337020,"high":98390.1485,"low":98303.1143,"open":98358.6566},{"close":98300.2443,"epoch":1731337080,"high":98325.5423,"low":98194.0835,"open":98315.1341},{"close":98280.1645,"epoch":1731337140,"high":98311.1252,"low":98237.0842,"open":98310.4297},{"close":98248.1194,"epoch":1731337200,"high":98302.3902,"low":98237.6812,"open":98285.2675},{"close":98032.5776,"epoch":1731337260,"high":98254.8444,"low":98032.5776,"open":98227.1833},{"close":97958.0631,"epoch":1731337320,"high":98055.5652,"low":97958.0631,"open":97991.5011},{"close":97951.2502,"epoch":1731337380,"high":97951.2502,"low":97836.5959,"open":97943.5947},{"close":97913.3392,"epoch":1731337440,"high":97980.8896,"low":97911.9568,"open":97980.8896},{"close":98086.7756,"epoch":1731337500,"high":98142.1968,"low":97903.123,"open":97903.123},{"close":98075.7384,"epoch":1731337560,"high":98140.7143,"low":98037.3398,"open":98088.3201},{"close":98060.9155,"epoch":173133762

Received data: {'candles': [{'close': 98303.1143, 'epoch': 1731337020, 'high': 98390.1485, 'low': 98303.1143, 'open': 98358.6566}, {'close': 98300.2443, 'epoch': 1731337080, 'high': 98325.5423, 'low': 98194.0835, 'open': 98315.1341}, {'close': 98280.1645, 'epoch': 1731337140, 'high': 98311.1252, 'low': 98237.0842, 'open': 98310.4297}, {'close': 98248.1194, 'epoch': 1731337200, 'high': 98302.3902, 'low': 98237.6812, 'open': 98285.2675}, {'close': 98032.5776, 'epoch': 1731337260, 'high': 98254.8444, 'low': 98032.5776, 'open': 98227.1833}, {'close': 97958.0631, 'epoch': 1731337320, 'high': 98055.5652, 'low': 97958.0631, 'open': 97991.5011}, {'close': 97951.2502, 'epoch': 1731337380, 'high': 97951.2502, 'low': 97836.5959, 'open': 97943.5947}, {'close': 97913.3392, 'epoch': 1731337440, 'high': 97980.8896, 'low': 97911.9568, 'open': 97980.8896}, {'close': 98086.7756, 'epoch': 1731337500, 'high': 98142.1968, 'low': 97903.123, 'open': 97903.123}, {'close': 98075.7384, 'epoch': 1731337560, 'hig

In [ ]:
import websocket
import json
import time
import threading
import pandas as pd
import numpy as np
import asyncio

API_TOKEN = 'NF0aJKvNJ4IhKnZ'
APP_ID = 64724

# Risk management parameters
STOP_LOSS_PERCENTAGE = 0.02  # 2% stop-loss
TAKE_PROFIT_PERCENTAGE = 0.05  # 5% take-profit
DURATION_MAX = 60  # Max duration for a trade in seconds

class DerivAPI:
    def __init__(self):
        self.ws = None
        self.data = {}
        self.subscribed = False
        self.response = None
        self.active_trades = {}

    def connect(self, retries=3, delay=5):
        attempt = 0
        while attempt < retries:
            try:
                websocket.enableTrace(True)
                self.ws = websocket.WebSocketApp(
                    f"wss://ws.binaryws.com/websockets/v3?app_id={APP_ID}",
                    on_message=self.on_message,
                    on_error=self.on_error,
                    on_close=self.on_close,
                    on_open=self.on_open
                )
                wst = threading.Thread(target=self.ws.run_forever)
                wst.daemon = True
                wst.start()

                conn_timeout = 10
                while not self.ws.sock or not self.ws.sock.connected and conn_timeout:
                    time.sleep(1)
                    conn_timeout -= 1

                if self.ws.sock and self.ws.sock.connected:
                    print("Connected to WebSocket")
                    return True
            except Exception as e:
                print(f"Connection failed: {e}, retrying in {delay} seconds...")
                time.sleep(delay)
                attempt += 1

        print('Failed to connect to WebSocket after retries')
        return False

    def on_message(self, ws, message):
        data = json.loads(message)
        if 'error' in data:
            print(f"Error: {data['error']['message']}")
        elif 'candles' in data:
            symbol = data['echo_req']['ticks_history']
            self.data[symbol] = pd.DataFrame(data['candles'])
            self.data[symbol]['time'] = pd.to_datetime(self.data[symbol]['epoch'], unit='s')
            self.subscribed = True
        elif 'proposal' in data:
            self.response = data['proposal']
        elif 'active_symbols' in data:
            print("Active Symbols:")
            for symbol in data['active_symbols']:
                print(symbol['symbol'], "-", symbol['display_name'])
        print(f"Received data: {data}")

    def on_error(self, ws, error):
        print(f"Error: {error}")

    def on_close(self, ws, close_status_code, close_msg):
        print("WebSocket connection closed")

    def on_open(self, ws):
        print("WebSocket connection opened")
        self.authorize()

    def authorize(self):
        self.ws.send(json.dumps({"authorize": API_TOKEN}))

    def get_candles(self, symbol, interval, count):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.subscribed = False
        self.ws.send(json.dumps({
            "ticks_history": symbol,
            "adjust_start_time": 1,
            "count": count,
            "end": "latest",
            "start": 1,
            "style": "candles",
            "granularity": interval
        }))

        timeout = 10
        while not self.subscribed and timeout:
            time.sleep(1)
            timeout -= 1

        if not self.subscribed:
            print("Failed to receive candle data for symbol:", symbol)
            return None

        return self.data[symbol]

    async def get_active_symbols(self):
        if not self.ws:
            print("WebSocket is not connected")
            return

        self.ws.send(json.dumps({
            "active_symbols": "full"
        }))

    async def proposal(self, proposal_params):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.response = None
        self.ws.send(json.dumps(proposal_params))

        timeout = 10
        while not self.response and timeout:
            await asyncio.sleep(1)
            timeout -= 1

        if not self.response:
            print("Failed to receive proposal response")
            return None

        return self.response

# Volatility (ATR) Calculation
def calculate_atr(df):
    df['H-L'] = df['high'] - df['low']
    df['H-PC'] = abs(df['high'] - df['close'].shift(1))
    df['L-PC'] = abs(df['low'] - df['close'].shift(1))
    df['TR'] = df[['H-L', 'H-PC', 'L-PC']].max(axis=1)
    df['ATR'] = df['TR'].rolling(window=14).mean()
    return df

# Calculate indicators: Moving Averages, RSI, Stochastic Oscillator, and ATR
def calculate_indicators(df):
    df['MA_9'] = df['close'].rolling(window=9).mean()
    df['MA_25'] = df['close'].rolling(window=25).mean()

    delta = df['close'].diff()
    gain = (delta.where(delta > 0, 0)).rolling(window=14).mean()
    loss = (-delta.where(delta < 0, 0)).rolling(window=14).mean()
    rs = gain / loss
    df['RSI'] = 100 - (100 / (1 + rs))

    low_10 = df['low'].rolling(window=10).min()
    high_6 = df['high'].rolling(window=14).max()
    df['%K'] = (df['close'] - low_14) / (high_14 - low_14) * 100
    df['%D'] = df['%K'].rolling(window=3).mean()

    df = calculate_atr(df)  # Add ATR to the dataframe
    return df

# Trading strategy based on indicators
def trading_strategy(df):
    last_row = df.iloc[-1]
    if last_row['MA_9'] > last_row['MA_25'] and last_row['RSI'] > 50 and last_row['%K'] > last_row['%D']:
        return 'BUY'
    elif last_row['MA_9'] < last_row['MA_25'] and last_row['RSI'] < 50 and last_row['%K'] < last_row['%D']:
        return 'SELL'
    else:
        return 'HOLD'

# Dynamic trade duration based on volatility (ATR)
def dynamic_trade_duration(df, max_duration=DURATION_MAX):
    atr = df['ATR'].iloc[-1]
    dynamic_duration = max_duration - int(atr * 100)  # Adjust the multiplier as needed
    return max(30, dynamic_duration)  # Ensure the duration doesn't go below 30 seconds

# Risk management for setting stop-loss and take-profit
def set_risk_levels(entry_price, signal):
    if signal == 'BUY':
        stop_loss = entry_price * (1 - STOP_LOSS_PERCENTAGE)
        take_profit = entry_price * (1 + TAKE_PROFIT_PERCENTAGE)
    elif signal == 'SELL':
        stop_loss = entry_price * (1 + STOP_LOSS_PERCENTAGE)
        take_profit = entry_price * (1 - TAKE_PROFIT_PERCENTAGE)
    return stop_loss, take_profit

# Execute trade based on signal
async def execute_trade(api, signal, symbol, entry_price):
    stop_loss, take_profit = set_risk_levels(entry_price, signal)
    trade_info = {'entry_price': entry_price, 'stop_loss': stop_loss, 'take_profit': take_profit}

    # Record trade info for tracking purposes
    api.active_trades[symbol] = trade_info
    print(f"Initiated {signal} trade for {symbol} at {entry_price} with SL: {stop_loss}, TP: {take_profit}")

    # Calculate dynamic duration
    trade_duration = dynamic_trade_duration(api.data[symbol])

    if signal == 'BUY':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "+0.1", "basis": "payout",
            "contract_type": "CALL", "currency": "USD", "duration": trade_duration, "duration_unit": "s",
            "symbol": symbol
        })
    elif signal == 'SELL':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "-0.1", "basis": "payout",
            "contract_type": "PUT", "currency": "USD", "duration": trade_duration, "duration_unit": "s",
            "symbol": symbol
        })

    if proposal:
        print(f"Trade executed: {signal} at {entry_price}")
        await track_trade(api, symbol, stop_loss, take_profit, trade_duration)

# Track the trade to monitor stop-loss/take-profit conditions
async def track_trade(api, symbol, stop_loss, take_profit, duration):
    start_time = time.time()
    while time.time() - start_time < duration:
        # Monitoring prices for stop-loss and take-profit conditions
        current_price = api.data[symbol].iloc[-1]['close']
        if current_price <= stop_loss or current_price >= take_profit:
            print(f"Trade closed at {current_price} (Stop-Loss or Take-Profit hit)")
            break
        await asyncio.sleep(1)

# Main function to run the bot
async def main():
    api = DerivAPI()
    if not api.connect():
        return

    await api.get_active_symbols()
    
    # Example: Trade for EUR/USD
    symbol = 'EURUSD'
    df = await api.get_candles(symbol, 60, 100)  # 1-minute candles, last 100
    df = calculate_indicators(df)
    
    signal = trading_strategy(df)
    entry_price = df['close'].iloc[-1]

    if signal != 'HOLD':
        await execute_trade(api, signal, symbol, entry_price)

if __name__ == "__main__":
    await (main())


--- request header ---
GET /websockets/v3?app_id=64724 HTTP/1.1
Upgrade: websocket
Host: ws.binaryws.com
Origin: https://ws.binaryws.com
Sec-WebSocket-Key: DEMj9FlhOMjMgO0m3q3joA==
Sec-WebSocket-Version: 13
Connection: Upgrade


-----------------------
--- response header ---
HTTP/1.1 101 Switching Protocols
Date: Tue, 12 Nov 2024 13:23:17 GMT
Content-Length: 0
Connection: upgrade
Sec-WebSocket-Accept: IgANePtUXNiiqtNClYNlP+IkFR0=
Upgrade: websocket
Content-Language: en
CF-Cache-Status: DYNAMIC
Server: cloudflare
CF-RAY: 8e16d5efed7165e5-MBA
alt-svc: h3=":443"; ma=86400
-----------------------
Websocket connected
++Sent raw: b'\x81\xa0Vk\x06\x81-Ig\xf4"\x03i\xf3?\x11c\xa3lK$\xcf\x10[g\xcb\x1d\x1dH\xcbb"n\xca81$\xfc'
++Sent decoded: fin=1 opcode=1 data=b'{"authorize": "NF0aJKvNJ4IhKnZ"}'
++Sent raw: b"\x81\x9a\xd4\xfb\x16\x05\xaf\xd9wf\xa0\x92``\x8b\x88oh\xb6\x94zv\xf6\xc16'\xb2\x8ezi\xf6\x86"
++Sent decoded: fin=1 opcode=1 data=b'{"active_symbols": "full"}'
++Sent raw: b'\x81\xfe\x00\x

WebSocket connection opened
Connected to WebSocket


++Rcv raw: b'\x81~\xac\xef{"active_symbols":[{"allow_forward_starting":0,"delay_amount":0,"display_name":"AUD Basket","display_order":28,"exchange_is_open":1,"exchange_name":"FOREX","intraday_interval_minutes":5,"is_trading_suspended":0,"market":"synthetic_index","market_display_name":"Derived","pip":0.001,"quoted_currency_symbol":"WLDAUD","spot":892.694,"spot_age":"1","spot_percentage_change":"-0.14","spot_time":"1731417780","subgroup":"baskets","subgroup_display_name":"Baskets","submarket":"forex_basket","submarket_display_name":"Forex Basket","symbol":"WLDAUD","symbol_type":"forex_basket"},{"allow_forward_starting":1,"delay_amount":0,"display_name":"AUD\\/CAD","display_order":10,"exchange_is_open":1,"exchange_name":"FOREX","intraday_interval_minutes":5,"is_trading_suspended":0,"market":"forex","market_display_name":"Forex","pip":1e-05,"quoted_currency_symbol":"CAD","spot":0.91311,"spot_age":"0","spot_percentage_change":"-0.29","spot_time":"1731417780","subgroup":"none","subgroup_dis

Active Symbols:
WLDAUD - AUD Basket
frxAUDCAD - AUD/CAD
frxAUDCHF - AUD/CHF
frxAUDJPY - AUD/JPY
frxAUDNZD - AUD/NZD
frxAUDUSD - AUD/USD
OTC_AS51 - Australia 200
cryBTCUSD - BTC/USD
RDBEAR - Bear Market Index
BOOM300N - Boom 300 Index
BOOM500 - Boom 500 Index
BOOM1000 - Boom 1000 Index
RDBULL - Bull Market Index
CRASH300N - Crash 300 Index
CRASH500 - Crash 500 Index
CRASH1000 - Crash 1000 Index
cryETHUSD - ETH/USD
WLDEUR - EUR Basket
frxEURAUD - EUR/AUD
frxEURCAD - EUR/CAD
frxEURCHF - EUR/CHF
frxEURGBP - EUR/GBP
frxEURJPY - EUR/JPY
frxEURNZD - EUR/NZD
frxEURUSD - EUR/USD
OTC_SX5E - Euro 50
OTC_FCHI - France 40
WLDGBP - GBP Basket
frxGBPAUD - GBP/AUD
frxGBPCAD - GBP/CAD
frxGBPCHF - GBP/CHF
frxGBPJPY - GBP/JPY
frxGBPNOK - GBP/NOK
frxGBPNZD - GBP/NZD
frxGBPUSD - GBP/USD
OTC_GDAXI - Germany 40
WLDXAU - Gold Basket
frxXAUUSD - Gold/USD
OTC_HSI - Hong Kong 50
OTC_N225 - Japan 225
JD10 - Jump 10 Index
JD25 - Jump 25 Index
JD50 - Jump 50 Index
JD75 - Jump 75 Index
JD100 - Jump 100 Index
frxNZDJ

TypeError: object NoneType can't be used in 'await' expression

Connection to remote host was lost. - goodbye


Error: Connection to remote host was lost.
WebSocket connection closed


In [ ]:
import websocket
import json
import time
import threading
import pandas as pd
import numpy as np
import asyncio

API_TOKEN = 'NF0aJKvNJ4IhKnZ'
APP_ID = 64724

# Risk management parameters
STOP_LOSS_PERCENTAGE = 0.02  # 2% stop-loss
TAKE_PROFIT_PERCENTAGE = 0.05  # 5% take-profit

class DerivAPI:
    def __init__(self):
        self.ws = None
        self.data = {}
        self.subscribed = False
        self.response = None
        self.active_symbols = []

    def connect(self, retries=3, delay=5):
        attempt = 0
        while attempt < retries:
            try:
                websocket.enableTrace(False)
                self.ws = websocket.WebSocketApp(
                    f"wss://ws.binaryws.com/websockets/v3?app_id={APP_ID}",
                    on_message=self.on_message,
                    on_error=self.on_error,
                    on_close=self.on_close,
                    on_open=self.on_open
                )
                wst = threading.Thread(target=self.ws.run_forever)
                wst.daemon = True
                wst.start()

                conn_timeout = 10
                while not self.ws.sock or not self.ws.sock.connected and conn_timeout:
                    time.sleep(1)
                    conn_timeout -= 1

                if self.ws.sock and self.ws.sock.connected:
                    print("Connected to WebSocket")
                    return True
            except Exception as e:
                print(f"Connection failed: {e}, retrying in {delay} seconds...")
                time.sleep(delay)
                attempt += 1

        print('Failed to connect to WebSocket after retries')
        return False

    def on_message(self, ws, message):
        data = json.loads(message)
        if 'error' in data:
            print(f"Error: {data['error']['message']}")
        elif 'candles' in data:
            symbol = data['echo_req']['ticks_history']
            self.data[symbol] = pd.DataFrame(data['candles'])
            self.data[symbol]['time'] = pd.to_datetime(self.data[symbol]['epoch'], unit='s')
            self.subscribed = True
        elif 'active_symbols' in data:
            self.active_symbols = [symbol['symbol'] for symbol in data['active_symbols']]
            print(f"Active symbols: {self.active_symbols}")
        elif 'proposal' in data:
            self.response = data['proposal']

    def on_error(self, ws, error):
        print(f"Error: {error}")

    def on_close(self, ws, close_status_code, close_msg):
        print("WebSocket connection closed")

    def on_open(self, ws):
        print("WebSocket connection opened")
        self.authorize()

    def authorize(self):
        self.ws.send(json.dumps({"authorize": API_TOKEN}))

    def get_candles(self, symbol, interval, count):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.subscribed = False
        self.ws.send(json.dumps({
            "ticks_history": symbol,
            "adjust_start_time": 1,
            "count": count,
            "end": "latest",
            "start": 1,
            "style": "candles",
            "granularity": interval
        }))

        timeout = 10
        while not self.subscribed and timeout:
            time.sleep(1)
            timeout -= 1

        if not self.subscribed:
            print(f"Failed to receive candle data for symbol: {symbol}")
            return None

        return self.data[symbol]

    async def get_active_symbols(self):
        if not self.ws:
            print("WebSocket is not connected")
            return

        self.ws.send(json.dumps({
            "active_symbols": "full"
        }))

    async def proposal(self, proposal_params):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.response = None
        self.ws.send(json.dumps(proposal_params))

        timeout = 10
        while not self.response and timeout:
            await asyncio.sleep(1)
            timeout -= 1

        if not self.response:
            print("Failed to receive proposal response")
            return None

        return self.response


def calculate_indicators(df):
    df['MA_9'] = df['close'].rolling(window=9).mean()
    df['MA_25'] = df['close'].rolling(window=25).mean()

    delta = df['close'].diff()
    gain = (delta.where(delta > 0, 0)).rolling(window=14).mean()
    loss = (-delta.where(delta < 0, 0)).rolling(window=14).mean()
    rs = gain / loss
    df['RSI'] = 100 - (100 / (1 + rs))

    low_14 = df['low'].rolling(window=14).min()
    high_14 = df['high'].rolling(window=14).max()
    df['%K'] = (df['close'] - low_14) / (high_14 - low_14) * 100
    df['%D'] = df['%K'].rolling(window=3).mean()

    return df


def trading_strategy(df):
    last_row = df.iloc[-1]
    if last_row['MA_9'] > last_row['MA_25'] and last_row['RSI'] > 50 and last_row['%K'] > last_row['%D']:
        return 'BUY'
    elif last_row['MA_9'] < last_row['MA_25'] and last_row['RSI'] < 50 and last_row['%K'] < last_row['%D']:
        return 'SELL'
    else:
        return 'HOLD'


def determine_trade_duration(df):
    """Determine the trade duration dynamically based on market conditions."""
    volatility = df['close'].std()
    if volatility > 1:
        return 300  # 5 minutes for high volatility
    else:
        return 60  # 1 minute for low volatility


async def execute_trade(api, signal, symbol, entry_price, duration):
    stop_loss, take_profit = set_risk_levels(entry_price, signal)
    print(f"Initiating {signal} trade for {symbol} at {entry_price} with SL: {stop_loss}, TP: {take_profit}, Duration: {duration}s")

    proposal_params = {
        "proposal": 1,
        "amount": 100,
        "basis": "payout",
        "contract_type": "CALL" if signal == "BUY" else "PUT",
        "currency": "USD",
        "duration": duration,
        "duration_unit": "s",
        "symbol": symbol
    }

    proposal = await api.proposal(proposal_params)
    if proposal and 'id' in proposal:
        proposal_id = proposal['id']
        api.ws.send(json.dumps({"buy": proposal_id, "price": 100}))
        print(f"Trade executed with proposal ID: {proposal_id}")
    else:
        print(f"Failed to execute {signal} trade for {symbol}")


async def main():
    api = DerivAPI()
    if not api.connect():
        return

    await api.get_active_symbols()
    valid_symbols = api.active_symbols
    if not valid_symbols:
        print("No valid symbols available.")
        return

    symbol = valid_symbols[0]
    df = api.get_candles(symbol, 60, 100)
    if df is None:
        print(f"Failed to retrieve data for {symbol}.")
        return

    df = calculate_indicators(df)
    signal = trading_strategy(df)
    entry_price = df['close'].iloc[-1]

    if signal != 'HOLD':
        duration = determine_trade_duration(df)
        await execute_trade(api, signal, symbol, entry_price, duration)


if __name__ == "__main__":
    await (main())


Websocket connected


WebSocket connection opened
Connected to WebSocket
No valid symbols available.


Active symbols: ['WLDAUD', 'frxAUDCAD', 'frxAUDCHF', 'frxAUDJPY', 'frxAUDNZD', 'frxAUDUSD', 'OTC_AS51', 'cryBTCUSD', 'RDBEAR', 'BOOM300N', 'BOOM500', 'BOOM1000', 'RDBULL', 'CRASH300N', 'CRASH500', 'CRASH1000', 'cryETHUSD', 'WLDEUR', 'frxEURAUD', 'frxEURCAD', 'frxEURCHF', 'frxEURGBP', 'frxEURJPY', 'frxEURNZD', 'frxEURUSD', 'OTC_SX5E', 'OTC_FCHI', 'WLDGBP', 'frxGBPAUD', 'frxGBPCAD', 'frxGBPCHF', 'frxGBPJPY', 'frxGBPNOK', 'frxGBPNZD', 'frxGBPUSD', 'OTC_GDAXI', 'WLDXAU', 'frxXAUUSD', 'OTC_HSI', 'OTC_N225', 'JD10', 'JD25', 'JD50', 'JD75', 'JD100', 'frxNZDJPY', 'frxNZDUSD', 'OTC_AEX', 'frxXPDUSD', 'frxXPTUSD', 'frxXAGUSD', 'stpRNG', 'stpRNG2', 'stpRNG3', 'stpRNG4', 'stpRNG5', 'OTC_SSMI', 'OTC_FTSE', 'OTC_SPC', 'OTC_NDX', 'WLDUSD', 'frxUSDCAD', 'frxUSDCHF', 'frxUSDJPY', 'frxUSDMXN', 'frxUSDNOK', 'frxUSDPLN', 'frxUSDSEK', '1HZ10V', 'R_10', '1HZ25V', 'R_25', '1HZ50V', 'R_50', '1HZ75V', 'R_75', '1HZ100V', 'R_100', '1HZ150V', '1HZ250V', 'OTC_DJI']


Connection to remote host was lost. - goodbye


Error: Connection to remote host was lost.
WebSocket connection closed


In [ ]:
import websocket
import json
import time
import threading
import pandas as pd
import numpy as np
import asyncio

API_TOKEN = 'NF0aJKvNJ4IhKnZ'
APP_ID = 64724

# Risk management parameters
STOP_LOSS_PERCENTAGE = 0.02  # 2% stop-loss
TAKE_PROFIT_PERCENTAGE = 0.05  # 5% take-profit

class DerivAPI:
    def __init__(self):
        self.ws = None
        self.data = {}
        self.subscribed = False
        self.response = None
        self.active_symbols = []

    def connect(self, retries=3, delay=5):
        attempt = 0
        while attempt < retries:
            try:
                websocket.enableTrace(False)
                self.ws = websocket.WebSocketApp(
                    f"wss://ws.binaryws.com/websockets/v3?app_id={APP_ID}",
                    on_message=self.on_message,
                    on_error=self.on_error,
                    on_close=self.on_close,
                    on_open=self.on_open
                )
                wst = threading.Thread(target=self.ws.run_forever)
                wst.daemon = True
                wst.start()

                conn_timeout = 10
                while not self.ws.sock or not self.ws.sock.connected and conn_timeout:
                    time.sleep(1)
                    conn_timeout -= 1

                if self.ws.sock and self.ws.sock.connected:
                    print("Connected to WebSocket")
                    return True
            except Exception as e:
                print(f"Connection failed: {e}, retrying in {delay} seconds...")
                time.sleep(delay)
                attempt += 1

        print('Failed to connect to WebSocket after retries')
        return False

    def on_message(self, ws, message):
        data = json.loads(message)
        if 'error' in data:
            print(f"Error: {data['error']['message']}")
        elif 'candles' in data:
            symbol = data['echo_req']['ticks_history']
            self.data[symbol] = pd.DataFrame(data['candles'])
            self.data[symbol]['time'] = pd.to_datetime(self.data[symbol]['epoch'], unit='s')
            self.subscribed = True
        elif 'proposal' in data:
            self.response = data['proposal']
        elif 'active_symbols' in data:
            self.active_symbols = [symbol['symbol'] for symbol in data['active_symbols']]
        print(f"Received data: {data}")

    def on_error(self, ws, error):
        print(f"Error: {error}")

    def on_close(self, ws, close_status_code, close_msg):
        print("WebSocket connection closed")

    def on_open(self, ws):
        print("WebSocket connection opened")
        self.authorize()

    def authorize(self):
        self.ws.send(json.dumps({"authorize": API_TOKEN}))

    def get_candles(self, symbol, interval, count):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.subscribed = False
        self.ws.send(json.dumps({
            "ticks_history": symbol,
            "adjust_start_time": 1,
            "count": count,
            "end": "latest",
            "start": 1,
            "style": "candles",
            "granularity": interval
        }))

        timeout = 10
        while not self.subscribed and timeout:
            time.sleep(1)
            timeout -= 1

        if not self.subscribed:
            print(f"Failed to receive candle data for symbol: {symbol}")
            return None

        return self.data[symbol]

    async def get_active_symbols(self):
        if not self.ws:
            print("WebSocket is not connected")
            return

        self.ws.send(json.dumps({
            "active_symbols": "full"
        }))

    async def proposal(self, proposal_params):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.response = None
        self.ws.send(json.dumps(proposal_params))

        timeout = 10
        while not self.response and timeout:
            await asyncio.sleep(1)
            timeout -= 1

        if not self.response:
            print("Failed to receive proposal response")
            return None

        return self.response


def calculate_indicators(df):
    df['MA_9'] = df['close'].rolling(window=9).mean()
    df['MA_25'] = df['close'].rolling(window=25).mean()

    delta = df['close'].diff()
    gain = (delta.where(delta > 0, 0)).rolling(window=14).mean()
    loss = (-delta.where(delta < 0, 0)).rolling(window=14).mean()
    rs = gain / loss
    df['RSI'] = 100 - (100 / (1 + rs))

    low_14 = df['low'].rolling(window=14).min()
    high_14 = df['high'].rolling(window=14).max()
    df['%K'] = (df['close'] - low_14) / (high_14 - low_14) * 100
    df['%D'] = df['%K'].rolling(window=3).mean()

    return df


def trading_strategy(df):
    last_row = df.iloc[-1]
    if last_row['MA_9'] > last_row['MA_25'] and last_row['RSI'] > 50 and last_row['%K'] > last_row['%D']:
        return 'BUY'
    elif last_row['MA_9'] < last_row['MA_25'] and last_row['RSI'] < 50 and last_row['%K'] < last_row['%D']:
        return 'SELL'
    else:
        return 'HOLD'


def determine_trade_duration(df):
    volatility = df['close'].pct_change().std()
    if volatility < 0.005:
        return 60  # 1 minute
    elif volatility < 0.01:
        return 300  # 5 minutes
    else:
        return 900  # 15 minutes


def set_risk_levels(entry_price, signal):
    if signal == 'BUY':
        stop_loss = entry_price * (1 - STOP_LOSS_PERCENTAGE)
        take_profit = entry_price * (1 + TAKE_PROFIT_PERCENTAGE)
    elif signal == 'SELL':
        stop_loss = entry_price * (1 + STOP_LOSS_PERCENTAGE)
        take_profit = entry_price * (1 - TAKE_PROFIT_PERCENTAGE)
    return stop_loss, take_profit


async def execute_trade(api, signal, symbol, entry_price, duration):
    stop_loss, take_profit = set_risk_levels(entry_price, signal)
    print(f"Initiating {signal} trade for {symbol} at {entry_price} with SL: {stop_loss}, TP: {take_profit}, Duration: {duration} seconds")

    if signal == 'BUY':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "+0.1", "basis": "payout",
            "contract_type": "CALL", "currency": "USD", "duration": duration, "duration_unit": "s",
            "symbol": symbol
        })
    elif signal == 'SELL':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "-0.1", "basis": "payout",
            "contract_type": "PUT", "currency": "USD", "duration": duration, "duration_unit": "s",
            "symbol": symbol
        })

    if proposal and 'id' in proposal:
        proposal_id = proposal['id']
        api.ws.send(json.dumps({"buy": proposal_id, "price": 100}))
        print(f"Executed {signal} trade for {symbol} with proposal ID: {proposal_id}")
    else:
        print(f"Failed to execute {signal} trade for {symbol}")


async def main():
    api = DerivAPI()
    if not api.connect():
        return

    await api.get_active_symbols()
    valid_symbols = [symbol for symbol in api.active_symbols if symbol.startswith('frx')]
    if not valid_symbols:
        print("No valid forex symbols available.")
        return

    print(f"Selected symbol: {valid_symbols[0]}")
    symbol = valid_symbols[0]

    candles = api.get_candles(symbol, 60, 100)
    if candles is None:
        print(f"Failed to retrieve data for {symbol}.")
        return

    df = calculate_indicators(candles)
    signal = trading_strategy(df)
    entry_price = df['close'].iloc[-1]

    if signal != 'HOLD':
        duration = determine_trade_duration(df)
        await execute_trade(api, signal, symbol, entry_price, duration)


if __name__ == "__main__":
    await (main())


Websocket connected


WebSocket connection opened
Connected to WebSocket
No valid forex symbols available.


Received data: {'active_symbols': [{'allow_forward_starting': 0, 'delay_amount': 0, 'display_name': 'AUD Basket', 'display_order': 28, 'exchange_is_open': 1, 'exchange_name': 'FOREX', 'intraday_interval_minutes': 5, 'is_trading_suspended': 0, 'market': 'synthetic_index', 'market_display_name': 'Derived', 'pip': 0.001, 'quoted_currency_symbol': 'WLDAUD', 'spot': 892.958, 'spot_age': '0', 'spot_percentage_change': '-0.11', 'spot_time': '1731418710', 'subgroup': 'baskets', 'subgroup_display_name': 'Baskets', 'submarket': 'forex_basket', 'submarket_display_name': 'Forex Basket', 'symbol': 'WLDAUD', 'symbol_type': 'forex_basket'}, {'allow_forward_starting': 1, 'delay_amount': 0, 'display_name': 'AUD/CAD', 'display_order': 10, 'exchange_is_open': 1, 'exchange_name': 'FOREX', 'intraday_interval_minutes': 5, 'is_trading_suspended': 0, 'market': 'forex', 'market_display_name': 'Forex', 'pip': 1e-05, 'quoted_currency_symbol': 'CAD', 'spot': 0.91306, 'spot_age': '0', 'spot_percentage_change': '-0

Connection to remote host was lost. - goodbye


Error: Connection to remote host was lost.
WebSocket connection closed


In [ ]:
import websocket
import json
import time
import threading
import pandas as pd
import numpy as np
import asyncio

API_TOKEN = 'NF0aJKvNJ4IhKnZ'
APP_ID = 64724

# Risk management parameters
STOP_LOSS_PERCENTAGE = 0.01
TAKE_PROFIT_PERCENTAGE = 0.03

class DerivAPI:
    def __init__(self):
        self.ws = None
        self.data = {}
        self.subscribed = False
        self.response = None
        self.active_trades = {}

    def connect(self, retries=3, delay=5):
        attempt = 0
        while attempt < retries:
            try:
                websocket.enableTrace(True)
                self.ws = websocket.WebSocketApp(
                    f"wss://ws.binaryws.com/websockets/v3?app_id={APP_ID}",
                    on_message=self.on_message,
                    on_error=self.on_error,
                    on_close=self.on_close,
                    on_open=self.on_open
                )
                wst = threading.Thread(target=self.ws.run_forever)
                wst.daemon = True
                wst.start()

                conn_timeout = 10
                while not self.ws.sock or not self.ws.sock.connected and conn_timeout:
                    time.sleep(1)
                    conn_timeout -= 1

                if self.ws.sock and self.ws.sock.connected:
                    print("Connected to WebSocket")
                    return True
            except Exception as e:
                print(f"Connection failed: {e}, retrying in {delay} seconds...")
                time.sleep(delay)
                attempt += 1

        print('Failed to connect to WebSocket after retries')
        return False

    def on_message(self, ws, message):
        data = json.loads(message)
        if 'error' in data:
            print(f"Error: {data['error']['message']}")
        elif 'candles' in data:
            symbol = data['echo_req']['ticks_history']
            self.data[symbol] = pd.DataFrame(data['candles'])
            self.data[symbol]['time'] = pd.to_datetime(self.data[symbol]['epoch'], unit='s')
            self.subscribed = True
        elif 'proposal' in data:
            self.response = data['proposal']
        elif 'active_symbols' in data:
            print("Active Symbols:")
            for symbol in data['active_symbols']:
                print(symbol['symbol'], "-", symbol['display_name'])
        print(f"Received data: {data}")

    def on_error(self, ws, error):
        print(f"Error: {error}")

    def on_close(self, ws, close_status_code, close_msg):
        print("WebSocket connection closed")

    def on_open(self, ws):
        print("WebSocket connection opened")
        self.authorize()

    def authorize(self):
        self.ws.send(json.dumps({"authorize": API_TOKEN}))

    def get_candles(self, symbol, interval, count):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.subscribed = False
        self.ws.send(json.dumps({
            "ticks_history": symbol,
            "adjust_start_time": 1,
            "count": count,
            "end": "latest",
            "start": 1,
            "style": "candles",
            "granularity": interval
        }))

        timeout = 10
        while not self.subscribed and timeout:
            time.sleep(1)
            timeout -= 1

        if not self.subscribed:
            print("Failed to receive candle data for symbol:", symbol)
            return None

        return self.data[symbol]

    async def get_active_symbols(self):
        if not self.ws:
            print("WebSocket is not connected")
            return

        self.ws.send(json.dumps({
            "active_symbols": "full"
        }))

    async def proposal(self, proposal_params):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.response = None
        self.ws.send(json.dumps(proposal_params))

        timeout = 10
        while not self.response and timeout:
            await asyncio.sleep(1)
            timeout -= 1

        if not self.response:
            print("Failed to receive proposal response")
            return None

        return self.response

def calculate_indicators(df):
    df['MA_9'] = df['close'].rolling(window=9).mean()
    df['MA_25'] = df['close'].rolling(window=25).mean()

    delta = df['close'].diff()
    gain = (delta.where(delta > 0, 0)).rolling(window=14).mean()
    loss = (-delta.where(delta < 0, 0)).rolling(window=14).mean()
    rs = gain / loss
    df['RSI'] = 100 - (100 / (1 + rs))

    low_k = df['low'].rolling(window=10).min()
    high_k = df['high'].rolling(window=10).max()
    df['%K'] = (df['close'] - low_k) / (high_k - low_k) * 100
    df['%D'] = df['%K'].rolling(window=6).mean()

    return df

def trading_strategy(df):
    last_row = df.iloc[-1]
    if last_row['MA_9'] > last_row['MA_25'] and last_row['RSI'] > 50 and last_row['%K'] > last_row['%D']:
        return 'BUY'
    elif last_row['MA_9'] < last_row['MA_25'] and last_row['RSI'] < 50 and last_row['%K'] < last_row['%D']:
        return 'SELL'
    else:
        return 'HOLD'

def set_risk_levels(entry_price, signal):
    if signal == 'BUY':
        stop_loss = entry_price * (1 - STOP_LOSS_PERCENTAGE)
        take_profit = entry_price * (1 + TAKE_PROFIT_PERCENTAGE)
    elif signal == 'SELL':
        stop_loss = entry_price * (1 + STOP_LOSS_PERCENTAGE)
        take_profit = entry_price * (1 - TAKE_PROFIT_PERCENTAGE)
    return stop_loss, take_profit

def get_dynamic_duration(df):
    # Example dynamic duration based on volatility (standard deviation of close prices)
    volatility = df['close'].rolling(window=10).std().iloc[-1]
    duration = max(30, min(120, int(volatility * 100)))
    return duration

async def execute_trade(api, signal, symbol, entry_price):
    stop_loss, take_profit = set_risk_levels(entry_price, signal)
    trade_info = {'entry_price': entry_price, 'stop_loss': stop_loss, 'take_profit': take_profit}

    # Record trade info for tracking purposes
    api.active_trades[symbol] = trade_info
    print(f"Initiated {signal} trade for {symbol} at {entry_price} with SL: {stop_loss}, TP: {take_profit}")

    candles = api.get_candles(symbol, 60, 100)
    duration = get_dynamic_duration(candles)

    if signal == 'BUY':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "+0.1", "basis": "payout",
            "contract_type": "CALL", "currency": "USD", "duration": duration, "duration_unit": "s",
            "symbol": symbol
        })
    elif signal == 'SELL':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "-0.1", "basis": "payout",
            "contract_type": "PUT", "currency": "USD", "duration": duration, "duration_unit": "s",
            "symbol": symbol
        })

    if proposal and 'id' in proposal:
        proposal_id = proposal['id']
        api.ws.send(json.dumps({"buy": proposal_id, "price": 100}))
        print(f"Executed {signal} trade for {symbol} with proposal ID: {proposal_id}")
    else:
        print(f"Failed to execute {signal} trade for {symbol}")

async def main():
    deriv_api = DerivAPI()
    if not deriv_api.connect():
        return

    await deriv_api.get_active_symbols()  # Fetch and print all active symbols

    symbols = ['R_100', 'R_50', 'R_75']  # List of symbols to analyze
    interval = 60
    count = 100

    while True:
        for symbol in symbols:
            candles = deriv_api.get_candles(symbol, interval, count)
            if candles is not None:
                df = calculate_indicators(candles)
                signal = trading_strategy(df)
                print(f"Current signal for {symbol}: {signal}")

                # Example entry price from the last close price (for demonstration)
                entry_price = df['close'].iloc[-1]

                if signal in ['BUY', 'SELL']:
                    await execute_trade(deriv_api, signal, symbol, entry_price)
            else:
                print(f"Failed to retrieve candle data for {symbol}")

        time.sleep(60)

if __name__ == "__main__":
    await (main())


--- request header ---
GET /websockets/v3?app_id=64724 HTTP/1.1
Upgrade: websocket
Host: ws.binaryws.com
Origin: https://ws.binaryws.com
Sec-WebSocket-Key: ogxZbNDfRLQhZVmu+CcZLg==
Sec-WebSocket-Version: 13
Connection: Upgrade


-----------------------
--- response header ---
HTTP/1.1 101 Switching Protocols
Date: Tue, 12 Nov 2024 13:51:13 GMT
Content-Length: 0
Connection: upgrade
Sec-WebSocket-Accept: wxTMCJD7j/y0EbabKdhcZZqfD3A=
Upgrade: websocket
Content-Language: en
CF-Cache-Status: DYNAMIC
Server: cloudflare
CF-RAY: 8e16fed778d365ec-MBA
alt-svc: h3=":443"; ma=86400
-----------------------
Websocket connected
++Sent raw: b'\x81\xa0k\xc4\xea\xb7\x10\xe6\x8b\xc2\x1f\xac\x85\xc5\x02\xbe\x8f\x95Q\xe4\xc8\xf9-\xf4\x8b\xfd \xb2\xa4\xfd_\x8d\x82\xfc\x05\x9e\xc8\xca'
++Sent decoded: fin=1 opcode=1 data=b'{"authorize": "NF0aJKvNJ4IhKnZ"}'
++Sent raw: b'\x81\x9a\xc6\x02\x0c\x8b\xbd m\xe8\xb2kz\xee\x99qu\xe6\xa4m`\xf8\xe48,\xa9\xa0w`\xe7\xe4\x7f'
++Sent decoded: fin=1 opcode=1 data=b'{"active

WebSocket connection opened
Connected to WebSocket


++Rcv raw: b'\x81~\xac\xec{"active_symbols":[{"allow_forward_starting":0,"delay_amount":0,"display_name":"AUD Basket","display_order":28,"exchange_is_open":1,"exchange_name":"FOREX","intraday_interval_minutes":5,"is_trading_suspended":0,"market":"synthetic_index","market_display_name":"Derived","pip":0.001,"quoted_currency_symbol":"WLDAUD","spot":892.691,"spot_age":"0","spot_percentage_change":"-0.14","spot_time":"1731419460","subgroup":"baskets","subgroup_display_name":"Baskets","submarket":"forex_basket","submarket_display_name":"Forex Basket","symbol":"WLDAUD","symbol_type":"forex_basket"},{"allow_forward_starting":1,"delay_amount":0,"display_name":"AUD\\/CAD","display_order":10,"exchange_is_open":1,"exchange_name":"FOREX","intraday_interval_minutes":5,"is_trading_suspended":0,"market":"forex","market_display_name":"Forex","pip":1e-05,"quoted_currency_symbol":"CAD","spot":0.91241,"spot_age":"0","spot_percentage_change":"-0.37","spot_time":"1731419460","subgroup":"none","subgroup_dis

Active Symbols:
WLDAUD - AUD Basket
frxAUDCAD - AUD/CAD
frxAUDCHF - AUD/CHF
frxAUDJPY - AUD/JPY
frxAUDNZD - AUD/NZD
frxAUDUSD - AUD/USD
OTC_AS51 - Australia 200
cryBTCUSD - BTC/USD
RDBEAR - Bear Market Index
BOOM300N - Boom 300 Index
BOOM500 - Boom 500 Index
BOOM1000 - Boom 1000 Index
RDBULL - Bull Market Index
CRASH300N - Crash 300 Index
CRASH500 - Crash 500 Index
CRASH1000 - Crash 1000 Index
cryETHUSD - ETH/USD
WLDEUR - EUR Basket
frxEURAUD - EUR/AUD
frxEURCAD - EUR/CAD
frxEURCHF - EUR/CHF
frxEURGBP - EUR/GBP
frxEURJPY - EUR/JPY
frxEURNZD - EUR/NZD
frxEURUSD - EUR/USD
OTC_SX5E - Euro 50
OTC_FCHI - France 40
WLDGBP - GBP Basket
frxGBPAUD - GBP/AUD
frxGBPCAD - GBP/CAD
frxGBPCHF - GBP/CHF
frxGBPJPY - GBP/JPY
frxGBPNOK - GBP/NOK
frxGBPNZD - GBP/NZD
frxGBPUSD - GBP/USD
OTC_GDAXI - Germany 40
WLDXAU - Gold Basket
frxXAUUSD - Gold/USD
OTC_HSI - Hong Kong 50
OTC_N225 - Japan 225
JD10 - Jump 10 Index
JD25 - Jump 25 Index
JD50 - Jump 50 Index
JD75 - Jump 75 Index
JD100 - Jump 100 Index
frxNZDJ

++Rcv raw: b'\x81~\x05\xc2{"authorize":{"account_list":[{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1710220418,"currency":"USD","currency_type":"fiat","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR6779028"},{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1709901738,"currency":"BTC","currency_type":"crypto","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR6763883"},{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1721128861,"currency":"tUSDT","currency_type":"crypto","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR7371492"},{"account_category":"trading","account_type":"binary","broker":"VRTC","created_at":1709898717,"currency":"USD","currency_type":"fiat","is_disabled":0,"is_virtual":1,"landing_company_name":"virtual","linked_to":[],"loginid":"VRTC10086060"}],"balance

...

Received data: {'echo_req': {'amount': 100, 'barrier': '+0.1', 'basis': 'payout', 'contract_type': 'CALL', 'currency': 'USD', 'duration': 120, 'duration_unit': 's', 'product_type': 'basic', 'proposal': 1, 'symbol': 'R_75'}, 'msg_type': 'proposal', 'proposal': {'ask_price': 51.14, 'contract_details': {'barrier': '91383.1418'}, 'date_expiry': 1731420439, 'date_start': 1731420319, 'display_value': '51.14', 'id': '212a6aa8-4e11-cfa8-0cc1-f0b5663f31fc', 'longcode': 'Win payout if Volatility 75 Index is strictly higher than entry spot plus 0.1000 at 2 minutes after contract start time.', 'payout': 100, 'spot': 91383.0418, 'spot_time': 1731420318, 'validation_params': {'payout': {'max': '50000.00'}, 'stake': {'min': '0.35'}}}}


++Sent raw: b'\x81\xbd\xf5\xf3"\xac\x8e\xd1@\xd9\x8c\xd1\x18\x8c\xd7\xc1\x13\x9e\x94\xc5C\xcd\xcd\xde\x16\xc9\xc4\xc2\x0f\xcf\x93\x92\x1a\x81\xc5\x90A\x9d\xd8\x95\x12\xce\xc0\xc5\x14\x9f\x93\xc0\x13\xca\x96\xd1\x0e\x8c\xd7\x83P\xc5\x96\x96\x00\x96\xd5\xc2\x12\x9c\x88'
++Sent decoded: fin=1 opcode=1 data=b'{"buy": "212a6aa8-4e11-cfa8-0cc1-f0b5663f31fc", "price": 100}'


Executed BUY trade for R_75 with proposal ID: 212a6aa8-4e11-cfa8-0cc1-f0b5663f31fc


++Rcv raw: b'\x81~\x01\xc7{"buy":{"balance_after":9495.74,"buy_price":51.14,"contract_id":262822790468,"longcode":"Win payout if Volatility 75 Index is strictly higher than entry spot plus 0.1000 at 2 minutes after contract start time.","payout":100,"purchase_time":1731420320,"shortcode":"CALL_R_75_100.00_1731420320_1731420440_S1000P_0","start_time":1731420320,"transaction_id":523958024408},"echo_req":{"buy":"212a6aa8-4e11-cfa8-0cc1-f0b5663f31fc","price":100},"msg_type":"buy"}'
++Rcv decoded: fin=1 opcode=1 data=b'{"buy":{"balance_after":9495.74,"buy_price":51.14,"contract_id":262822790468,"longcode":"Win payout if Volatility 75 Index is strictly higher than entry spot plus 0.1000 at 2 minutes after contract start time.","payout":100,"purchase_time":1731420320,"shortcode":"CALL_R_75_100.00_1731420320_1731420440_S1000P_0","start_time":1731420320,"transaction_id":523958024408},"echo_req":{"buy":"212a6aa8-4e11-cfa8-0cc1-f0b5663f31fc","price":100},"msg_type":"buy"}'


Received data: {'buy': {'balance_after': 9495.74, 'buy_price': 51.14, 'contract_id': 262822790468, 'longcode': 'Win payout if Volatility 75 Index is strictly higher than entry spot plus 0.1000 at 2 minutes after contract start time.', 'payout': 100, 'purchase_time': 1731420320, 'shortcode': 'CALL_R_75_100.00_1731420320_1731420440_S1000P_0', 'start_time': 1731420320, 'transaction_id': 523958024408}, 'echo_req': {'buy': '212a6aa8-4e11-cfa8-0cc1-f0b5663f31fc', 'price': 100}, 'msg_type': 'buy'}


In [ ]:
import websocket
import json
import time
import threading
import pandas as pd
import numpy as np
import asyncio
import random

API_TOKEN = 'NF0aJKvNJ4IhKnZ'
APP_ID = 64724

# Risk management parameters
STOP_LOSS_PERCENTAGE = 0.01  # 1% stop-loss
TAKE_PROFIT_PERCENTAGE = 0.03  # 3% take-profit

class DerivAPI:
    def __init__(self):
        self.ws = None
        self.data = {}
        self.subscribed = False
        self.response = None
        self.active_trades = {}
        self.active_symbols = []

    def connect(self, retries=3, delay=5):
        attempt = 0
        while attempt < retries:
            try:
                websocket.enableTrace(True)
                self.ws = websocket.WebSocketApp(
                    f"wss://ws.binaryws.com/websockets/v3?app_id={APP_ID}",
                    on_message=self.on_message,
                    on_error=self.on_error,
                    on_close=self.on_close,
                    on_open=self.on_open
                )
                wst = threading.Thread(target=self.ws.run_forever)
                wst.daemon = True
                wst.start()

                conn_timeout = 10
                while not self.ws.sock or not self.ws.sock.connected and conn_timeout:
                    time.sleep(1)
                    conn_timeout -= 1

                if self.ws.sock and self.ws.sock.connected:
                    print("Connected to WebSocket")
                    return True
            except Exception as e:
                print(f"Connection failed: {e}, retrying in {delay} seconds...")
                time.sleep(delay)
                attempt += 1

        print('Failed to connect to WebSocket after retries')
        return False

    def on_message(self, ws, message):
        data = json.loads(message)
        if 'error' in data:
            print(f"Error: {data['error']['message']}")
        elif 'candles' in data:
            symbol = data['echo_req']['ticks_history']
            self.data[symbol] = pd.DataFrame(data['candles'])
            self.data[symbol]['time'] = pd.to_datetime(self.data[symbol]['epoch'], unit='s')
            self.subscribed = True
        elif 'proposal' in data:
            self.response = data['proposal']
        elif 'active_symbols' in data:
            self.active_symbols = [symbol['symbol'] for symbol in data['active_symbols']]
            print("Active Symbols:")
            print(self.active_symbols)

    def on_error(self, ws, error):
        print(f"Error: {error}")

    def on_close(self, ws, close_status_code, close_msg):
        print("WebSocket connection closed")

    def on_open(self, ws):
        print("WebSocket connection opened")
        self.authorize()

    def authorize(self):
        self.ws.send(json.dumps({"authorize": API_TOKEN}))

    def get_candles(self, symbol, interval, count):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.subscribed = False
        self.ws.send(json.dumps({
            "ticks_history": symbol,
            "adjust_start_time": 1,
            "count": count,
            "end": "latest",
            "start": 1,
            "style": "candles",
            "granularity": interval
        }))

        timeout = 10
        while not self.subscribed and timeout:
            time.sleep(1)
            timeout -= 1

        if not self.subscribed:
            print(f"Failed to receive candle data for symbol: {symbol}")
            return None

        return self.data[symbol]

    async def proposal(self, proposal_params):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.response = None
        self.ws.send(json.dumps(proposal_params))

        timeout = 10
        while not self.response and timeout:
            await asyncio.sleep(1)
            timeout -= 1

        if not self.response:
            print("Failed to receive proposal response")
            return None

        return self.response

def calculate_indicators(df):
    df['MA_9'] = df['close'].rolling(window=9).mean()
    df['MA_25'] = df['close'].rolling(window=25).mean()

    # RSI
    delta = df['close'].diff()
    gain = (delta.where(delta > 0, 0)).rolling(window=14).mean()
    loss = (-delta.where(delta < 0, 0)).rolling(window=14).mean()
    rs = gain / loss
    df['RSI'] = 100 - (100 / (1 + rs))

    # Stochastic Oscillator (10, 6, 6)
    low_14 = df['low'].rolling(window=10).min()
    high_14 = df['high'].rolling(window=10).max()
    df['%K'] = (df['close'] - low_14) / (high_14 - low_14) * 100
    df['%D'] = df['%K'].rolling(window=6).mean()

    return df

def trading_strategy(df):
    last_row = df.iloc[-1]
    if last_row['MA_9'] > last_row['MA_25'] and last_row['RSI'] > 50 and last_row['%K'] > last_row['%D']:
        return 'BUY'
    elif last_row['MA_9'] < last_row['MA_25'] and last_row['RSI'] < 50 and last_row['%K'] < last_row['%D']:
        return 'SELL'
    else:
        return 'HOLD'

def set_risk_levels(entry_price, signal):
    if signal == 'BUY':
        stop_loss = entry_price * (1 - STOP_LOSS_PERCENTAGE)
        take_profit = entry_price * (1 + TAKE_PROFIT_PERCENTAGE)
    elif signal == 'SELL':
        stop_loss = entry_price * (1 + STOP_LOSS_PERCENTAGE)
        take_profit = entry_price * (1 - TAKE_PROFIT_PERCENTAGE)
    return stop_loss, take_profit

def calculate_dynamic_duration(df):
    """Calculate dynamic duration based on market conditions"""
    # Example: If the RSI is above 70 or below 30, trade duration can be longer (trend is stronger)
    if df['RSI'].iloc[-1] > 70 or df['RSI'].iloc[-1] < 30:
        return 120  # Longer duration if RSI indicates overbought or oversold condition
    else:
        return 60  # Standard duration otherwise

async def execute_trade(api, signal, symbol, entry_price, df):
    stop_loss, take_profit = set_risk_levels(entry_price, signal)
    trade_info = {'entry_price': entry_price, 'stop_loss': stop_loss, 'take_profit': take_profit}

    # Record trade info for tracking purposes
    api.active_trades[symbol] = trade_info
    print(f"Initiated {signal} trade for {symbol} at {entry_price} with SL: {stop_loss}, TP: {take_profit}")

    duration = calculate_dynamic_duration(df)  # Dynamically calculate trade duration based on market conditions

    if signal == 'BUY':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "+0.1", "basis": "payout",
            "contract_type": "CALL", "currency": "USD", "duration": duration, "duration_unit": "s",
            "symbol": symbol
        })
    elif signal == 'SELL':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "-0.1", "basis": "payout",
            "contract_type": "PUT", "currency": "USD", "duration": duration, "duration_unit": "s",
            "symbol": symbol
        })

    if proposal and 'id' in proposal:
        proposal_id = proposal['id']
        api.ws.send(json.dumps({"buy": proposal_id, "price": 100}))
        print(f"Executed {signal} trade for {symbol} with proposal ID: {proposal_id}")
    else:
        print(f"Failed to execute {signal} trade for {symbol}")

async def main():
    deriv_api = DerivAPI()
    if not deriv_api.connect():
        return

    await deriv_api.get_active_symbols()  # Fetch and print all active symbols

    while True:
        symbol = random.choice(deriv_api.active_symbols)  # Randomly select a symbol to trade
        print(f"Selected symbol: {symbol}")

        interval = 60
        count = 100
        candles = deriv_api.get_candles(symbol, interval, count)
        if candles is not None:
            df = calculate_indicators(candles)
            signal = trading_strategy(df)
            print(f"Current signal for {symbol}: {signal}")

            # Example entry price from the last close price (for demonstration)
            entry_price = df['close'].iloc[-1]

            if signal in ['BUY', 'SELL']:
                await execute_trade(deriv_api, signal, symbol, entry_price, df)
        else:
            print(f"Failed to retrieve candle data for {symbol}")

        time.sleep(5)

if __name__ == "__main__":
    await (main())


--- request header ---
GET /websockets/v3?app_id=64724 HTTP/1.1
Upgrade: websocket
Host: ws.binaryws.com
Origin: https://ws.binaryws.com
Sec-WebSocket-Key: d9vk/OAOG1mbsalDao06TA==
Sec-WebSocket-Version: 13
Connection: Upgrade


-----------------------
--- response header ---
HTTP/1.1 101 Switching Protocols
Date: Tue, 12 Nov 2024 14:06:42 GMT
Content-Length: 0
Connection: upgrade
Content-Language: en
Upgrade: websocket
Sec-WebSocket-Accept: Bb+4aGcaK1WcogWZsCmM9dPaelo=
CF-Cache-Status: DYNAMIC
Server: cloudflare
CF-RAY: 8e17158a69c665e7-MBA
alt-svc: h3=":443"; ma=86400
-----------------------
Websocket connected
++Sent raw: b'\x81\xa0B,"\xa69\x0eC\xd36DM\xd4+VG\x84x\x0c\x00\xe8\x04\x1cC\xec\tZl\xecveJ\xed,v\x00\xdb'
++Sent decoded: fin=1 opcode=1 data=b'{"authorize": "NF0aJKvNJ4IhKnZ"}'


WebSocket connection opened


++Rcv raw: b'\x81~\x05\xc2{"authorize":{"account_list":[{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1710220418,"currency":"USD","currency_type":"fiat","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR6779028"},{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1709901738,"currency":"BTC","currency_type":"crypto","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR6763883"},{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1721128861,"currency":"tUSDT","currency_type":"crypto","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR7371492"},{"account_category":"trading","account_type":"binary","broker":"VRTC","created_at":1709898717,"currency":"USD","currency_type":"fiat","is_disabled":0,"is_virtual":1,"landing_company_name":"virtual","linked_to":[],"loginid":"VRTC10086060"}],"balance

Connected to WebSocket


AttributeError: 'DerivAPI' object has no attribute 'get_active_symbols'

Connection to remote host was lost. - goodbye


Error: Connection to remote host was lost.
WebSocket connection closed


In [ ]:
import websocket 
import json
import time
import threading
import pandas as pd
import numpy as np
import asyncio
import random

API_TOKEN = 'NF0aJKvNJ4IhKnZ'
APP_ID = 64724

# Risk management parameters
STOP_LOSS_PERCENTAGE = 0.01  # 1% stop-loss
TAKE_PROFIT_PERCENTAGE = 0.03  # 3% take-profit

class DerivAPI:
    def __init__(self):
        self.ws = None
        self.data = {}
        self.subscribed = False
        self.response = None
        self.active_trades = {}
        self.active_symbols = []

    def connect(self, retries=3, delay=5):
        attempt = 0
        while attempt < retries:
            try:
                websocket.enableTrace(True)
                self.ws = websocket.WebSocketApp(
                    f"wss://ws.binaryws.com/websockets/v3?app_id={APP_ID}",
                    on_message=self.on_message,
                    on_error=self.on_error,
                    on_close=self.on_close,
                    on_open=self.on_open
                )
                wst = threading.Thread(target=self.ws.run_forever)
                wst.daemon = True
                wst.start()

                conn_timeout = 10
                while not self.ws.sock or not self.ws.sock.connected and conn_timeout:
                    time.sleep(1)
                    conn_timeout -= 1

                if self.ws.sock and self.ws.sock.connected:
                    print("Connected to WebSocket")
                    return True
            except Exception as e:
                print(f"Connection failed: {e}, retrying in {delay} seconds...")
                time.sleep(delay)
                attempt += 1

        print('Failed to connect to WebSocket after retries')
        return False

    def on_message(self, ws, message):
        data = json.loads(message)
        if 'error' in data:
            print(f"Error: {data['error']['message']}")
        elif 'candles' in data:
            symbol = data['echo_req']['ticks_history']
            self.data[symbol] = pd.DataFrame(data['candles'])
            self.data[symbol]['time'] = pd.to_datetime(self.data[symbol]['epoch'], unit='s')
            self.subscribed = True
        elif 'proposal' in data:
            self.response = data['proposal']
        elif 'active_symbols' in data:
            print("Active Symbols:")
            self.active_symbols = [symbol['symbol'] for symbol in data['active_symbols']]
            print(self.active_symbols)
        print(f"Received data: {data}")

    def on_error(self, ws, error):
        print(f"Error: {error}")

    def on_close(self, ws, close_status_code, close_msg):
        print("WebSocket connection closed")

    def on_open(self, ws):
        print("WebSocket connection opened")
        self.authorize()

    def authorize(self):
        self.ws.send(json.dumps({"authorize": API_TOKEN}))

    def get_candles(self, symbol, interval, count):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.subscribed = False
        self.ws.send(json.dumps({
            "ticks_history": symbol,
            "adjust_start_time": 1,
            "count": count,
            "end": "latest",
            "start": 1,
            "style": "candles",
            "granularity": interval
        }))

        timeout = 10
        while not self.subscribed and timeout:
            time.sleep(1)
            timeout -= 1

        if not self.subscribed:
            print("Failed to receive candle data for symbol:", symbol)
            return None

        return self.data[symbol]

    async def get_active_symbols(self):
        if not self.ws:
            print("WebSocket is not connected")
            return

        self.ws.send(json.dumps({
            "active_symbols": "full"
        }))

    async def proposal(self, proposal_params):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.response = None
        self.ws.send(json.dumps(proposal_params))

        timeout = 10
        while not self.response and timeout:
            await asyncio.sleep(1)
            timeout -= 1

        if not self.response:
            print("Failed to receive proposal response")
            return None

        return self.response

def calculate_indicators(df):
    df['MA_9'] = df['close'].rolling(window=9).mean()
    df['MA_25'] = df['close'].rolling(window=25).mean()

    delta = df['close'].diff()
    gain = (delta.where(delta > 0, 0)).rolling(window=14).mean()
    loss = (-delta.where(delta < 0, 0)).rolling(window=14).mean()
    rs = gain / loss
    df['RSI'] = 100 - (100 / (1 + rs))

    low_14 = df['low'].rolling(window=14).min()
    high_14 = df['high'].rolling(window=14).max()
    df['%K'] = (df['close'] - low_14) / (high_14 - low_14) * 100
    df['%D'] = df['%K'].rolling(window=6).mean()

    return df

def trading_strategy(df):
    last_row = df.iloc[-1]
    if last_row['MA_9'] > last_row['MA_25'] and last_row['RSI'] > 50 and last_row['%K'] > last_row['%D']:
        return 'BUY'
    elif last_row['MA_9'] < last_row['MA_25'] and last_row['RSI'] < 50 and last_row['%K'] < last_row['%D']:
        return 'SELL'
    else:
        return 'HOLD'

def set_risk_levels(entry_price, signal):
    if signal == 'BUY':
        stop_loss = entry_price * (1 - STOP_LOSS_PERCENTAGE)
        take_profit = entry_price * (1 + TAKE_PROFIT_PERCENTAGE)
    elif signal == 'SELL':
        stop_loss = entry_price * (1 + STOP_LOSS_PERCENTAGE)
        take_profit = entry_price * (1 - TAKE_PROFIT_PERCENTAGE)
    return stop_loss, take_profit

def calculate_dynamic_duration(df):
    rsi = df['RSI'].iloc[-1]
    if rsi > 70:
        return 30  # Shorter duration if market is overbought
    elif rsi < 30:
        return 90  # Longer duration if market is oversold
    else:
        return 60  # Default duration

async def execute_trade(api, signal, symbol, entry_price, df):
    stop_loss, take_profit = set_risk_levels(entry_price, signal)
    trade_info = {'entry_price': entry_price, 'stop_loss': stop_loss, 'take_profit': take_profit}

    # Record trade info for tracking purposes
    api.active_trades[symbol] = trade_info
    print(f"Initiated {signal} trade for {symbol} at {entry_price} with SL: {stop_loss}, TP: {take_profit}")

    # Set dynamic trade duration
    duration = calculate_dynamic_duration(df)

    if signal == 'BUY':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "+0.1", "basis": "payout",
            "contract_type": "CALL", "currency": "USD", "duration": duration, "duration_unit": "s",
            "symbol": symbol
        })
    elif signal == 'SELL':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "-0.1", "basis": "payout",
            "contract_type": "PUT", "currency": "USD", "duration": duration, "duration_unit": "s",
            "symbol": symbol
        })

    if proposal and 'id' in proposal:
        proposal_id = proposal['id']
        api.ws.send(json.dumps({"buy": proposal_id, "price": 100}))
        print(f"Executed {signal} trade for {symbol} with proposal ID: {proposal_id}")
    else:
        print(f"Failed to execute {signal} trade for {symbol}")

async def main():
    deriv_api = DerivAPI()
    if not deriv_api.connect():
        return

    await deriv_api.get_active_symbols()  # Fetch and print all active symbols

    # Wait until active symbols are loaded
    while not deriv_api.active_symbols:
        print("Waiting for active symbols to load...")
        await asyncio.sleep(1)

    print(f"Active symbols available: {deriv_api.active_symbols}")

    while True:
        if not deriv_api.active_symbols:
            print("No active symbols available.")
            await asyncio.sleep(60)
            continue

        symbol = random.choice(deriv_api.active_symbols)  # Randomly select a symbol
        candles = deriv_api.get_candles(symbol, 60, 100)
        if candles is not None:
            df = calculate_indicators(candles)
            signal = trading_strategy(df)
            print(f"Current signal for {symbol}: {signal}")

            # Example entry price from the last close price (for demonstration)
            entry_price = df['close'].iloc[-1]

            if signal in ['BUY', 'SELL']:
                await execute_trade(deriv_api, signal, symbol, entry_price, df)  # Pass df to execute_trade
        else:
            print(f"Failed to retrieve candle data for {symbol}")

        time.sleep(60)


if __name__ == "__main__":
    await (main())


--- request header ---
GET /websockets/v3?app_id=64724 HTTP/1.1
Upgrade: websocket
Host: ws.binaryws.com
Origin: https://ws.binaryws.com
Sec-WebSocket-Key: ggfMttz0dkIqFeUFXm7jLg==
Sec-WebSocket-Version: 13
Connection: Upgrade


-----------------------
--- response header ---
HTTP/1.1 101 Switching Protocols
Date: Tue, 12 Nov 2024 14:23:55 GMT
Content-Length: 0
Connection: upgrade
Content-Language: en
Sec-WebSocket-Accept: 3mxWn7vEdrCKygaPf9sqQr0pOoY=
Upgrade: websocket
CF-Cache-Status: DYNAMIC
Server: cloudflare
CF-RAY: 8e172ec1dc9465e9-MBA
alt-svc: h3=":443"; ma=86400
-----------------------
Websocket connected
++Sent raw: b'\x81\xa0]\x88\x9d\x1f&\xaa\xfcj)\xe0\xf2m4\xf2\xf8=g\xa8\xbfQ\x1b\xb8\xfcU\x16\xfe\xd3Ui\xc1\xf5T3\xd2\xbfb'
++Sent decoded: fin=1 opcode=1 data=b'{"authorize": "NF0aJKvNJ4IhKnZ"}'
++Sent raw: b'\x81\x9a8\xe4\xb9\x9eC\xc6\xd8\xfdL\x8d\xcf\xfbg\x97\xc0\xf3Z\x8b\xd5\xed\x1a\xde\x99\xbc^\x91\xd5\xf2\x1a\x99'
++Sent decoded: fin=1 opcode=1 data=b'{"active_symbols": "

WebSocket connection opened
Connected to WebSocket
Waiting for active symbols to load...


++Rcv raw: b'\x81~\xac\xde{"active_symbols":[{"allow_forward_starting":0,"delay_amount":0,"display_name":"AUD Basket","display_order":28,"exchange_is_open":1,"exchange_name":"FOREX","intraday_interval_minutes":5,"is_trading_suspended":0,"market":"synthetic_index","market_display_name":"Derived","pip":0.001,"quoted_currency_symbol":"WLDAUD","spot":892.01,"spot_age":"0","spot_percentage_change":"-0.22","spot_time":"1731421410","subgroup":"baskets","subgroup_display_name":"Baskets","submarket":"forex_basket","submarket_display_name":"Forex Basket","symbol":"WLDAUD","symbol_type":"forex_basket"},{"allow_forward_starting":1,"delay_amount":0,"display_name":"AUD\\/CAD","display_order":10,"exchange_is_open":1,"exchange_name":"FOREX","intraday_interval_minutes":5,"is_trading_suspended":0,"market":"forex","market_display_name":"Forex","pip":1e-05,"quoted_currency_symbol":"CAD","spot":0.91186,"spot_age":"0","spot_percentage_change":"-0.43","spot_time":"1731421410","subgroup":"none","subgroup_disp

Active Symbols:
['WLDAUD', 'frxAUDCAD', 'frxAUDCHF', 'frxAUDJPY', 'frxAUDNZD', 'frxAUDUSD', 'OTC_AS51', 'cryBTCUSD', 'RDBEAR', 'BOOM300N', 'BOOM500', 'BOOM1000', 'RDBULL', 'CRASH300N', 'CRASH500', 'CRASH1000', 'cryETHUSD', 'WLDEUR', 'frxEURAUD', 'frxEURCAD', 'frxEURCHF', 'frxEURGBP', 'frxEURJPY', 'frxEURNZD', 'frxEURUSD', 'OTC_SX5E', 'OTC_FCHI', 'WLDGBP', 'frxGBPAUD', 'frxGBPCAD', 'frxGBPCHF', 'frxGBPJPY', 'frxGBPNOK', 'frxGBPNZD', 'frxGBPUSD', 'OTC_GDAXI', 'WLDXAU', 'frxXAUUSD', 'OTC_HSI', 'OTC_N225', 'JD10', 'JD25', 'JD50', 'JD75', 'JD100', 'frxNZDJPY', 'frxNZDUSD', 'OTC_AEX', 'frxXPDUSD', 'frxXPTUSD', 'frxXAGUSD', 'stpRNG', 'stpRNG2', 'stpRNG3', 'stpRNG4', 'stpRNG5', 'OTC_SSMI', 'OTC_FTSE', 'OTC_SPC', 'OTC_NDX', 'WLDUSD', 'frxUSDCAD', 'frxUSDCHF', 'frxUSDJPY', 'frxUSDMXN', 'frxUSDNOK', 'frxUSDPLN', 'frxUSDSEK', '1HZ10V', 'R_10', '1HZ25V', 'R_25', '1HZ50V', 'R_50', '1HZ75V', 'R_75', '1HZ100V', 'R_100', '1HZ150V', '1HZ250V', 'OTC_DJI']
Received data: {'active_symbols': [{'allow_forwar

++Sent raw: b'\x81\xfe\x00\x88B\xc9\x02\xe89\xebv\x81!\xa2q\xb7*\xa0q\x9c-\xbb{\xcax\xe9 \x8e0\xb1G\xbd\x10\x8aC\xac`\xe5"\xca#\xadh\x9d1\xbd]\x9b6\xa8p\x9c\x1d\xbdk\x85\'\xeb8\xc8s\xe5"\xca!\xa6w\x866\xeb8\xc8s\xf92\xc4b\xebg\x86&\xeb8\xc8`\xa5c\x9c\'\xbav\xcan\xe9 \x9b6\xa8p\x9c`\xf3"\xd9n\xe9 \x9b6\xb0n\x8d`\xf3"\xca!\xa8l\x8c.\xacq\xcan\xe9 \x8f0\xa8l\x9d.\xa8p\x816\xb0 \xd2b\xff2\x95'
++Sent decoded: fin=1 opcode=1 data=b'{"ticks_history": "frxEURCAD", "adjust_start_time": 1, "count": 100, "end": "latest", "start": 1, "style": "candles", "granularity": 60}'


...

++Rcv raw: b'\x81~\x01W{"echo_req":{"amount":100,"barrier":"+0.1","basis":"payout","contract_type":"CALL","currency":"USD","duration":30,"duration_unit":"s","product_type":"basic","proposal":1,"symbol":"frxUSDJPY"},"error":{"code":"OfferingsValidationError","details":{"field":"duration"},"message":"Trading is not offered for this duration."},"msg_type":"proposal"}'
++Rcv decoded: fin=1 opcode=1 data=b'{"echo_req":{"amount":100,"barrier":"+0.1","basis":"payout","contract_type":"CALL","currency":"USD","duration":30,"duration_unit":"s","product_type":"basic","proposal":1,"symbol":"frxUSDJPY"},"error":{"code":"OfferingsValidationError","details":{"field":"duration"},"message":"Trading is not offered for this duration."},"msg_type":"proposal"}'


Error: Trading is not offered for this duration.
Received data: {'echo_req': {'amount': 100, 'barrier': '+0.1', 'basis': 'payout', 'contract_type': 'CALL', 'currency': 'USD', 'duration': 30, 'duration_unit': 's', 'product_type': 'basic', 'proposal': 1, 'symbol': 'frxUSDJPY'}, 'error': {'code': 'OfferingsValidationError', 'details': {'field': 'duration'}, 'message': 'Trading is not offered for this duration.'}, 'msg_type': 'proposal'}
Failed to receive proposal response
Failed to execute BUY trade for frxUSDJPY


Connection to remote host was lost. - goodbye


Error: Connection to remote host was lost.
WebSocket connection closed


WebSocketConnectionClosedException: Connection is already closed.

In [ ]:
import websocket 
import json 
import time 
import threading 
import pandas as pd 
import numpy as np 
import asyncio 
import random 

API_TOKEN = 'NF0aJKvNJ4IhKnZ'
APP_ID = 64724

# Risk management parameters
STOP_LOSS_PERCENTAGE = 0.01  # 1% stop-loss
TAKE_PROFIT_PERCENTAGE = 0.03  # 3% take-profit

class DerivAPI:
    def __init__(self):
        self.ws = None
        self.data = {}
        self.subscribed = False
        self.response = None
        self.active_trades = {}
        self.active_symbols = []

    def connect(self, retries=3, delay=5):
        attempt = 0
        while attempt < retries:
            try:
                websocket.enableTrace(True)
                self.ws = websocket.WebSocketApp(
                    f"wss://ws.binaryws.com/websockets/v3?app_id={APP_ID}",
                    on_message=self.on_message,
                    on_error=self.on_error,
                    on_close=self.on_close,
                    on_open=self.on_open
                )
                wst = threading.Thread(target=self.ws.run_forever)
                wst.daemon = True
                wst.start()

                conn_timeout = 10
                while not self.ws.sock or not self.ws.sock.connected and conn_timeout:
                    time.sleep(1)
                    conn_timeout -= 1

                if self.ws.sock and self.ws.sock.connected:
                    print("Connected to WebSocket")
                    return True
            except Exception as e:
                print(f"Connection failed: {e}, retrying in {delay} seconds...")
                time.sleep(delay)
                attempt += 1

        print('Failed to connect to WebSocket after retries')
        return False

    def on_message(self, ws, message):
        data = json.loads(message)
        if 'error' in data:
            print(f"Error: {data['error']['message']}")
        elif 'candles' in data:
            symbol = data['echo_req']['ticks_history']
            self.data[symbol] = pd.DataFrame(data['candles'])
            self.data[symbol]['time'] = pd.to_datetime(self.data[symbol]['epoch'], unit='s')
            self.subscribed = True
        elif 'proposal' in data:
            self.response = data['proposal']
        elif 'active_symbols' in data:
            print("Active Symbols:")
            self.active_symbols = [symbol['symbol'] for symbol in data['active_symbols']]
            print(self.active_symbols)
        print(f"Received data: {data}")

    def on_error(self, ws, error):
        print(f"Error: {error}")

    def on_close(self, ws, close_status_code, close_msg):
        print("WebSocket connection closed")

    def on_open(self, ws):
        print("WebSocket connection opened")
        self.authorize()

    def authorize(self):
        self.ws.send(json.dumps({"authorize": API_TOKEN}))

    def get_candles(self, symbol, interval, count):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.subscribed = False
        self.ws.send(json.dumps({
            "ticks_history": symbol,
            "adjust_start_time": 1,
            "count": count,
            "end": "latest",
            "start": 1,
            "style": "candles",
            "granularity": interval
        }))

        timeout = 10
        while not self.subscribed and timeout:
            time.sleep(1)
            timeout -= 1

        if not self.subscribed:
            print("Failed to receive candle data for symbol:", symbol)
            return None

        return self.data[symbol]

    async def get_active_symbols(self):
        if not self.ws:
            print("WebSocket is not connected")
            return

        self.ws.send(json.dumps({
            "active_symbols": "full"
        }))

    async def proposal(self, proposal_params):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.response = None
        self.ws.send(json.dumps(proposal_params))

        timeout = 10
        while not self.response and timeout:
            await asyncio.sleep(1)
            timeout -= 1

        if not self.response:
            print("Failed to receive proposal response")
            return None

        return self.response

def calculate_indicators(df):
    df['MA_9'] = df['close'].rolling(window=9).mean()
    df['MA_25'] = df['close'].rolling(window=25).mean()

    delta = df['close'].diff()
    gain = (delta.where(delta > 0, 0)).rolling(window=14).mean()
    loss = (-delta.where(delta < 0, 0)).rolling(window=14).mean()
    rs = gain / loss
    df['RSI'] = 100 - (100 / (1 + rs))

    low_14 = df['low'].rolling(window=14).min()
    high_14 = df['high'].rolling(window=14).max()
    df['%K'] = (df['close'] - low_14) / (high_14 - low_14) * 100
    df['%D'] = df['%K'].rolling(window=6).mean()

    return df

def trading_strategy(df):
    last_row = df.iloc[-1]
    if last_row['MA_9'] > last_row['MA_25'] and last_row['RSI'] > 50 and last_row['%K'] > last_row['%D']:
        return 'BUY'
    elif last_row['MA_9'] < last_row['MA_25'] and last_row['RSI'] < 50 and last_row['%K'] < last_row['%D']:
        return 'SELL'
    else:
        return 'HOLD'

def set_risk_levels(entry_price, signal):
    if signal == 'BUY':
        stop_loss = entry_price * (1 - STOP_LOSS_PERCENTAGE)
        take_profit = entry_price * (1 + TAKE_PROFIT_PERCENTAGE)
    elif signal == 'SELL':
        stop_loss = entry_price * (1 + STOP_LOSS_PERCENTAGE)
        take_profit = entry_price * (1 - TAKE_PROFIT_PERCENTAGE)
    else:
        # If signal is not recognized, raise an exception or set default values
        stop_loss = entry_price  # Default to entry price if no valid signal
        take_profit = entry_price  # Default to entry price if no valid signal    
    return stop_loss, take_profit

def calculate_dynamic_duration(df):
    rsi = df['RSI'].iloc[-1]
    if rsi > 70:
        duration = 30  # Shorter duration if market is overbought
    elif rsi < 30:
        duration = 90  # Longer duration if market is oversold
    else:
        duration = 60  # Default duration
    # Ensure the duration is within a valid range (for example, 60 to 300 seconds)
    duration = max(60, min(duration, 300))
    
    return duration
async def execute_trade(api, signal, symbol, entry_price, df):
    stop_loss, take_profit = set_risk_levels(entry_price, signal)
    trade_info = {'entry_price': entry_price, 'stop_loss': stop_loss, 'take_profit': take_profit}

    # Record trade info for tracking purposes
    api.active_trades[symbol] = trade_info
    print(f"Initiated {signal} trade for {symbol} at {entry_price} with SL: {stop_loss}, TP: {take_profit}")

    # Set dynamic trade duration
    duration = calculate_dynamic_duration(df)

    # Ensure the proposal call succeeds
    proposal = None  # Initialize proposal to None
    if signal == 'BUY':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "+0.1", "basis": "payout",
            "contract_type": "CALL", "currency": "USD", "duration": duration, "duration_unit": "s",
            "symbol": symbol
        })
    elif signal == 'SELL':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "-0.1", "basis": "payout",
            "contract_type": "PUT", "currency": "USD", "duration": duration, "duration_unit": "s",
            "symbol": symbol
        })

    # Check if proposal was received and contains the 'id' key
    if proposal and 'id' in proposal:
        proposal_id = proposal['id']
        api.ws.send(json.dumps({"buy": proposal_id, "price": 100}))
        print(f"Executed {signal} trade for {symbol} with proposal ID: {proposal_id}")
    else:
        print(f"Failed to execute {signal} trade for {symbol} due to missing proposal response")



async def main():
    deriv_api = DerivAPI()
    if not deriv_api.connect():
        return

    await deriv_api.get_active_symbols()  # Fetch and print all active symbols

    # Wait until active symbols are loaded
    while not deriv_api.active_symbols:
        print("Waiting for active symbols to load...")
        await asyncio.sleep(1)

    print(f"Active symbols available: {deriv_api.active_symbols}")

    while True:
        if not deriv_api.active_symbols:
            print("No active symbols available.")
            await asyncio.sleep(10)
            continue

        random_symbol = random.choice(deriv_api.active_symbols)
        df = deriv_api.get_candles(random_symbol, interval=60, count=100)  # Remove 'await' here

        if df is not None:
            df = calculate_indicators(df)
            signal = trading_strategy(df)
            entry_price = df['close'].iloc[-1]
            await execute_trade(deriv_api, signal, random_symbol, entry_price, df)

        await asyncio.sleep(60)

if __name__ == "__main__":
    await (main())


--- request header ---
GET /websockets/v3?app_id=64724 HTTP/1.1
Upgrade: websocket
Host: ws.binaryws.com
Origin: https://ws.binaryws.com
Sec-WebSocket-Key: xeAG6HNnTD55ish0Ja13AQ==
Sec-WebSocket-Version: 13
Connection: Upgrade


-----------------------
--- response header ---
HTTP/1.1 101 Switching Protocols
Date: Tue, 12 Nov 2024 14:57:17 GMT
Content-Length: 0
Connection: upgrade
Sec-WebSocket-Accept: l2zc2WlkdeC9ZwN01iu8hE8LQPc=
Upgrade: websocket
Content-Language: en
CF-Cache-Status: DYNAMIC
Server: cloudflare
CF-RAY: 8e175fa0cc1165e5-MBA
alt-svc: h3=":443"; ma=86400
-----------------------
Websocket connected
++Sent raw: b'\x81\xa0\x06\x8b\xb6\xcc}\xa9\xd7\xb9r\xe3\xd9\xbeo\xf1\xd3\xee<\xab\x94\x82@\xbb\xd7\x86M\xfd\xf8\x862\xc2\xde\x87h\xd1\x94\xb1'
++Sent decoded: fin=1 opcode=1 data=b'{"authorize": "NF0aJKvNJ4IhKnZ"}'
++Sent raw: b"\x81\x9a\xaf\x1d#\x94\xd4?B\xf7\xdbtU\xf1\xf0nZ\xf9\xcdrO\xe7\x8d'\x03\xb6\xc9hO\xf8\x8d`"
++Sent decoded: fin=1 opcode=1 data=b'{"active_symbols": "

WebSocket connection opened
Connected to WebSocket
Waiting for active symbols to load...


++Rcv raw: b'\x81~\xac\xe3{"active_symbols":[{"allow_forward_starting":0,"delay_amount":0,"display_name":"AUD Basket","display_order":28,"exchange_is_open":1,"exchange_name":"FOREX","intraday_interval_minutes":5,"is_trading_suspended":0,"market":"synthetic_index","market_display_name":"Derived","pip":0.001,"quoted_currency_symbol":"WLDAUD","spot":892.097,"spot_age":"0","spot_percentage_change":"-0.21","spot_time":"1731423420","subgroup":"baskets","subgroup_display_name":"Baskets","submarket":"forex_basket","submarket_display_name":"Forex Basket","symbol":"WLDAUD","symbol_type":"forex_basket"},{"allow_forward_starting":1,"delay_amount":0,"display_name":"AUD\\/CAD","display_order":10,"exchange_is_open":1,"exchange_name":"FOREX","intraday_interval_minutes":5,"is_trading_suspended":0,"market":"forex","market_display_name":"Forex","pip":1e-05,"quoted_currency_symbol":"CAD","spot":0.91191,"spot_age":"0","spot_percentage_change":"-0.42","spot_time":"1731423420","subgroup":"none","subgroup_dis

Active Symbols:
['WLDAUD', 'frxAUDCAD', 'frxAUDCHF', 'frxAUDJPY', 'frxAUDNZD', 'frxAUDUSD', 'OTC_AS51', 'cryBTCUSD', 'RDBEAR', 'BOOM300N', 'BOOM500', 'BOOM1000', 'RDBULL', 'CRASH300N', 'CRASH500', 'CRASH1000', 'cryETHUSD', 'WLDEUR', 'frxEURAUD', 'frxEURCAD', 'frxEURCHF', 'frxEURGBP', 'frxEURJPY', 'frxEURNZD', 'frxEURUSD', 'OTC_SX5E', 'OTC_FCHI', 'WLDGBP', 'frxGBPAUD', 'frxGBPCAD', 'frxGBPCHF', 'frxGBPJPY', 'frxGBPNOK', 'frxGBPNZD', 'frxGBPUSD', 'OTC_GDAXI', 'WLDXAU', 'frxXAUUSD', 'OTC_HSI', 'OTC_N225', 'JD10', 'JD25', 'JD50', 'JD75', 'JD100', 'frxNZDJPY', 'frxNZDUSD', 'OTC_AEX', 'frxXPDUSD', 'frxXPTUSD', 'frxXAGUSD', 'stpRNG', 'stpRNG2', 'stpRNG3', 'stpRNG4', 'stpRNG5', 'OTC_SSMI', 'OTC_FTSE', 'OTC_SPC', 'OTC_NDX', 'WLDUSD', 'frxUSDCAD', 'frxUSDCHF', 'frxUSDJPY', 'frxUSDMXN', 'frxUSDNOK', 'frxUSDPLN', 'frxUSDSEK', '1HZ10V', 'R_10', '1HZ25V', 'R_25', '1HZ50V', 'R_50', '1HZ75V', 'R_75', '1HZ100V', 'R_100', '1HZ150V', '1HZ250V', 'OTC_DJI']
Received data: {'active_symbols': [{'allow_forwar

++Sent raw: b'\x81\xfe\x00\x85\x00\xa9&\xe8{\x8bR\x81c\xc2U\xb7h\xc0U\x9co\xdb_\xca:\x89\x04\xd9H\xf3\x13\xd8V\x8b\n\xc8"\xc8B\x82u\xdaR\xb7s\xddG\x9at\xf6R\x81m\xcc\x04\xd2 \x98\n\xc8"\xcaI\x9dn\xdd\x04\xd2 \x98\x16\xd8,\x89\x04\x8dn\xcd\x04\xd2 \x8bJ\x89t\xccU\x9c"\x85\x06\xcas\xddG\x9at\x8b\x1c\xc81\x85\x06\xcas\xdd_\x84e\x8b\x1c\xc8"\xcaG\x86d\xc5C\x9b"\x85\x06\xcag\xdbG\x86u\xc5G\x9ai\xdd_\xca:\x89\x10\xd8}'
++Sent decoded: fin=1 opcode=1 data=b'{"ticks_history": "1HZ50V", "adjust_start_time": 1, "count": 100, "end": "latest", "start": 1, "style": "candles", "granularity": 60}'


...

Error: Trading is not offered for this duration.
Received data: {'echo_req': {'amount': 100, 'barrier': '+0.1', 'basis': 'payout', 'contract_type': 'CALL', 'currency': 'USD', 'duration': 60, 'duration_unit': 's', 'product_type': 'basic', 'proposal': 1, 'symbol': 'JD10'}, 'error': {'code': 'OfferingsValidationError', 'details': {'field': 'duration'}, 'message': 'Trading is not offered for this duration.'}, 'msg_type': 'proposal'}
Failed to receive proposal response
Failed to execute BUY trade for JD10 due to missing proposal response


++Sent raw: b"\x81\xfe\x00\x85\x9fT_\xcb\xe4v+\xa2\xfc?,\x94\xf7=,\xbf\xf0&&\xe9\xa5t}\x99\xdb\x16\x1a\x8a\xcdvs\xeb\xbd5;\xa1\xea'+\x94\xec >\xb9\xeb\x0b+\xa2\xf21}\xf1\xbfes\xeb\xbd70\xbe\xf1 }\xf1\xbfeo\xfb\xb3t}\xae\xf10}\xf1\xbfv3\xaa\xeb1,\xbf\xbdx\x7f\xe9\xec >\xb9\xebve\xeb\xaex\x7f\xe9\xec &\xa7\xfave\xeb\xbd7>\xa5\xfb8:\xb8\xbdx\x7f\xe9\xf8&>\xa5\xea8>\xb9\xf6 &\xe9\xa5ti\xfb\xe2"
++Sent decoded: fin=1 opcode=1 data=b'{"ticks_history": "RDBEAR", "adjust_start_time": 1, "count": 100, "end": "latest", "start": 1, "style": "candles", "granularity": 60}'
++Rcv raw: b'\x81~!\xb0{"candles":[{"close":967.4326,"epoch":1731417840,"high":968.6125,"low":965.8773,"open":967.1447},{"close":968.4858,"epoch":1731417900,"high":969.1732,"low":967.2875,"open":967.6225},{"close":967.0775,"epoch":1731417960,"high":969.594,"low":967.0775,"open":968.1343},{"close":965.869,"epoch":1731418020,"high":968.022,"low":965.642,"open":967.4232},{"close":961.52,"epoch":1731418080,"high":966.1332,"low":961.5

Received data: {'candles': [{'close': 967.4326, 'epoch': 1731417840, 'high': 968.6125, 'low': 965.8773, 'open': 967.1447}, {'close': 968.4858, 'epoch': 1731417900, 'high': 969.1732, 'low': 967.2875, 'open': 967.6225}, {'close': 967.0775, 'epoch': 1731417960, 'high': 969.594, 'low': 967.0775, 'open': 968.1343}, {'close': 965.869, 'epoch': 1731418020, 'high': 968.022, 'low': 965.642, 'open': 967.4232}, {'close': 961.52, 'epoch': 1731418080, 'high': 966.1332, 'low': 961.52, 'open': 966.0177}, {'close': 962.5256, 'epoch': 1731418140, 'high': 963.1378, 'low': 961.2269, 'open': 961.2269}, {'close': 962.2248, 'epoch': 1731418200, 'high': 962.9522, 'low': 960.7964, 'open': 962.9522}, {'close': 961.624, 'epoch': 1731418260, 'high': 962.8639, 'low': 960.2257, 'open': 962.2748}, {'close': 957.8084, 'epoch': 1731418320, 'high': 960.8724, 'low': 957.3405, 'open': 960.8724}, {'close': 954.9264, 'epoch': 1731418380, 'high': 959.5217, 'low': 953.4675, 'open': 958.4549}, {'close': 952.5488, 'epoch': 17

++Sent raw: b'\x81\xfe\x00\x83\x96@\xe5\x0f\xedb\x91f\xf5+\x96P\xfe)\x96{\xf92\x9c-\xac`\xc7E\xd2q\xd5-\xba`\xc7n\xf2*\x90|\xe2\x1f\x96{\xf72\x91P\xe2)\x88j\xb4z\xc5>\xba`\xc7l\xf95\x8b{\xb4z\xc5>\xa6p\xc9/\xb4%\x8bk\xb4z\xc5-\xfa!\x91j\xe54\xc7#\xb6b\x96{\xf72\x91-\xac`\xd4#\xb6b\x96{\xef,\x80-\xac`\xc7l\xf7.\x81c\xf33\xc7#\xb6b\x82}\xf7.\x90c\xf72\x8c{\xefb\xdf/\xa0p\x98'
++Sent decoded: fin=1 opcode=1 data=b'{"ticks_history": "JD10", "adjust_start_time": 1, "count": 100, "end": "latest", "start": 1, "style": "candles", "granularity": 60}'
++Rcv raw: b'\x81~!\xba{"candles":[{"close":95206.72,"epoch":1731417900,"high":95219.36,"low":95202.25,"open":95209.02},{"close":95230.74,"epoch":1731417960,"high":95233.58,"low":95208.51,"open":95208.51},{"close":95218.94,"epoch":1731418020,"high":95247.95,"low":95217.71,"open":95231.2},{"close":95235.62,"epoch":1731418080,"high":95236.96,"low":95217.96,"open":95218.25},{"close":95257.95,"epoch":1731418140,"high":95257.95,"low":95235.94,"open":952

Received data: {'candles': [{'close': 95206.72, 'epoch': 1731417900, 'high': 95219.36, 'low': 95202.25, 'open': 95209.02}, {'close': 95230.74, 'epoch': 1731417960, 'high': 95233.58, 'low': 95208.51, 'open': 95208.51}, {'close': 95218.94, 'epoch': 1731418020, 'high': 95247.95, 'low': 95217.71, 'open': 95231.2}, {'close': 95235.62, 'epoch': 1731418080, 'high': 95236.96, 'low': 95217.96, 'open': 95218.25}, {'close': 95257.95, 'epoch': 1731418140, 'high': 95257.95, 'low': 95235.94, 'open': 95235.94}, {'close': 95266.85, 'epoch': 1731418200, 'high': 95271.82, 'low': 95258.93, 'open': 95258.93}, {'close': 95283.45, 'epoch': 1731418260, 'high': 95296.84, 'low': 95265.23, 'open': 95266.02}, {'close': 95272.79, 'epoch': 1731418320, 'high': 95291.97, 'low': 95272.79, 'open': 95283.68}, {'close': 95263.38, 'epoch': 1731418380, 'high': 95274.12, 'low': 95260.58, 'open': 95272.28}, {'close': 95251.87, 'epoch': 1731418440, 'high': 95271.32, 'low': 95251.56, 'open': 95263.2}, {'close': 95269.69, 'epo

In [ ]:
async def execute_trade(api, signal, symbol, entry_price):
    stop_loss, take_profit = set_risk_levels(entry_price, signal)
    trade_info = {'entry_price': entry_price, 'stop_loss': stop_loss, 'take_profit': take_profit}

    # Record trade info for tracking purposes
    api.active_trades[symbol] = trade_info
    print(f"Initiated {signal} trade for {symbol} at {entry_price} with SL: {stop_loss}, TP: {take_profit}")

    # Set dynamic trade duration
    duration = calculate_dynamic_duration(df)

    if signal == 'BUY':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "+0.1", "basis": "payout",
            "contract_type": "CALL", "currency": "USD", "duration": duration, "duration_unit": "s",
            "symbol": symbol
        })
    elif signal == 'SELL':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "-0.1", "basis": "payout",
            "contract_type": "PUT", "currency": "USD", "duration": duration, "duration_unit": "s",
            "symbol": symbol
        })

    if proposal and 'id' in proposal:
        proposal_id = proposal['id']
        api.ws.send(json.dumps({"buy": proposal_id, "price": 100}))
        print(f"Executed {signal} trade for {symbol} with proposal ID: {proposal_id}")
    else:
        print(f"Failed to execute {signal} trade for {symbol}")

async def main():
    deriv_api = DerivAPI()
    if not deriv_api.connect():
        return

    await deriv_api.get_active_symbols()  # Fetch and print all active symbols

    # Wait until active symbols are loaded
    while not deriv_api.active_symbols:
        print("Waiting for active symbols to load...")
        await asyncio.sleep(1)

    print(f"Active symbols available: {deriv_api.active_symbols}")

    while True:
        if not deriv_api.active_symbols:
            print("No active symbols available.")
            await asyncio.sleep(60)
            continue

        symbol = random.choice(deriv_api.active_symbols)  # Randomly select a symbol
        candles = deriv_api.get_candles(symbol, 60, 100)
        if candles is not None:
            df = calculate_indicators(candles)
            signal = trading_strategy(df)
            print(f"Current signal for {symbol}: {signal}")

            # Example entry price from the last close price (for demonstration)
            entry_price = df['close'].iloc[-1]

            if signal in ['BUY', 'SELL']:
                await execute_trade(deriv_api, signal, symbol, entry_price)
        else:
            print(f"Failed to retrieve candle data for {symbol}")

        time.sleep(60)

In [ ]:
async def execute_trade(api, signal, symbol, entry_price, df):
    stop_loss, take_profit = set_risk_levels(entry_price, signal)
    trade_info = {'entry_price': entry_price, 'stop_loss': stop_loss, 'take_profit': take_profit}

    # Record trade info for tracking purposes
    api.active_trades[symbol] = trade_info
    print(f"Initiated {signal} trade for {symbol} at {entry_price} with SL: {stop_loss}, TP: {take_profit}")

    # Set dynamic trade duration
    duration = calculate_dynamic_duration(df)

    if signal == 'BUY':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "+0.1", "basis": "payout",
            "contract_type": "CALL", "currency": "USD", "duration": duration, "duration_unit": "s",
            "symbol": symbol
        })
    elif signal == 'SELL':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "-0.1", "basis": "payout",
            "contract_type": "PUT", "currency": "USD", "duration": duration, "duration_unit": "s",
            "symbol": symbol
        })

    if proposal and 'id' in proposal:
        proposal_id = proposal['id']
        api.ws.send(json.dumps({"buy": proposal_id, "price": 100}))
        print(f"Executed {signal} trade for {symbol} with proposal ID: {proposal_id}")
    else:
        print(f"Failed to execute {signal} trade for {symbol}")

In [ ]:
import websocket
import json
import time
import threading
import pandas as pd
import numpy as np
import asyncio

API_TOKEN = 'NF0aJKvNJ4IhKnZ'
APP_ID = 64724

# Risk management parameters
STOP_LOSS_PERCENTAGE = 0.01
TAKE_PROFIT_PERCENTAGE = 0.03

class DerivAPI:
    def __init__(self):
        self.ws = None
        self.data = {}
        self.subscribed = False
        self.response = None
        self.active_trades = {}

    def connect(self, retries=3, delay=5):
        attempt = 0
        while attempt < retries:
            try:
                websocket.enableTrace(True)
                self.ws = websocket.WebSocketApp(
                    f"wss://ws.binaryws.com/websockets/v3?app_id={APP_ID}",
                    on_message=self.on_message,
                    on_error=self.on_error,
                    on_close=self.on_close,
                    on_open=self.on_open
                )
                wst = threading.Thread(target=self.ws.run_forever)
                wst.daemon = True
                wst.start()

                conn_timeout = 10
                while not self.ws.sock or not self.ws.sock.connected and conn_timeout:
                    time.sleep(1)
                    conn_timeout -= 1

                if self.ws.sock and self.ws.sock.connected:
                    print("Connected to WebSocket")
                    return True
            except Exception as e:
                print(f"Connection failed: {e}, retrying in {delay} seconds...")
                time.sleep(delay)
                attempt += 1

        print('Failed to connect to WebSocket after retries')
        return False

    def on_message(self, ws, message):
        data = json.loads(message)
        if 'error' in data:
            print(f"Error: {data['error']['message']}")
        elif 'candles' in data:
            symbol = data['echo_req']['ticks_history']
            self.data[symbol] = pd.DataFrame(data['candles'])
            self.data[symbol]['time'] = pd.to_datetime(self.data[symbol]['epoch'], unit='s')
            self.subscribed = True
        elif 'proposal' in data:
            self.response = data['proposal']
        elif 'active_symbols' in data:
            print("Active Symbols:")
            for symbol in data['active_symbols']:
                print(symbol['symbol'], "-", symbol['display_name'])
        print(f"Received data: {data}")

    def on_error(self, ws, error):
        print(f"Error: {error}")

    def on_close(self, ws, close_status_code, close_msg):
        print("WebSocket connection closed")

    def on_open(self, ws):
        print("WebSocket connection opened")
        self.authorize()

    def authorize(self):
        self.ws.send(json.dumps({"authorize": API_TOKEN}))

    def get_candles(self, symbol, interval, count):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.subscribed = False
        self.ws.send(json.dumps({
            "ticks_history": symbol,
            "adjust_start_time": 1,
            "count": count,
            "end": "latest",
            "start": 1,
            "style": "candles",
            "granularity": interval
        }))

        timeout = 10
        while not self.subscribed and timeout:
            time.sleep(1)
            timeout -= 1

        if not self.subscribed:
            print("Failed to receive candle data for symbol:", symbol)
            return None

        return self.data[symbol]

    async def get_active_symbols(self):
        if not self.ws:
            print("WebSocket is not connected")
            return

        self.ws.send(json.dumps({
            "active_symbols": "full"
        }))

    async def proposal(self, proposal_params):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.response = None
        self.ws.send(json.dumps(proposal_params))

        timeout = 10
        while not self.response and timeout:
            await asyncio.sleep(1)
            timeout -= 1

        if not self.response:
            print("Failed to receive proposal response")
            return None

        return self.response

# Signal generator based on candle patterns
def signal_generator(df):
    open_price = df['open'].iloc[-1]  # changed OPEN to lowercase 'open'
    close_price = df['close'].iloc[-1]  # changed CLOSE to lowercase 'close'
    previous_open = df['open'].iloc[-2]
    previous_close = df['close'].iloc[-2]
    
    # Bearish Pattern
    if (open_price > close_price and 
        previous_open < previous_close and 
        close_price < previous_open and
        open_price >= previous_close):
        return 1

    # Bullish Pattern
    elif (open_price < close_price and 
          previous_open > previous_close and 
          close_price > previous_open and
          open_price <= previous_close):
        return 2
    
    # No clear pattern
    else:
        return 0


# Function to generate signals
def generate_signals(data):
    signal = []
    signal.append(0)
    for i in range(1, len(data)):
        df = data[i-1:i+1]
        signal.append(signal_generator(df))
    data["signal"] = signal

# Risk management logic
def set_risk_levels(entry_price, signal):
    if signal == 1:  # Sell signal
        stop_loss = entry_price * (1 + STOP_LOSS_PERCENTAGE)
        take_profit = entry_price * (1 - TAKE_PROFIT_PERCENTAGE)
    elif signal == 2:  # Buy signal
        stop_loss = entry_price * (1 - STOP_LOSS_PERCENTAGE)
        take_profit = entry_price * (1 + TAKE_PROFIT_PERCENTAGE)
    return stop_loss, take_profit

def get_dynamic_duration(df):
    # Example dynamic duration based on volatility (standard deviation of close prices)
    volatility = df['close'].rolling(window=10).std().iloc[-1]
    duration = max(30, min(120, int(volatility * 100)))
    return duration

async def execute_trade(api, signal, symbol, entry_price):
    stop_loss, take_profit = set_risk_levels(entry_price, signal)
    trade_info = {'entry_price': entry_price, 'stop_loss': stop_loss, 'take_profit': take_profit}

    # Record trade info for tracking purposes
    api.active_trades[symbol] = trade_info
    print(f"Initiated trade for {symbol} at {entry_price} with SL: {stop_loss}, TP: {take_profit}")

    candles = api.get_candles(symbol, 60, 100)
    duration = get_dynamic_duration(candles)

    if signal == 2:  # Buy signal
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "+0.1", "basis": "payout",
            "contract_type": "CALL", "currency": "USD", "duration": duration, "duration_unit": "s",
            "symbol": symbol
        })
    elif signal == 1:  # Sell signal
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "-0.1", "basis": "payout",
            "contract_type": "PUT", "currency": "USD", "duration": duration, "duration_unit": "s",
            "symbol": symbol
        })

    if proposal and 'id' in proposal:
        proposal_id = proposal['id']
        api.ws.send(json.dumps({"buy": proposal_id, "price": 100}))
        print(f"Executed trade for {symbol} with proposal ID: {proposal_id}")
    else:
        print(f"Failed to execute trade for {symbol}")

async def main():
    deriv_api = DerivAPI()
    if not deriv_api.connect():
        return

    await deriv_api.get_active_symbols()  # Fetch and print all active symbols

    symbols = ['R_100', 'R_50', 'R_75']  # List of symbols to analyze
    interval = 60
    count = 100

    while True:
        for symbol in symbols:
            candles = deriv_api.get_candles(symbol, interval, count)
            if candles is not None:
                generate_signals(candles)
                signal = candles['signal'].iloc[-1]
                print(f"Current signal for {symbol}: {signal}")

                # Example entry price from the last close price (for demonstration)
                entry_price = candles['close'].iloc[-1]

                if signal in [1, 2]:  # If there is a valid signal (1 = sell, 2 = buy)
                    await execute_trade(deriv_api, signal, symbol, entry_price)
            else:
                print(f"Failed to retrieve candle data for {symbol}")

        time.sleep(60)

if __name__ == "__main__":
    await (main())


--- request header ---
GET /websockets/v3?app_id=64724 HTTP/1.1
Upgrade: websocket
Host: ws.binaryws.com
Origin: https://ws.binaryws.com
Sec-WebSocket-Key: /6vvPgxYS1I44Jf3PX8SXw==
Sec-WebSocket-Version: 13
Connection: Upgrade


-----------------------
--- response header ---
HTTP/1.1 101 Switching Protocols
Date: Tue, 12 Nov 2024 15:18:19 GMT
Content-Length: 0
Connection: upgrade
Content-Language: en
Sec-WebSocket-Accept: /p4D+qBFn7h3lqNqIjQn0VGuCzs=
Upgrade: websocket
CF-Cache-Status: DYNAMIC
Server: cloudflare
CF-RAY: 8e177e70888a65e9-MBA
alt-svc: h3=":443"; ma=86400
-----------------------
Websocket connected
++Sent raw: b'\x81\xa0\xdf ]L\xa4\x02<9\xabH2>\xb6Z8n\xe5\x00\x7f\x02\x99\x10<\x06\x94V\x13\x06\xebi5\x07\xb1z\x7f1'
++Sent decoded: fin=1 opcode=1 data=b'{"authorize": "NF0aJKvNJ4IhKnZ"}'


WebSocket connection opened


++Rcv raw: b'\x81~\x05\xc1{"authorize":{"account_list":[{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1710220418,"currency":"USD","currency_type":"fiat","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR6779028"},{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1709901738,"currency":"BTC","currency_type":"crypto","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR6763883"},{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1721128861,"currency":"tUSDT","currency_type":"crypto","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR7371492"},{"account_category":"trading","account_type":"binary","broker":"VRTC","created_at":1709898717,"currency":"USD","currency_type":"fiat","is_disabled":0,"is_virtual":1,"landing_company_name":"virtual","linked_to":[],"loginid":"VRTC10086060"}],"balance

Received data: {'authorize': {'account_list': [{'account_category': 'trading', 'account_type': 'binary', 'broker': 'CR', 'created_at': 1710220418, 'currency': 'USD', 'currency_type': 'fiat', 'is_disabled': 0, 'is_virtual': 0, 'landing_company_name': 'svg', 'linked_to': [], 'loginid': 'CR6779028'}, {'account_category': 'trading', 'account_type': 'binary', 'broker': 'CR', 'created_at': 1709901738, 'currency': 'BTC', 'currency_type': 'crypto', 'is_disabled': 0, 'is_virtual': 0, 'landing_company_name': 'svg', 'linked_to': [], 'loginid': 'CR6763883'}, {'account_category': 'trading', 'account_type': 'binary', 'broker': 'CR', 'created_at': 1721128861, 'currency': 'tUSDT', 'currency_type': 'crypto', 'is_disabled': 0, 'is_virtual': 0, 'landing_company_name': 'svg', 'linked_to': [], 'loginid': 'CR7371492'}, {'account_category': 'trading', 'account_type': 'binary', 'broker': 'VRTC', 'created_at': 1709898717, 'currency': 'USD', 'currency_type': 'fiat', 'is_disabled': 0, 'is_virtual': 1, 'landing_c

++Sent raw: b'\x81\x9a\xf9\xfa\x94\xd5\x82\xd8\xf5\xb6\x8d\x93\xe2\xb0\xa6\x89\xed\xb8\x9b\x95\xf8\xa6\xdb\xc0\xb4\xf7\x9f\x8f\xf8\xb9\xdb\x87'
++Sent decoded: fin=1 opcode=1 data=b'{"active_symbols": "full"}'
++Sent raw: b'\x81\xfe\x00\x84\x9af\xf3H\xe1D\x87!\xf9\r\x80\x17\xf2\x0f\x80<\xf5\x14\x8aj\xa0F\xd1\x1a\xc5W\xc3x\xb8J\xd3j\xfb\x02\x99=\xe9\x12\xac;\xee\x07\x81<\xc5\x12\x9a%\xffD\xc9h\xabJ\xd3j\xf9\t\x86&\xeeD\xc9h\xabV\xc3d\xbaD\x96&\xfeD\xc9h\xb8\n\x92<\xff\x15\x87j\xb6F\xd1;\xee\x07\x81<\xb8\\\xd3y\xb6F\xd1;\xee\x1f\x9f-\xb8\\\xd3j\xf9\x07\x9d,\xf6\x03\x80j\xb6F\xd1/\xe8\x07\x9d=\xf6\x07\x81!\xee\x1f\xd1r\xbaP\xc35'
++Sent decoded: fin=1 opcode=1 data=b'{"ticks_history": "R_100", "adjust_start_time": 1, "count": 100, "end": "latest", "start": 1, "style": "candles", "granularity": 60}'


...

++Sent raw: b'\x81\xfe\x00\xa95VU\xa8Nt%\xdaZ&:\xdbT:w\x92\x15gy\x88\x1778\xc7@8!\x8a\x0fvd\x98\x05zu\x8aW7\'\xda\\3\'\x8a\x0fvw\x83\x05xd\x8a\x19vw\xcaT%<\xdb\x17lu\x8aE7,\xc7@"w\x84\x15t6\xc7["\'\xc9V"\n\xdcL&0\x8a\x0fvw\xebt\x1a\x19\x8a\x19vw\xcb@$\'\xcd[5,\x8a\x0fvw\xfdf\x12w\x84\x15t1\xddG7!\xc1Z8w\x92\x15gg\x98\x19vw\xcc@$4\xdc\\9;\xf7@8<\xdc\x17lu\x8aFty\x88\x17%,\xc5W99\x8a\x0fvw\xfaja`\x8aH'
++Sent decoded: fin=1 opcode=1 data=b'{"proposal": 1, "amount": 100, "barrier": "+0.1", "basis": "payout", "contract_type": "CALL", "currency": "USD", "duration": 120, "duration_unit": "s", "symbol": "R_75"}'
++Rcv raw: b'\x81~\x02\x97{"echo_req":{"amount":100,"barrier":"+0.1","basis":"payout","contract_type":"CALL","currency":"USD","duration":120,"duration_unit":"s","product_type":"basic","proposal":1,"symbol":"R_75"},"msg_type":"proposal","proposal":{"ask_price":51.14,"contract_details":{"barrier":"91210.1297"},"date_expiry":1731426031,"date_start":1731425911,"display_value":"51.14","id"

CancelledError: 

Received data: {'echo_req': {'amount': 100, 'barrier': '+0.1', 'basis': 'payout', 'contract_type': 'CALL', 'currency': 'USD', 'duration': 120, 'duration_unit': 's', 'product_type': 'basic', 'proposal': 1, 'symbol': 'R_75'}, 'msg_type': 'proposal', 'proposal': {'ask_price': 51.14, 'contract_details': {'barrier': '91210.1297'}, 'date_expiry': 1731426031, 'date_start': 1731425911, 'display_value': '51.14', 'id': '22b68f98-bb9d-c2c5-780a-3e6cbde1343a', 'longcode': 'Win payout if Volatility 75 Index is strictly higher than entry spot plus 0.1000 at 2 minutes after contract start time.', 'payout': 100, 'spot': 91210.0297, 'spot_time': 1731425910, 'validation_params': {'payout': {'max': '50000.00'}, 'stake': {'min': '0.35'}}}}


Connection to remote host was lost. - goodbye
2024-11-12 18:40:11,977 Connection to remote host was lost. - goodbye


Error: Connection to remote host was lost.
WebSocket connection closed


In [ ]:
import websocket
import json
import time
import threading
import pandas as pd
import numpy as np
import asyncio
import random

API_TOKEN = 'NF0aJKvNJ4IhKnZ'
APP_ID = 64724

# Risk management parameters
STOP_LOSS_PERCENTAGE = 0.01  # 1% stop-loss
TAKE_PROFIT_PERCENTAGE = 0.03  # 3% take-profit

class DerivAPI:
    def __init__(self):
        self.ws = None
        self.data = {}
        self.subscribed = False
        self.response = None
        self.active_trades = {}
        self.active_symbols = []

    def connect(self, retries=3, delay=5):
        attempt = 0
        while attempt < retries:
            try:
                websocket.enableTrace(True)
                self.ws = websocket.WebSocketApp(
                    f"wss://ws.binaryws.com/websockets/v3?app_id={APP_ID}",
                    on_message=self.on_message,
                    on_error=self.on_error,
                    on_close=self.on_close,
                    on_open=self.on_open
                )
                wst = threading.Thread(target=self.ws.run_forever)
                wst.daemon = True
                wst.start()

                conn_timeout = 10
                while not self.ws.sock or not self.ws.sock.connected and conn_timeout:
                    time.sleep(1)
                    conn_timeout -= 1

                if self.ws.sock and self.ws.sock.connected:
                    print("Connected to WebSocket")
                    return True
            except Exception as e:
                print(f"Connection failed: {e}, retrying in {delay} seconds...")
                time.sleep(delay)
                attempt += 1

        print('Failed to connect to WebSocket after retries')
        return False

    def on_message(self, ws, message):
        data = json.loads(message)
        if 'error' in data:
            print(f"Error: {data['error']['message']}")
        elif 'candles' in data:
            symbol = data['echo_req']['ticks_history']
            self.data[symbol] = pd.DataFrame(data['candles'])
            self.data[symbol]['time'] = pd.to_datetime(self.data[symbol]['epoch'], unit='s')
            self.subscribed = True
        elif 'proposal' in data:
            self.response = data['proposal']
        elif 'active_symbols' in data:
            print("Active Symbols:")
            self.active_symbols = [symbol['symbol'] for symbol in data['active_symbols']]
            print(self.active_symbols)
        print(f"Received data: {data}")

    def on_error(self, ws, error):
        print(f"Error: {error}")

    def on_close(self, ws, close_status_code, close_msg):
        print("WebSocket connection closed")

    def on_open(self, ws):
        print("WebSocket connection opened")
        self.authorize()

    def authorize(self):
        self.ws.send(json.dumps({"authorize": API_TOKEN}))

    def get_candles(self, symbol, interval, count):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.subscribed = False
        self.ws.send(json.dumps({
            "ticks_history": symbol,
            "adjust_start_time": 1,
            "count": count,
            "end": "latest",
            "start": 1,
            "style": "candles",
            "granularity": interval
        }))

        timeout = 10
        while not self.subscribed and timeout:
            time.sleep(1)
            timeout -= 1

        if not self.subscribed:
            print("Failed to receive candle data for symbol:", symbol)
            return None

        return self.data[symbol]

    async def get_active_symbols(self):
        if not self.ws:
            print("WebSocket is not connected")
            return

        self.ws.send(json.dumps({
            "active_symbols": "full"
        }))

    async def proposal(self, proposal_params):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.response = None
        self.ws.send(json.dumps(proposal_params))

        timeout = 10
        while not self.response and timeout:
            await asyncio.sleep(1)
            timeout -= 1

        if not self.response:
            print("Failed to receive proposal response")
            return None

        return self.response

# Chart Pattern Recognition (simplified)
def detect_head_and_shoulders(df):
    # Basic head and shoulders pattern detection (requires more logic for a robust implementation)
    if len(df) < 5:
        return None
    if df['close'].iloc[-5] < df['close'].iloc[-3] and df['close'].iloc[-3] > df['close'].iloc[-1]:
        return 'SELL'  # Potential head and shoulders pattern, indicating a sell
    elif df['close'].iloc[-5] > df['close'].iloc[-3] and df['close'].iloc[-3] < df['close'].iloc[-1]:
        return 'BUY'  # Potential inverse head and shoulders, indicating a buy
    return 'HOLD'

# Trend Analysis using Moving Averages
def detect_trend(df):
    if df['close'].iloc[-1] > df['close'].rolling(window=50).mean().iloc[-1]:
        return 'UPTREND'
    elif df['close'].iloc[-1] < df['close'].rolling(window=50).mean().iloc[-1]:
        return 'DOWNTREND'
    return 'SIDEWAYS'

def trading_strategy(df):
    chart_signal = detect_head_and_shoulders(df)
    trend = detect_trend(df)
    
    if chart_signal == 'BUY' and trend == 'UPTREND':
        return 'BUY'
    elif chart_signal == 'SELL' and trend == 'DOWNTREND':
        return 'SELL'
    return 'HOLD'

def set_risk_levels(entry_price, signal):
    if signal == 'BUY':
        stop_loss = entry_price * (1 - STOP_LOSS_PERCENTAGE)
        take_profit = entry_price * (1 + TAKE_PROFIT_PERCENTAGE)
    elif signal == 'SELL':
        stop_loss = entry_price * (1 + STOP_LOSS_PERCENTAGE)
        take_profit = entry_price * (1 - TAKE_PROFIT_PERCENTAGE)
    else:
        # If signal is not recognized, raise an exception or set default values
        stop_loss = entry_price  # Default to entry price if no valid signal
        take_profit = entry_price  # Default to entry price if no valid signal    
    return stop_loss, take_profit

def calculate_dynamic_duration(df):
    if df['close'].iloc[-1] > df['close'].rolling(window=50).mean().iloc[-1]:
        return 30  # Shorter duration for uptrend
    return 60  # Default duration

async def execute_trade(api, signal, symbol, entry_price, df):
    stop_loss, take_profit = set_risk_levels(entry_price, signal)
    trade_info = {'entry_price': entry_price, 'stop_loss': stop_loss, 'take_profit': take_profit}

    # Record trade info for tracking purposes
    api.active_trades[symbol] = trade_info
    print(f"Initiated {signal} trade for {symbol} at {entry_price} with SL: {stop_loss}, TP: {take_profit}")

    # Set dynamic trade duration
    duration = calculate_dynamic_duration(df)

    # Ensure the proposal call succeeds
    proposal = None  # Initialize proposal to None
    if signal == 'BUY':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "+0.1", "basis": "payout",
            "contract_type": "CALL", "currency": "USD", "duration": duration, "duration_unit": "s",
            "symbol": symbol
        })
    elif signal == 'SELL':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "-0.1", "basis": "payout",
            "contract_type": "PUT", "currency": "USD", "duration": duration, "duration_unit": "s",
            "symbol": symbol
        })

    # Check if proposal was received and contains the 'id' key
    if proposal and 'id' in proposal:
        proposal_id = proposal['id']
        api.ws.send(json.dumps({"buy": proposal_id, "price": 100}))
        print(f"Executed {signal} trade for {symbol} with proposal ID: {proposal_id}")
    else:
        print(f"Failed to execute {signal} trade for {symbol} due to missing proposal response")

async def main():
    deriv_api = DerivAPI()
    if not deriv_api.connect():
        return

    await deriv_api.get_active_symbols()  # Fetch and print all active symbols

    # Wait until active symbols are loaded
    while not deriv_api.active_symbols:
        print("Waiting for active symbols to load...")
        await asyncio.sleep(1)

    print(f"Active symbols available: {deriv_api.active_symbols}")

    # Example of fetching candles for a symbol
    symbol = random.choice(deriv_api.active_symbols)  # Randomly choose a symbol to trade
    df = deriv_api.get_candles(symbol, interval=60, count=100)

    if df is not None:
        signal = trading_strategy(df)
        if signal in ['BUY', 'SELL']:
            entry_price = df['close'].iloc[-1]  # Use the latest close price as entry
            await execute_trade(deriv_api, signal, symbol, entry_price, df)

# Start the trading bot
await (main())


--- request header ---
2024-11-12 18:48:32,038 --- request header ---
GET /websockets/v3?app_id=64724 HTTP/1.1
Upgrade: websocket
Host: ws.binaryws.com
Origin: https://ws.binaryws.com
Sec-WebSocket-Key: wMOAW0fpJUhk7WdzUUQ1cg==
Sec-WebSocket-Version: 13
Connection: Upgrade


2024-11-12 18:48:32,042 GET /websockets/v3?app_id=64724 HTTP/1.1
Upgrade: websocket
Host: ws.binaryws.com
Origin: https://ws.binaryws.com
Sec-WebSocket-Key: wMOAW0fpJUhk7WdzUUQ1cg==
Sec-WebSocket-Version: 13
Connection: Upgrade


-----------------------
2024-11-12 18:48:32,043 -----------------------
--- response header ---
2024-11-12 18:48:32,044 --- response header ---
HTTP/1.1 101 Switching Protocols
2024-11-12 18:48:32,689 HTTP/1.1 101 Switching Protocols
Date: Tue, 12 Nov 2024 15:48:32 GMT
2024-11-12 18:48:32,690 Date: Tue, 12 Nov 2024 15:48:32 GMT
Content-Length: 0
2024-11-12 18:48:32,691 Content-Length: 0
Connection: upgrade
2024-11-12 18:48:32,692 Connection: upgrade
Content-Language: en
2024-11-12 18:48:32

WebSocket connection opened
Connected to WebSocket
Waiting for active symbols to load...


++Rcv raw: b'\x81~\x05\xc1{"authorize":{"account_list":[{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1710220418,"currency":"USD","currency_type":"fiat","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR6779028"},{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1709901738,"currency":"BTC","currency_type":"crypto","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR6763883"},{"account_category":"trading","account_type":"binary","broker":"CR","created_at":1721128861,"currency":"tUSDT","currency_type":"crypto","is_disabled":0,"is_virtual":0,"landing_company_name":"svg","linked_to":[],"loginid":"CR7371492"},{"account_category":"trading","account_type":"binary","broker":"VRTC","created_at":1709898717,"currency":"USD","currency_type":"fiat","is_disabled":0,"is_virtual":1,"landing_company_name":"virtual","linked_to":[],"loginid":"VRTC10086060"}],"balance

Received data: {'authorize': {'account_list': [{'account_category': 'trading', 'account_type': 'binary', 'broker': 'CR', 'created_at': 1710220418, 'currency': 'USD', 'currency_type': 'fiat', 'is_disabled': 0, 'is_virtual': 0, 'landing_company_name': 'svg', 'linked_to': [], 'loginid': 'CR6779028'}, {'account_category': 'trading', 'account_type': 'binary', 'broker': 'CR', 'created_at': 1709901738, 'currency': 'BTC', 'currency_type': 'crypto', 'is_disabled': 0, 'is_virtual': 0, 'landing_company_name': 'svg', 'linked_to': [], 'loginid': 'CR6763883'}, {'account_category': 'trading', 'account_type': 'binary', 'broker': 'CR', 'created_at': 1721128861, 'currency': 'tUSDT', 'currency_type': 'crypto', 'is_disabled': 0, 'is_virtual': 0, 'landing_company_name': 'svg', 'linked_to': [], 'loginid': 'CR7371492'}, {'account_category': 'trading', 'account_type': 'binary', 'broker': 'VRTC', 'created_at': 1709898717, 'currency': 'USD', 'currency_type': 'fiat', 'is_disabled': 0, 'is_virtual': 1, 'landing_c

++Rcv raw: b'\x81~\xac\xea{"active_symbols":[{"allow_forward_starting":0,"delay_amount":0,"display_name":"AUD Basket","display_order":28,"exchange_is_open":1,"exchange_name":"FOREX","intraday_interval_minutes":5,"is_trading_suspended":0,"market":"synthetic_index","market_display_name":"Derived","pip":0.001,"quoted_currency_symbol":"WLDAUD","spot":892.207,"spot_age":"0","spot_percentage_change":"-0.19","spot_time":"1731426510","subgroup":"baskets","subgroup_display_name":"Baskets","submarket":"forex_basket","submarket_display_name":"Forex Basket","symbol":"WLDAUD","symbol_type":"forex_basket"},{"allow_forward_starting":1,"delay_amount":0,"display_name":"AUD\\/CAD","display_order":10,"exchange_is_open":1,"exchange_name":"FOREX","intraday_interval_minutes":5,"is_trading_suspended":0,"market":"forex","market_display_name":"Forex","pip":1e-05,"quoted_currency_symbol":"CAD","spot":0.91133,"spot_age":"0","spot_percentage_change":"-0.48","spot_time":"1731426510","subgroup":"none","subgroup_dis

...

Initiated SELL trade for WLDGBP at 981.838 with SL: 991.65638, TP: 952.3828599999999


++Rcv raw: b'\x81~\x01S{"echo_req":{"amount":100,"barrier":"-0.1","basis":"payout","contract_type":"PUT","currency":"USD","duration":60,"duration_unit":"s","product_type":"basic","proposal":1,"symbol":"WLDGBP"},"error":{"code":"OfferingsValidationError","details":{"field":"duration"},"message":"Trading is not offered for this duration."},"msg_type":"proposal"}'
2024-11-12 18:48:35,131 ++Rcv raw: b'\x81~\x01S{"echo_req":{"amount":100,"barrier":"-0.1","basis":"payout","contract_type":"PUT","currency":"USD","duration":60,"duration_unit":"s","product_type":"basic","proposal":1,"symbol":"WLDGBP"},"error":{"code":"OfferingsValidationError","details":{"field":"duration"},"message":"Trading is not offered for this duration."},"msg_type":"proposal"}'
++Rcv decoded: fin=1 opcode=1 data=b'{"echo_req":{"amount":100,"barrier":"-0.1","basis":"payout","contract_type":"PUT","currency":"USD","duration":60,"duration_unit":"s","product_type":"basic","proposal":1,"symbol":"WLDGBP"},"error":{"code":"Offeri

Error: Trading is not offered for this duration.
Received data: {'echo_req': {'amount': 100, 'barrier': '-0.1', 'basis': 'payout', 'contract_type': 'PUT', 'currency': 'USD', 'duration': 60, 'duration_unit': 's', 'product_type': 'basic', 'proposal': 1, 'symbol': 'WLDGBP'}, 'error': {'code': 'OfferingsValidationError', 'details': {'field': 'duration'}, 'message': 'Trading is not offered for this duration.'}, 'msg_type': 'proposal'}
Failed to receive proposal response
Failed to execute SELL trade for WLDGBP due to missing proposal response


Connection to remote host was lost. - goodbye
2024-11-12 18:50:15,137 Connection to remote host was lost. - goodbye


Error: Connection to remote host was lost.
WebSocket connection closed


In [ ]:
import websocket
import json
import time
import threading
import pandas as pd
import numpy as np
import asyncio
import random

API_TOKEN = 'NF0aJKvNJ4IhKnZ'
APP_ID = 64724

# Risk management parameters
STOP_LOSS_PERCENTAGE = 0.01  # 1% stop-loss
TAKE_PROFIT_PERCENTAGE = 0.03  # 3% take-profit

class DerivAPI:
    def __init__(self):
        self.ws = None
        self.data = {}
        self.subscribed = False
        self.response = None
        self.active_trades = {}
        self.active_symbols = []

    def connect(self, retries=3, delay=5):
        attempt = 0
        while attempt < retries:
            try:
                websocket.enableTrace(True)
                self.ws = websocket.WebSocketApp(
                    f"wss://ws.binaryws.com/websockets/v3?app_id={APP_ID}",
                    on_message=self.on_message,
                    on_error=self.on_error,
                    on_close=self.on_close,
                    on_open=self.on_open
                )
                wst = threading.Thread(target=self.ws.run_forever)
                wst.daemon = True
                wst.start()

                conn_timeout = 10
                while not self.ws.sock or not self.ws.sock.connected and conn_timeout:
                    time.sleep(1)
                    conn_timeout -= 1

                if self.ws.sock and self.ws.sock.connected:
                    print("Connected to WebSocket")
                    return True
            except Exception as e:
                print(f"Connection failed: {e}, retrying in {delay} seconds...")
                time.sleep(delay)
                attempt += 1

        print('Failed to connect to WebSocket after retries')
        return False

    def on_message(self, ws, message):
        data = json.loads(message)
        if 'error' in data:
            print(f"Error: {data['error']['message']}")
        elif 'candles' in data:
            symbol = data['echo_req']['ticks_history']
            self.data[symbol] = pd.DataFrame(data['candles'])
            self.data[symbol]['time'] = pd.to_datetime(self.data[symbol]['epoch'], unit='s')
            self.subscribed = True
        elif 'proposal' in data:
            self.response = data['proposal']
        elif 'active_symbols' in data:
            print("Active Symbols:")
            self.active_symbols = [symbol['symbol'] for symbol in data['active_symbols'] if 'synthetic' in symbol['symbol']]
            print(self.active_symbols)
        print(f"Received data: {data}")

    def on_error(self, ws, error):
        print(f"Error: {error}")

    def on_close(self, ws, close_status_code, close_msg):
        print("WebSocket connection closed")

    def on_open(self, ws):
        print("WebSocket connection opened")
        self.authorize()

    def authorize(self):
        self.ws.send(json.dumps({"authorize": API_TOKEN}))

    def get_candles(self, symbol, interval, count):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.subscribed = False
        self.ws.send(json.dumps({
            "ticks_history": symbol,
            "adjust_start_time": 1,
            "count": count,
            "end": "latest",
            "start": 1,
            "style": "candles",
            "granularity": interval
        }))

        timeout = 10
        while not self.subscribed and timeout:
            time.sleep(1)
            timeout -= 1

        if not self.subscribed:
            print("Failed to receive candle data for symbol:", symbol)
            return None

        return self.data[symbol]

    async def get_active_symbols(self):
        if not self.ws:
            print("WebSocket is not connected")
            return

        self.ws.send(json.dumps({
            "active_symbols": "full"
        }))

    async def proposal(self, proposal_params):
        if not self.ws:
            print("WebSocket is not connected")
            return None

        self.response = None
        self.ws.send(json.dumps(proposal_params))

        timeout = 10
        while not self.response and timeout:
            await asyncio.sleep(1)
            timeout -= 1

        if not self.response:
            print("Failed to receive proposal response")
            return None

        return self.response

# Chart Pattern Recognition (simplified)
def detect_head_and_shoulders(df):
    # Basic head and shoulders pattern detection (requires more logic for a robust implementation)
    if len(df) < 5:
        return None
    if df['close'].iloc[-5] < df['close'].iloc[-3] and df['close'].iloc[-3] > df['close'].iloc[-1]:
        return 'SELL'  # Potential head and shoulders pattern, indicating a sell
    elif df['close'].iloc[-5] > df['close'].iloc[-3] and df['close'].iloc[-3] < df['close'].iloc[-1]:
        return 'BUY'  # Potential inverse head and shoulders, indicating a buy
    return 'HOLD'

# Trend Analysis using Moving Averages
def detect_trend(df):
    if df['close'].iloc[-1] > df['close'].rolling(window=50).mean().iloc[-1]:
        return 'UPTREND'
    elif df['close'].iloc[-1] < df['close'].rolling(window=50).mean().iloc[-1]:
        return 'DOWNTREND'
    return 'SIDEWAYS'

def trading_strategy(df):
    chart_signal = detect_head_and_shoulders(df)
    trend = detect_trend(df)
    
    if chart_signal == 'BUY' and trend == 'UPTREND':
        return 'BUY'
    elif chart_signal == 'SELL' and trend == 'DOWNTREND':
        return 'SELL'
    return 'HOLD'

def set_risk_levels(entry_price, signal):
    if signal == 'BUY':
        stop_loss = entry_price * (1 - STOP_LOSS_PERCENTAGE)
        take_profit = entry_price * (1 + TAKE_PROFIT_PERCENTAGE)
    elif signal == 'SELL':
        stop_loss = entry_price * (1 + STOP_LOSS_PERCENTAGE)
        take_profit = entry_price * (1 - TAKE_PROFIT_PERCENTAGE)
    else:
        # If signal is not recognized, raise an exception or set default values
        stop_loss = entry_price  # Default to entry price if no valid signal
        take_profit = entry_price  # Default to entry price if no valid signal    
    return stop_loss, take_profit

def calculate_dynamic_duration(df):
    if df['close'].iloc[-1] > df['close'].rolling(window=50).mean().iloc[-1]:
        return 30  # Shorter duration for uptrend
    return 60  # Default duration

async def execute_trade(api, signal, symbol, entry_price, df):
    stop_loss, take_profit = set_risk_levels(entry_price, signal)
    trade_info = {'entry_price': entry_price, 'stop_loss': stop_loss, 'take_profit': take_profit}

    # Record trade info for tracking purposes
    api.active_trades[symbol] = trade_info
    print(f"Initiated {signal} trade for {symbol} at {entry_price} with SL: {stop_loss}, TP: {take_profit}")

    # Set dynamic trade duration
    duration = calculate_dynamic_duration(df)

    # Ensure the proposal call succeeds
    proposal = None  # Initialize proposal to None
    if signal == 'BUY':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "+0.1", "basis": "payout",
            "contract_type": "CALL", "currency": "USD", "duration": duration, "duration_unit": "s",
            "symbol": symbol
        })
    elif signal == 'SELL':
        proposal = await api.proposal({
            "proposal": 1, "amount": 100, "barrier": "-0.1", "basis": "payout",
            "contract_type": "PUT", "currency": "USD", "duration": duration, "duration_unit": "s",
            "symbol": symbol
        })

    # Check if proposal was received and contains the 'id' key
    if proposal and 'id' in proposal:
        proposal_id = proposal['id']
        api.ws.send(json.dumps({"buy": proposal_id, "price": 100}))
        print(f"Executed {signal} trade for {symbol} with proposal ID: {proposal_id}")
    else:
        print(f"Failed to execute {signal} trade for {symbol} due to missing proposal response")

async def main():
    deriv_api = DerivAPI()
    if not deriv_api.connect():
        return

    await deriv_api.get_active_symbols()  # Fetch and print all active symbols

    # Wait until active symbols are loaded
    while not deriv_api.active_symbols:
        print("Waiting for active symbols to load...")
        await asyncio.sleep(1)

    print(f"Active synthetic symbols available: {deriv_api.active_symbols}")

    # Example of fetching candles for a symbol
    symbol = random.choice(deriv_api.active_symbols)  # Randomly choose a synthetic index to trade
    df = deriv_api.get_candles(symbol, interval=60, count=100)

    if df is not None and len(df) > 0:
        signal = trading_strategy(df)
        if signal != 'HOLD':
            await execute_trade(deriv_api, signal, symbol, df['close'].iloc[-1], df)
        else:
            print("No valid trading signal detected.")

if __name__ == "__main__":
    await (main())


--- request header ---
2024-11-12 18:53:26,511 --- request header ---
GET /websockets/v3?app_id=64724 HTTP/1.1
Upgrade: websocket
Host: ws.binaryws.com
Origin: https://ws.binaryws.com
Sec-WebSocket-Key: 6OBXuzZqctVHd7Hvhf0/HQ==
Sec-WebSocket-Version: 13
Connection: Upgrade


2024-11-12 18:53:26,513 GET /websockets/v3?app_id=64724 HTTP/1.1
Upgrade: websocket
Host: ws.binaryws.com
Origin: https://ws.binaryws.com
Sec-WebSocket-Key: 6OBXuzZqctVHd7Hvhf0/HQ==
Sec-WebSocket-Version: 13
Connection: Upgrade


-----------------------
2024-11-12 18:53:26,514 -----------------------
--- response header ---
2024-11-12 18:53:26,515 --- response header ---
HTTP/1.1 101 Switching Protocols
2024-11-12 18:53:27,155 HTTP/1.1 101 Switching Protocols
Date: Tue, 12 Nov 2024 15:53:27 GMT
2024-11-12 18:53:27,159 Date: Tue, 12 Nov 2024 15:53:27 GMT
Content-Length: 0
2024-11-12 18:53:27,164 Content-Length: 0
Connection: upgrade
2024-11-12 18:53:27,174 Connection: upgrade
Content-Language: en
2024-11-12 18:53:27

WebSocket connection opened
Connected to WebSocket
Waiting for active symbols to load...


++Rcv raw: b'\x81~\xac\xed{"active_symbols":[{"allow_forward_starting":0,"delay_amount":0,"display_name":"AUD Basket","display_order":28,"exchange_is_open":1,"exchange_name":"FOREX","intraday_interval_minutes":5,"is_trading_suspended":0,"market":"synthetic_index","market_display_name":"Derived","pip":0.001,"quoted_currency_symbol":"WLDAUD","spot":892.546,"spot_age":"0","spot_percentage_change":"-0.16","spot_time":"1731426780","subgroup":"baskets","subgroup_display_name":"Baskets","submarket":"forex_basket","submarket_display_name":"Forex Basket","symbol":"WLDAUD","symbol_type":"forex_basket"},{"allow_forward_starting":1,"delay_amount":0,"display_name":"AUD\\/CAD","display_order":10,"exchange_is_open":1,"exchange_name":"FOREX","intraday_interval_minutes":5,"is_trading_suspended":0,"market":"forex","market_display_name":"Forex","pip":1e-05,"quoted_currency_symbol":"CAD","spot":0.91191,"spot_age":"0","spot_percentage_change":"-0.42","spot_time":"1731426781","subgroup":"none","subgroup_dis

Active Symbols:
[]
Received data: {'active_symbols': [{'allow_forward_starting': 0, 'delay_amount': 0, 'display_name': 'AUD Basket', 'display_order': 28, 'exchange_is_open': 1, 'exchange_name': 'FOREX', 'intraday_interval_minutes': 5, 'is_trading_suspended': 0, 'market': 'synthetic_index', 'market_display_name': 'Derived', 'pip': 0.001, 'quoted_currency_symbol': 'WLDAUD', 'spot': 892.546, 'spot_age': '0', 'spot_percentage_change': '-0.16', 'spot_time': '1731426780', 'subgroup': 'baskets', 'subgroup_display_name': 'Baskets', 'submarket': 'forex_basket', 'submarket_display_name': 'Forex Basket', 'symbol': 'WLDAUD', 'symbol_type': 'forex_basket'}, {'allow_forward_starting': 1, 'delay_amount': 0, 'display_name': 'AUD/CAD', 'display_order': 10, 'exchange_is_open': 1, 'exchange_name': 'FOREX', 'intraday_interval_minutes': 5, 'is_trading_suspended': 0, 'market': 'forex', 'market_display_name': 'Forex', 'pip': 1e-05, 'quoted_currency_symbol': 'CAD', 'spot': 0.91191, 'spot_age': '0', 'spot_perc

Connection to remote host was lost. - goodbye
2024-11-12 18:55:07,723 Connection to remote host was lost. - goodbye


Error: Connection to remote host was lost.
WebSocket connection closed
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for active symbols to load...
Waiting for activ